# AP21
Updated May 2022
M. Shmakova


In [1]:
import numpy as np
from numpy import *

Starting Spark application


FloatProgress(value=0.0, bar_style='info', description='Progress:', layout=Layout(height='25px', width='50%'),…

SparkSession available as 'spark'.


FloatProgress(value=0.0, bar_style='info', description='Progress:', layout=Layout(height='25px', width='50%'),…

In [2]:
import boto3
# import boto
import sys 
from sys import *

import io
import json 
from json import *

from glob import glob

import os
# os.getcwd()
# sorted(os.listdir())

FloatProgress(value=0.0, bar_style='info', description='Progress:', layout=Layout(height='25px', width='50%'),…

In [3]:
from pyspark.sql import functions as F

# pyspark functions 
from pyspark.sql import Row
from pyspark.sql.window import Window
from pyspark.sql.types import StructType , StructField , StringType, IntegerType, LongType, BooleanType, TimestampType
from pyspark.sql.types import DoubleType, FloatType, ArrayType, MapType 
from pyspark.sql.functions import when, lit, create_map, desc
from pyspark.sql.functions import input_file_name
from pyspark.sql.functions import json_tuple, from_json, get_json_object
from pyspark.sql.functions import col, upper ,initcap, explode_outer
from pyspark.sql.functions import udf, size, avg, count, sum, explode
from pyspark.sql.functions import expr, collect_list, collect_set
from pyspark.sql.functions import to_timestamp, percentile_approx 

from pyspark.ml.feature import StringIndexer

from functools import reduce
from operator import add


FloatProgress(value=0.0, bar_style='info', description='Progress:', layout=Layout(height='25px', width='50%'),…

In [4]:
import pandas as pd
from pandas import DataFrame, read_csv, Series
pd.set_option('display.width', 1000)
pd.set_option('display.expand_frame_repr', False)
pd.set_option("display.max_columns", None)

FloatProgress(value=0.0, bar_style='info', description='Progress:', layout=Layout(height='25px', width='50%'),…

# LOAD DATA SCRIPT

In [5]:
sle_schema = StructType([
    StructField("ap_mac",StringType(),True),
    StructField("band",StringType(),True),
    StructField("classifier",StringType(),True),
    StructField("classifier_rank",LongType(),True),
    StructField("client_os",StringType(),True),
    StructField("client_type",StringType(),True),
    StructField("client_wcid",StringType(),True),
    StructField("duration",LongType(),True),
    StructField("en_client_sle_agg",LongType(),True),
    StructField("ex_wl",LongType(),True),
    StructField("metric",StringType(),True),
    StructField("metric_rank",LongType(),True),
    StructField("value",StringType(),True),
    StructField("org_id",StringType(),True),
    StructField("prev_ap_mac",StringType(),True),
    StructField("prev_band",StringType(),True),
    StructField("prev_rssi",LongType(),True),
    StructField("rssi",LongType(),True),   
    StructField("site_id",StringType(),True),
    StructField("time",LongType(),True),
    StructField("wlan_id",StringType(),True),
    StructField("best_roam_candidate_24",StringType(),True),
    StructField("best_roam_candidate_24_rssi",LongType(),True),
    StructField("best_roam_candidate_5",StringType(),True),
    StructField("best_roam_candidate_5_rssi",LongType(),True)])

FloatProgress(value=0.0, bar_style='info', description='Progress:', layout=Layout(height='25px', width='50%'),…

In [6]:
# READ DATA 

path_r =  'roaming_events_stats_site'                  # all roaming events by site
path_s =  'roaming_sticky_client_stats_site'           # signal-sticky-clients events per site
path_ap = 'roaming_sticky_client_stats_site_ap2_band'  # signal-sticky-clients events per site/ap2/band
path_c =  'roaming_sticky_client_stats_site_clients'   # signal-sticky-clients events per site/client
path_b =  'roaming_events_stats_bayesian_v2'

def get_roaming_agg_data(path_type, date, hour,  env, sites=[]):
    """
    
    """    
    bucket = "s3://mist-aggregated-stats-{env}/aggregated-stats/".format(env=env) 
    bucket =  bucket + path
    if hour:
        folder = bucket + "dt=%s/hr=%s*/*.parquet"%(date, hour)
    else: 
        folder = bucket + "dt=%s/*/*.parquet"%(date)
    print(folder)    
    df = spark.read.parquet(folder)  
    if sites:
        df = df.where(F.col('site_id').isin(sites))
    df = df.withColumn("timestamp", F.to_timestamp(df['stats_agg_time']))
    return df

path_s = "roaming_anomaly_candidate/"
path_c =  "client_roaming_anomaly_candidate/"

def get_events_candidate_data(date, hour,  env, sites=[]):
    
    bucket = "s3://mist-aggregated-stats-{env}/aggregated-stats/".format(env=env) 
    bucket =  bucket + "roaming_anomaly_candidate/"
    if hour:
        folder = bucket + "dt=%s/hr=%s*/*.csv"%(date, hour)
    else: 
        folder = bucket + "dt=%s/*/*.csv"%(date)
    print(folder)    
    df = spark.read.csv(folder) 
    if sites:
        df = df.where(F.col('site_id').isin(sites))
    df = df.withColumn("timestamp", F.to_timestamp(df['stats_agg_time']))
    return df

def get_roaming_sle_data(date, hour, env, sites =[]):
    """
    
    """    
    bucket = "s3://mist-secorapp-{env}/".format(env=env)
    path =  "cv-sle-roaming-multipartition-v2/"
    path = path + "cv-sle-roaming-multipartition-v2-{env}/".format(env=env)
    bucket =  bucket + path
    
    
    if hour:
        folder = bucket + "dt=%s/hr=%s/*.seq"%(date, hour)
    else: 
        folder = bucket + "dt=%s/hr=*/*.seq"%(date)
    print(folder)    
    data_rdd = spark.sparkContext.sequenceFile(folder).map(lambda r: json.loads(r[1]))
    df = spark.createDataFrame(data_rdd, sle_schema)
    if sites:
        df = df.where(F.col('site_id').isin(sites))
    df = df.withColumn("timestamp",F.to_timestamp((F.col('time')/1000).cast(LongType()))).persist()
    return df

def get_client_stats(date, hour, env, sites =[]):
    bucket = 's3://mist-secorapp-{env}/client-stats-analytics/'.format(env=env)
    bucket =  bucket + 'client-stats-analytics-{env}/'.format(env=env)
    bucket = bucket + 'dt={dt}/hr={hr}/*.parquet'.format(dt=date, hr=hour)

    print(bucket)
    df = spark.read.parquet(bucket)
    if sites:
        df = df.where(F.col('site_id').isin(sites))
    df = df.withColumn("timestamp", F.to_timestamp((F.col("terminator_timestamp")/1000000).cast(LongType()))).persist()   
    return df

def get_cov_data(date, env, sites=[]):
    """
    
    """    
    bucket = "s3://mist-secorapp-{env}/".format(env=env)
    path = "cv-sle-cov-multipartition/"
    path = path + "cv-sle-cov-multipartition-{env}/".format(env=env)
    folder = bucket + path + "dt={}/*".format(date)
    print(folder)    
    df = spark.read.format('orc').load(folder)
    if sites:
        df = df.where(F.col("site_id").isin(sites))
    df = df.withColumn("timestamp", F.to_timestamp(df['time']))
    return df

def get_cap_data(date, env, sites=[]):
    """
    
    """    
    bucket = "s3://mist-secorapp-{env}/".format(env=env)
    path = "cv-sle-cap-multipartition/"
    path = path + "cv-sle-cap-multipartition-{env}/".format(env=env)
    folder = bucket + path + "dt={}/*".format(date)
    print(folder)    
    df = spark.read.format('orc').load(folder)
    if sites:
        df = df.where(F.col("site_id").isin(sites))
    df = df.withColumn("timestamp", F.to_timestamp(df['time']))
    return df

def get_ap_health_data(date, env, sites=[]):
    """
    
    """    
    bucket = "s3://mist-secorapp-{env}/".format(env=env)
    path = "cv-sle-ap-health/"
    path = path + "cv-sle-ap-health-{env}/".format(env=env)
    folder = bucket + path + "dt={}/*".format(date)
    print(folder)    
    df = spark.read.format('orc').load(folder)   
    if sites:
        df = df.where(F.col("site_id").isin(sites))
    df = df.withColumn("timestamp", F.to_timestamp(df['time']))
    return df

def get_ttc_data(date, env, sites=[]):
    """
    
    """    
    bucket = "s3://mist-secorapp-{env}/".format(env=env)
    path = "cv-sle-preconnection-ttc/"
    path = path + "cv-sle-preconnection-ttc-{env}/".format(env=env)
    folder = bucket + path + "dt={}/*".format(date)
    print(folder)    
    df = spark.read.format('orc').load(folder)
    if sites:
        df = df.where(F.col("site_id").isin(sites))
    df = df.withColumn("timestamp", F.to_timestamp(df['time']))
    return df

def get_ftc_data(date, env, sites=[]):
    """
    
    """    
    bucket = "s3://mist-secorapp-{env}/".format(env=env)
    path = "cv-sle-preconnection-ftc/"
    path = path + "cv-sle-preconnection-ftc-{env}/".format(env=env)
    folder = bucket + path + "dt={}/*".format(date)
    print(folder)    
    df = spark.read.format('orc').load(folder)
    if sites:
        df = df.where(F.col("site_id").isin(sites))
    df = df.withColumn("timestamp", F.to_timestamp(df['time']))
    return df

def get_sticky_client_events_only(dt, hr, env, sites=[]):
    s3_gs_bucket = 's3://mist-secorapp-{env}/sticky-client/sticky-client-production-{env}'.format(env=env)
    s3_gs_bucket += '/dt={dt}/hr={hr}/*.seq'.format(dt=dt, hr=hr)
    print(s3_gs_bucket)
    data_rdd = sc.sequenceFile(s3_gs_bucket).map(lambda x: json.loads(x[1]))
    df_sticky = data_rdd.filter(lambda x: x['event_type'] == 'sticky-client') \
                        .map(lambda x: x.get("source"))\
                        .filter(lambda x: x.get("Sticky")==True)\
                        .toDF()
    keys = ['OrgID', 'SiteID', 'WLAN', 'AP', 'BSSID', 'AvgRSSI', 'Band', 'SSID']
    exprs = ['WC', 'When'] + [F.col('Assoc').getItem(k).alias(k) for k in keys] 
    df_sticky = df_sticky.select(*exprs)       
    if sites:
        df_sticky = df_sticky.where(F.col('SiteID').isin(sites))    
    return df_sticky

def get_sticky_client_event_old(dt, hr, env, sites=[]):
    s3_gs_bucket = 's3://mist-secorapp-{env}/client-events/client-events-{env}'.format(env=env)
    s3_gs_bucket += '/dt={dt}/hr={hr}/*.seq'.format(dt=dt, hr=hr)
    print(s3_gs_bucket)
    data_rdd = sc.sequenceFile(s3_gs_bucket).map(lambda x: json.loads(x[1]))
    df_sticky = data_rdd.filter(lambda x: x['event_type'] == 'sticky-client') \
                        .map(lambda x: x.get("source"))\
                        .filter(lambda x: x.get("Sticky")==True)\
                        .toDF()
    keys = ['OrgID', 'SiteID', 'WLAN', 'AP', 'BSSID', 'AvgRSSI', 'Band', 'SSID']
    exprs = ['WC', 'When', 'RoamCandidates'] + [F.col('Assoc').getItem(k).alias(k) for k in keys] 
    df_sticky = df_sticky.select(*exprs)       
    if sites:
        df_sticky = df_sticky.where(F.col('SiteID').isin(sites))    
    return df_sticky

from pyspark.sql.functions import monotonically_increasing_id

def get_sticky_client_event(dt, hr, env, sites=[]):
    s3_gs_bucket = 's3://mist-secorapp-{env}/client-events/client-events-{env}'.format(env=env)
    s3_gs_bucket += '/dt={dt}/hr={hr}/*.seq'.format(dt=dt, hr=hr)
    print(s3_gs_bucket)
    data_rdd = sc.sequenceFile(s3_gs_bucket).map(lambda x: json.loads(x[1]))
    df = data_rdd.filter(lambda x: x['event_type'] == 'sticky-client') \
                 .filter(lambda x: x['sticky'] == True).toDF()
    cols = [c for c in df.columns if c != 'source']
    df = df.select(cols)
    df_sticky = data_rdd.filter(lambda x: x['event_type'] == 'sticky-client') \
                        .filter(lambda x: x['sticky'] == True)\
                        .map(lambda x: x.get("source"))\
                        .toDF()
    df = df.withColumn("id", F.monotonically_increasing_id())
    keys = ['OrgID', 'SiteID', 'WLAN', 'AP', 'BSSID', 'AvgRSSI', 'Band', 'SSID']    
    exprs = ['WC', 'When', 'RoamCandidates'] + [F.col('Assoc').getItem(k).alias(k) for k in keys] 
    df_sticky = df_sticky.select(*exprs)
    df_sticky = df_sticky.withColumn("id", F.monotonically_increasing_id())
    df_out = df.join(df_sticky, "id")
    if sites:
        df_out = df_out.where(F.col('SiteID').isin(sites))  
    return df_out


# new working version

def extract_cs(data):
    op = data["source"]
    for f in fields:
        op[f] = data[f]
    return op

def get_sticky_client_event_tt2a(dt, hr, env, sites=[]):
    
    s3_gs_bucket = 's3://mist-secorapp-{env}/client-events/client-events-{env}'.format(env=env)
    s3_gs_bucket += '/dt={dt}/hr={hr}/*.seq'.format(dt=date, hr=hour)

    fields = ["event_type","source","wc_id"]
    def extract_cs(data):
        op = data["source"]
        for f in fields:
            op[f] = data[f]
        return op
  
    data = sc.sequenceFile(s3_gs_bucket).map(lambda r: json.loads(r[1])) \
                                        .filter(lambda x: x['event_type'] == 'sticky-client')\
                                        .map(lambda x: extract_cs(x))\
                                        .filter(lambda x: x["Sticky"]==True)
    df_ce = spark.createDataFrame(data)
    df_out = df_ce.withColumn("RoamCandidates",F.explode("RoamCandidates")).select("Assoc.OrgID","Assoc.SiteID","Assoc.AP","Assoc.AvgRSSI","Assoc.Band","WC","wc_id",\
                "RoamCandidates","When")
    if sites:     
        df_out = df_out.where(F.col('SiteID').isin(sites)) 
        
    return df_out

def get_sticky_client_event_tt2(dt, hr, env, sites=[]):
    
    s3_gs_bucket = 's3://mist-secorapp-{env}/client-events/client-events-{env}'.format(env=env)
    s3_gs_bucket += '/dt={dt}/hr={hr}/*.seq'.format(dt=date, hr=hour)

    fields = ["event_type","source","wc_id", 'timestamp']
    def extract_cs(data):
        op = data["source"]
        for f in fields:
            op[f] = data[f]
        return op
  
    data = sc.sequenceFile(s3_gs_bucket).map(lambda r: json.loads(r[1])) \
                                        .filter(lambda x: x['event_type'] == 'sticky-client')\
                                        .map(lambda x: extract_cs(x))\
                                        .filter(lambda x: x["Sticky"]==True)
    df_ce = spark.createDataFrame(data)
    """    
    df_out = df_ce.withColumn("RoamCandidates",F.explode("RoamCandidates")).select("Assoc.OrgID",
                                                                                   "Assoc.SiteID",
                                                                                   "Assoc.AP",
                                                                                   "Assoc.AvgRSSI",
                                                                                   "Assoc.Band",
                                                                                   "WC",
                                                                                   "wc_id",
                                                                                   "RoamCandidates",
                                                                                   'timestamp',
                                                                                   "When")"""
    df_out = df_ce.select("Assoc.OrgID",
                       "Assoc.SiteID",
                       "Assoc.AP",
                       "Assoc.AvgRSSI",
                       "Assoc.Band",
                       "WC",
                       "wc_id",
                       "RoamCandidates",
                       'timestamp',
                       "When")
    if sites:     
        df_out = df_out.where(F.col('SiteID').isin(sites)) 
        
    return df_out

FloatProgress(value=0.0, bar_style='info', description='Progress:', layout=Layout(height='25px', width='50%'),…

In [7]:
def fetch_sticky_roaming_event(dt, hr, env):
    s3_gs_bucket = 's3://mist-secorapp-{env}/cv-sle-roaming-multipartition-v2/cv-sle-roaming-multipartition-v2-{env}'.format(env=env)
    s3_gs_bucket += '/dt={dt}/hr={hr}/*.seq'.format(dt=dt, hr=hr)
    print(s3_gs_bucket)
    df_roam = sc.sequenceFile(s3_gs_bucket).map(lambda x: json.loads(x[1])).toDF()
    return df_roam

def fetch_sticky_client_event(dt, hr, env,sites=[]):
    s3_gs_bucket = 's3://mist-secorapp-{env}/sticky-client/sticky-client-production-{env}'.format(env=env)
    s3_gs_bucket += '/dt={dt}/hr={hr}/*.seq'.format(dt=dt, hr=hr)
    print(s3_gs_bucket)
    data_rdd = sc.sequenceFile(s3_gs_bucket).map(lambda x: json.loads(x[1])).toDF()
    df = spark.createDataFrame(data_rdd)
    if sites:
        df = df.where(F.col('SiteID').isin(sites))
    df = df.withColumn("timestamp",F.to_timestamp((F.col('time')/1000).cast(LongType()))).persist()
    return df

FloatProgress(value=0.0, bar_style='info', description='Progress:', layout=Layout(height='25px', width='50%'),…

# CLASS for aggregation 

In [8]:

DEC = 4
DEC_PRE = 2
class AggregationWinUtils():
    """
    COLLECTION OF AGGREGATION FUNCTIONS FOR WINDOW AGGREGATION
    CURRENT LIST: sum; count; countDistinct; mean; std; quantile

    """

    def __init__(self):
        """
        Class containing utils for aggregation based on window functions.
        This method allows to keep origunal data if needed and add aggregations on multiple levels
        """
        super(AggregationWinUtils, self).__init__()

    def get_sum(self, df, entity_cols, count_col, output_col, filter_in=""):
        """
        Count total number of roaming events for entity aggregation assuming a column with number of events for sum
        :param df:  data frame
        :param entity_cols:  list of aggregation entity example: ['org_id', 'site_id', 'ap_mac']
        :param count_col:  columns with number of events (numeric long)
        :param output_col:  output column
        :param filter_in:  Filtering condition if required
        :return: df with added column
        """
        win = Window.partitionBy(entity_cols)
        if filter_in:
            df = df.withColumn("temp", F.when(eval(filter_in), F.col(count_col)).otherwise(0))
            df = df.withColumn("temp_out", sum(F.col("temp")).over(win))
            df = df.drop(*["temp"])
        else:
            df = df.withColumn("temp_out", sum(F.col(count_col)).over(win))
        win1 = Window.partitionBy(entity_cols).orderBy(F.col("temp_out").desc())
        df = df.withColumn(output_col, F.first(df["temp_out"]).over(win1))
        df = df.drop(*["temp_out"])
        return df

    def get_counts(self, df, entity_cols, count_col, output_col, filter_in=""):
        """
        Count total number of roaming events for entity aggregation
        :param df:  data frame
        :param entity_cols:  list of aggregation entity example: ['org_id', 'site_id', 'ap_mac']
        :param count_col:  column for counting could be numaric or categorical string for count aggregation
        :param output_col:  output column
        :param filter_in:  Filtering condition if required
        :return: df with added column
        """
        win = Window.partitionBy(entity_cols)
        if filter_in:
            df = df.withColumn("temp", F.when(eval(filter_in), F.col(count_col)).otherwise(None))
            df = df.withColumn("temp_out", count(F.col("temp")).over(win))
            df = df.drop(*["temp"])
        else:
            df = df.withColumn("temp_out", count(F.col(count_col)).over(win))
        win1 = Window.partitionBy(entity_cols).orderBy(F.col("temp_out").desc())
        df = df.withColumn(output_col, F.first(df["temp_out"]).over(win1))
        df = df.drop(*["temp_out"])
        return df

    def get_distinct_counts(self, df, entity_cols, count_col, output_col, filter_in=""):
        """
        Count distinct clients or AP
        :param df:  data frame
        :param entity_cols:  list of aggregation entity example: ['org_id', 'site_id', 'ap_mac']
        :param count_col:  columns with number of events
        :param output_col:  output column
        :param filter_in:  Filtering condition if required example: "F.col('count_roaming')!=0"
        :return: df with added column
        """
        win = Window.partitionBy(entity_cols)
        if filter_in:
            df = df.withColumn("temp", F.when(eval(filter_in), F.col(count_col)).otherwise(None))
            df = df.withColumn(output_col, F.approx_count_distinct(F.col("temp"), 0.01).over(win))
            df = df.drop(*["temp"])
        else:
            df = df.withColumn(output_col, F.approx_count_distinct(F.col(count_col), 0.01).over(win))
        return df

    def get_quantile(self, df, entity_cols, data_col, output_col, quantile=0.5):
        """
         Calculate quantiles Default quantiles are set for median.
        :param df:  data frame
        :param entity_cols:  list of aggregation entity example: ['org_id', 'site_id', 'ap_mac']
        :param data_col:  columns to estimate quantiles
        :param output_col:  output column
        :param quantile:  required quantile: 0.5 or 0.75 default set to median 0.5
        :return: df with added column
        """
        win = Window.partitionBy(entity_cols).orderBy(F.col(data_col))
        df = df.withColumn("temp_rank", F.percent_rank().over(win))
        win2 = Window.partitionBy(entity_cols).orderBy(pow(df.temp_rank - quantile, 2))
        df = df.withColumn(output_col, F.round(F.first(data_col).over(win2), DEC_PRE))
        df = df.drop(*["temp_rank"])
        return df

    def get_mean(self, df, entity_cols, count_col, output_col, filter_in=""):
        """
        Calculate mean
        :param df:  data frame
        :param entity_cols:  list of aggregation entity example: ['org_id', 'site_id', 'ap_mac']
        :param count_col:  columns to estimate quantiles
        :param output_col:  output column name for mean
        :param filter_in:  Filtering condition if required example: "F.col('count_roaming')!=0"
        :return: df with added columns
        """
        if filter_in:
            df = df.withColumn("temp", F.when(eval(filter_in), F.col(count_col)).otherwise(None))
            win = Window.partitionBy(entity_cols).orderBy(F.col(count_col))
            df = df.withColumn("temp_out", F.avg(F.col("temp")).over(win))
            df = df.drop(*["temp"])
        else:
            win = Window.partitionBy(entity_cols).orderBy(F.col(count_col))
            df = df.withColumn("temp_out", F.avg(F.col(count_col)).over(win))
        win2 = Window.partitionBy(entity_cols).orderBy(F.col(count_col).desc())
        df = df.withColumn(output_col, F.round(F.first("temp_out").over(win2), DEC_PRE))
        df = df.drop(*["temp_out"])
        return df

    def get_stddev_t(self, df, entity_cols, count_col, output_col, filter_in=""):
        """
        Calculate standard deviation
        :param df:  data frame
        :param entity_cols:  list of aggregation entity example: ['org_id', 'site_id', 'ap_mac']
        :param count_col:  columns to estimate quantiles
        :param output_col:  output column name for mean
        :param filter_in:  Filtering condition if required example: "F.col('count_roaming')!=0"
        :return: df with added columns
        """
        if filter_in:
            df = df.withColumn("temp", F.when(eval(filter_in), F.col(count_col)).otherwise(None))
            win = Window.partitionBy(entity_cols).orderBy(F.col(count_col))
            df = df.withColumn("temp_out", F.stddev(F.col("temp")).over(win))
            df = df.drop(*["temp"])
        else:
            win = Window.partitionBy(entity_cols).orderBy(F.col(count_col))
            df = df.withColumn("temp_out", F.stddev(F.col(count_col)).over(win))
        df = df.fillna(0, subset=["temp_out"])
        win2 = Window.partitionBy(entity_cols).orderBy(F.col(count_col).desc())
        df = df.withColumn(output_col, F.round(F.first("temp_out").over(win2), DEC_PRE))
        df = df.drop(*["temp_out"])
        return df

    def get_stddev(self, df, entity_cols, count_col, output_col, filter_in=""):
        """
        Calculate mean and standard deviation
        :param df:  data frame
        :param entity_cols:  list of aggregation entity example: ['org_id', 'site_id', 'ap_mac']
        :param count_col:  columns to estimate quantiles
        :param output_col:  output column name for mean
        :param filter_in:  Filtering condition if required example: "F.col('count_roaming')!=0"
        :return: df with added columns
        """

        df = self.get_mean(df, entity_cols, count_col, 'mean_' + output_col, filter_in)
        df = self.get_counts(df, entity_cols, count_col, 'temp_count', filter_in)
        df = df.withColumn("temp_std", F.pow(F.col(count_col) - F.col('mean_' + output_col), 2))
        df = self.get_sum(df, entity_cols, "temp_std", 'temp_std_sum', filter_in)
        df = df.withColumn("std_" + output_col, F.when(F.col('temp_count') > 1,
                                                       F.round(F.col('temp_std_sum') / (F.col('temp_count') - 1),
                                                               DEC_PRE)
                                                       ).otherwise(0))
        df = df.drop(*['temp_count', "temp_std", 'temp_std_sum', 'mean_' + output_col])
        return df

    def get_stats(self, df, entity_cols, count_col, output_col, filter_in=""):
        """
        Calculate mean and standard deviation
        :param df:  data frame
        :param entity_cols:  list of aggregation entity example: ['org_id', 'site_id', 'ap_mac']
        :param count_col:  columns to estimate quantiles
        :param output_col:  output column name for mean
        :param filter_in:  Filtering condition if required example: "F.col('count_roaming')!=0"
        :return: df with added columns
        """

        df = self.get_mean(df, entity_cols, count_col, 'mean_'+output_col, filter_in)
        df = self.get_counts(df, entity_cols, count_col, 'temp_count', filter_in)
        df = df.withColumn("temp_std", F.pow(F.col(count_col) - F.col('mean_'+ output_col),2))
        df = self.get_sum(df, entity_cols, "temp_std", 'temp_std_sum', filter_in)
        df = df.withColumn("std_" + output_col, F.when(F.col('temp_count')>1,
                                                       F.round(F.col('temp_std_sum')/(F.col('temp_count')-1),
                                                               DEC_PRE)
                                                       ).otherwise(0))
        df = df.drop(*['temp_count', "temp_std", 'temp_std_sum'])
        return df

    def get_shape_param(self, df,
                        mean_col,
                        std_col,
                        q1_col,
                        q2_col,
                        q3_col,
                        output_range,
                        output_skew,
                        k=1.5):
        """
        Calculate upper range = Q3 + k*(Q3 -Q1) k = 1.5 and skewness in a data = (Mean - Median)/std
        :param df:  data frame
        :param mean_col:  column name for mean
        :param std_col:  column name for std
        :param q1_col:  column name for Q1
        :param q2_col:  column name for Q2 (median)
        :param q3_col: column name for Q3
        :param output_range: output column for range
        :param output_skew: output column for skewness
        :param k: parameter to calculate range
        :return: df with added columns
        """
        df = df.withColumn(output_range, F.col(q3_col) + k * (F.col(q3_col) - F.col(q1_col)))
        df = df.withColumn(output_range, F.when(F.col(output_range) < 1, F.col(output_range)).otherwise(1))
        df = df.withColumn(output_skew, F.when(F.col(std_col) != 0,
                                               (F.col(mean_col) - F.col(q2_col)) / F.col(std_col)
                                               ).otherwise(0))
        return df

    def get_top_contributor(self, df, entity_cols, contributor, count_col, output_col, filter_in=""):
        """
        Count total number of roaming events for entity aggregation
        :param df:  data frame
        :param entity_cols:  list of aggregation entity example: ['org_id', 'site_id', 'ap_mac']
        :param contributor: entity column to find highest contributing feture
        :param count_col:  column for counting could be numaric or categorical string for count aggregation
        :param output_col:  output column
        :param filter_in:  Filtering condition if required
        :return: df with added column
        """
        if type(contributor) == list:
            win = Window.partitionBy(entity_cols + contributor)
        else:
            win = Window.partitionBy(entity_cols + [contributor])

        if filter_in:
            df = df.withColumn("temp", F.when(eval(filter_in), F.col(count_col)).otherwise(None))
            df = df.withColumn("temp_out", count(F.col("temp")).over(win))
            df = df.drop(*["temp"])
        else:
            df = df.withColumn("temp_out", count(F.col(count_col)).over(win))

        # get best contributor based on counts
        win2 = Window.partitionBy(entity_cols).orderBy(F.col("temp_out").desc())
        df = df.withColumn(output_col + '_highest_count', F.first(df["temp_out"]).over(win2))
        if type(contributor) == list:
            for cc in contributor:
                df = df.withColumn(output_col + "_" + cc, F.first(df[cc]).over(win2))
        else:
            df = df.withColumn(output_col, F.first(df[contributor]).over(win2))

        """        
        df = df.where(
            (F.col("temp_out") == F.col(output_col + '_highest_count')) & (F.col(output_col) == F.col(contributor)))
        """
        # drop temp columns
        df = df.drop(*["temp_out"])
        return df

    def aggregator(self, df, agg_type, entity_cols, count_col, output_col, filter_in="", params=None, contributor=""):
        """"
        Setup aggregates for existing functions
        :param df:  data frame
        :param agg_type:  set up aggregates: ['sum', 'count', 'countDistinct', 'mean',  'stddev',  'quantile', 'stats']
                         ststs contains both mean and std
        :param entity_cols:  list of aggregation entity example: ['org_id', 'site_id', 'ap_mac']
        :param count_col:  columns to estimate quantiles
        :param output_col:  output column name for mean
        :param filter_in:  Filtering condition if required example: "F.col('count_roaming')!=0"
        :param params: additional parameters required for quantile calculations
        :param contributor:  column to eg=get top contributing entity
        :return: df with added columns
        """
        # <= Check if requested aggregation is in the existing list
        agg_list = ['sum', 'count', 'countDistinct', 'mean',  'stddev',  'stats', 'quantile']
        if agg_type == 'sum':
            df = self.get_sum(df, entity_cols, count_col, output_col, filter_in)
        elif agg_type == 'count':
            df = self.get_counts(df, entity_cols, count_col, output_col, filter_in)
        elif agg_type == 'countDistinct':
            df = self.get_distinct_counts(df, entity_cols, count_col, output_col, filter_in)
        elif agg_type == 'mean':
            df = self.get_mean(df, entity_cols, count_col, output_col, filter_in)
        elif agg_type == 'stddev':
            df = self.get_stddev(df, entity_cols, count_col, output_col, filter_in)
        elif agg_type == 'stats':
            df = self.get_stats(df, entity_cols, count_col, output_col, filter_in)
        elif agg_type == 'quantile':
            if params:
                df = self.get_quantile(df, entity_cols, count_col, output_col, params)
            else:
                df = self.get_quantile(df, entity_cols, count_col, output_col)
        elif agg_type == 'top_contributor':
            df = self.get_top_contributor(df, entity_cols, contributor, count_col, output_col, filter_in)
        else:
            print("<=== Aggregation  function is undefined. No aggregation was added")
        return df

FloatProgress(value=0.0, bar_style='info', description='Progress:', layout=Layout(height='25px', width='50%'),…

In [9]:
tools = AggregationWinUtils()

FloatProgress(value=0.0, bar_style='info', description='Progress:', layout=Layout(height='25px', width='50%'),…

# LOAD CONSTANTS AND SCRIPT

In [10]:
sc.addFile("s3://mist-data-science-dev/marina/roamin_events_code/roaming_events_constants.py")
sc.addFile("s3://mist-data-science-dev/marina/roamin_events_code/roaming_events_utils.py")
sc.addFile("s3://mist-data-science-dev/marina/roamin_events_code/roaming_events_constants_v2.py")

FloatProgress(value=0.0, bar_style='info', description='Progress:', layout=Layout(height='25px', width='50%'),…

In [11]:
import roaming_events_constants as const
from roaming_events_utils import RoamingEventsUtils

FloatProgress(value=0.0, bar_style='info', description='Progress:', layout=Layout(height='25px', width='50%'),…

In [12]:
import roaming_events_constants_v2 as const

FloatProgress(value=0.0, bar_style='info', description='Progress:', layout=Layout(height='25px', width='50%'),…

In [13]:
obj = RoamingEventsUtils()

FloatProgress(value=0.0, bar_style='info', description='Progress:', layout=Layout(height='25px', width='50%'),…

# ORGS NAMES 

In [14]:
df_org = spark.read.parquet("s3://mist-secorapp-production/dimension/org").select(F.col("id").alias("OrgID"),F.col("name").alias("org_name"))
df_name = spark.read.parquet("s3://mist-secorapp-production/dimension/site/site.parquet").select(F.col("id").alias("SiteID"),F.col("name").alias("site_name"),F.col("org_id").alias("OrgID")).join(df_org,["OrgID"])\
                .select("org_name","site_name","OrgID","SiteID")

t_org_1 = df_name.select(['OrgID','org_name']).withColumnRenamed('OrgID', 'org_id').dropDuplicates()
t_org_2 = df_name.select(['SiteID','site_name']).withColumnRenamed('SiteID', 'site_id').dropDuplicates()

FloatProgress(value=0.0, bar_style='info', description='Progress:', layout=Layout(height='25px', width='50%'),…

In [15]:
df_name.printSchema()

FloatProgress(value=0.0, bar_style='info', description='Progress:', layout=Layout(height='25px', width='50%'),…

root
 |-- org_name: string (nullable = true)
 |-- site_name: string (nullable = true)
 |-- OrgID: string (nullable = true)
 |-- SiteID: string (nullable = true)

In [16]:
# Get Org names to Pandas 
# t_org_p = t_org.select(['OrgID', 'org_name', "site_id", 'site_name']).toPandas()

FloatProgress(value=0.0, bar_style='info', description='Progress:', layout=Layout(height='25px', width='50%'),…

# DATA COLLECTION FOR AP DATA 

"s3://mist-secorapp-production/ap-stats-analytics/ap-stats-analytics-production/dt=2022-05-10/hr=21/"

"s3://mist-secorapp-production/es-client-event/es-client-event-production/dt=2022-04-15/hr=15/"

Events in the code:

    analytics/event_generator/client/client_event_code_mapping.py

1.  AP/band: 5c:5b:35:1e:81:f6 / Both

5c5b351e81f6 
org name / env: College Park Church / AWS
    
failure time: Before 11:15 AM EDT Thursday April 15   (15:00 for UTC)

2. 
5c5b351eb563 is assigned to Site[Main Building] 

under Org[Mount Pleasant Christian Church]

5c5b351eb563 : Feb 10 16:55 UTC


 

In [17]:
def get_es_client_data(date, hour, env, sites=[]):
    """
    
    """    
    bucket = "s3://mist-secorapp-{env}/".format(env=env)
    path = "es-client-event/"
    path =  bucket + path + "es-client-event-{env}/".format(env=env)
    
    if hour:
        folder = path + "dt=%s/hr=%s/*"%(date, hour)
    else: 
        folder = path + "dt=%s/*/*"%(date)
    print(folder)    
    df = spark.read.format('orc').load(folder)
    
        
    if sites:
        df = df.where(F.col("site_id").isin(sites))
    df = df.withColumn("timestamp",F.to_timestamp(df['When']))
    
    
    return df

FloatProgress(value=0.0, bar_style='info', description='Progress:', layout=Layout(height='25px', width='50%'),…

In [18]:
def get_ap_stats(date, hour, env, sites=[]):
    """
    
    """    
    bucket = 's3://mist-secorapp-{env}/ap-stats-analytics/ap-stats-analytics-{env}'.format(env=env)
    if hour:
        folder = bucket + "/dt=%s/hr=%s/*.parquet"%(date, hour)
    else: 
        folder = bucket + "/dt=%s/*/*.parquet"%(date)
    print(folder)    
    df = spark.read.parquet(folder) 
    
      
    if sites:
        df = df.where(F.col('site_id').isin(sites))
    # df = df.withColumn("timestamp",F.to_timestamp(df['stats_agg_time']))
    df = df.withColumn("timestamp", F.to_timestamp((F.col("terminator_timestamp")/1000000).cast(LongType()))).persist()   
    
    return df

FloatProgress(value=0.0, bar_style='info', description='Progress:', layout=Layout(height='25px', width='50%'),…

In [19]:
def get_client_stats(date, hour, env, sites =[]):
    bucket = 's3://mist-secorapp-{env}/client-stats-analytics/'.format(env=env)
    bucket =  bucket + 'client-stats-analytics-{env}/'.format(env=env)
    bucket = bucket + 'dt={dt}/hr={hr}/*.parquet'.format(dt=date, hr=hour)

    print(bucket)
    df = spark.read.parquet(bucket)
    if sites:
        df = df.where(F.col('site_id').isin(sites))
    df = df.withColumn("timestamp", F.to_timestamp((F.col("terminator_timestamp")/1000000).cast(LongType()))).persist()   
    return df

FloatProgress(value=0.0, bar_style='info', description='Progress:', layout=Layout(height='25px', width='50%'),…

In [20]:
ap_models = ['AP21-US', 'AP21-WW']

FloatProgress(value=0.0, bar_style='info', description='Progress:', layout=Layout(height='25px', width='50%'),…

In [21]:
AUTH_SUCC_LIST = ['CLIENT_AUTH_ASSOCIATION',
                  'CLIENT_AUTHENTICATED',
                  'CLIENT_AUTH_REASSOCIATION']
ASSO_SUCC_LIST = ['CLIENT_ASSOCIATION',
                  'CLIENT_REASSOCIATION']
NEUTRAL_LIST = ['CLIENT_DEAUTHENTICATION',
                'CLIENT_DEASSOCIATION',
                'CLIENT_DEAUTHENTICATED',
                'CLIENT_AUTH_ASSOCIATION_OKC',
                'CLIENT_AUTHENTICATED_11R',
                'CLIENT_AUTH_REASSOCIATION_OKC',
                'CLIENT_AUTH_REASSOCIATION_11R']

#### === 'STA_DOS_DISASSOC' === ####
#### === NOT TO HAVE === ####
AUTH_FAILURE_LIST=['CLIENT_ASSOCIATION_FAILURE', 
                   'REPEATED_AUTH_FAILURES']
DHCP_FAILURE_LIST=['MARVIS_EVENT_CLIENT_DHCP_STUCK',
                    'MARVIS_EVENT_CLIENT_DHCP_FAILURE']

#### === NOT TO HAVE === ####
AUTH_FAILURE_LIST = ['MARVIS_EVENT_CLIENT_AUTH_FAILURE',
                     'REPEATED_AUTH_FAILURES',
                     'MARVIS_EVENT_CLIENT_AUTH_FAILURE']
ASSO_FAILURE_LIST = ['CLIENT_ASSOCIATION_FAILURE']

events_out = AUTH_SUCC_LIST + ASSO_SUCC_LIST + NEUTRAL_LIST
events_missing = AUTH_FAILURE_LIST + ASSO_FAILURE_LIST

#    ['MARVIS_EVENT_CLIENT_STATIC_DNS_BLOCKED',
#     'MARVIS_EVENT_CLIENT_STATIC_IP_BLOCKED']

FloatProgress(value=0.0, bar_style='info', description='Progress:', layout=Layout(height='25px', width='50%'),…

In [22]:
ap_in = ['5c-5b-35-1e-70-8a', '5c-5b-35-1e-81-f6', '5c-5b-35-1e-b5-63']
sites = ['0a878d43-e796-4120-8cd8-b7359600af16', '41c289fa-a8e5-4b83-aa28-fb9d265dab26']
def get_ap21_data_ap(date, hour, env, sites=[], ap_in=[], models_in=[]):
    env ='production'
    # ap stats
    fields_in_data  = ['rx_decrypt_failures', 
                       'rx_pkts', 
                       'rx_errors', 
                       'tx_pkts', 
                       'tx_errors',
                       're_init']
    fields_in_radio  = ['dev', 
                       'band', 
                       'channel']
    ap_fields = ['site_id',
                 'org_id',
                 'id',
                 'model',
                 'uptime',
                 'interval',
                 'total_client_count', 
                 'active_client_count', 
                 'terminator_timestamp', 
                 'timestamp']
    
    ap_ent_fields = ['site_id',
                     'org_id',
                     'id',
                     'model',
                     'dev', 
                     'band', 
                     'channel']
    
    # AP data 
    df_ap = get_ap_stats(date, hour, env, sites) 
    # select a list of AP 
    if ap_in:
        df_ap = df_ap.where(F.col('id').isin(ap_in))
    if models_in:
        df_ap = df_ap.where(F.col('model').isin(ap_models)) 
    df_ap = df_ap.withColumn("radios", F.explode("radios")).select("*", F.col("radios.*"))
    df_ap = df_ap.withColumn('ap',  F.regexp_replace('id', '-', ''))
    df_ap = df_ap.select(ap_fields + fields_in_radio + fields_in_data)
    df_ap = df_ap.withColumn("timestamp_h", F.date_trunc('hour',F.col('timestamp')))
    df_ap = df_ap.withColumn('ap',  F.regexp_replace('id', '-', ''))    
    return df_ap

def get_ap21_data_cl_ev(date, hour, env):
    # events data
    df_c = get_es_client_data(date, hour, env)
    # add band 
    df_c = df_c.withColumn('band', F.json_tuple("metadata", "band"))
    df_c = df_c.withColumn('band', F.col("band").cast(IntegerType()))   
    return df_c

FloatProgress(value=0.0, bar_style='info', description='Progress:', layout=Layout(height='25px', width='50%'),…

# DETAILED STUDY OF CLIENTS CONNECTIONS 

In [23]:
fields_in_data  = ['rx_decrypt_failures', 
                   'rx_pkts', 
                   'rx_errors', 
                   'tx_pkts', 
                   'tx_errors',
                   're_init']

fields_in_radio  = ['dev', 
                    'band', 
                    'channel']
    
ap_ent_fields = ['site_id',
                 'org_id',
                 'id',
                 'model',
                 'dev', 
                 'band', 
                 'channel']

ap_fields_st =  ['site_id',
                 'org_id',
                 'id',
                 'model', 
                 'total_client_count', 
                 'active_client_count', 
                 'terminator_timestamp', 
                 'timestamp']

ap_fields = ['model',
             'uptime',
             'timestamp']

cl_fields = ['ap_id', 
             'site_id', 
             'org_id', 
             'model', 
             'client_wlan_id', 
             'client_band',
             'client_wcid', 
             'client_connected_time_sec', 
             'client_inactive_time_milli_sec', 
             'client_tx_bit_rate', 
             'client_tx_pkts_sent', 
             'client_rx_bit_rate',
             'client_rx_pkts',
             'client_rxbps', 
             'client_rxpps', 
             'isActive',
             'client_os', 
             'client_model',
             'client_rx_retried',
             'client_rx_retries',
             'client_rx_decrypt_failures',               
             'ap_time']

FloatProgress(value=0.0, bar_style='info', description='Progress:', layout=Layout(height='25px', width='50%'),…

In [ ]:
date = '2022-02-10'
hour = '1*'
env ='production'
# ap stats
sites = ['0a878d43-e796-4120-8cd8-b7359600af16', '41c289fa-a8e5-4b83-aa28-fb9d265dab26']
ap_in = ['5c-5b-35-1e-70-8a', '5c-5b-35-1e-81-f6', '5c-5b-35-1e-b5-63']
ap_in_c = ['5c5b351e708a', '5c5b351e81f6', '5c5b351eb563']

# CLIENT stats data 
df_cs = get_client_stats(date, hour, env)
df_cs = df_cs.where(F.col('ap_id').isin(ap_in))
# df_cs = df_cs.withColumn("radios", F.explode("radios")).select("*", F.col("radios.*"))
df_cs = df_cs.select(cl_fields + ap_fields)
df_cs = df_cs.withColumn('ap',  F.regexp_replace('ap_id', '-', ''))
df_cs = df_cs.withColumn("timestamp_h", F.date_trunc('hour',F.col('timestamp')))

In [ ]:
df_cs.printSchema()

In [ ]:
%%pretty
df_cs.where(F.col('ap_id')=='5c-5b-35-1e-b5-63').orderBy(F.col('timestamp')).show(40, truncate=False)

In [ ]:
%%pretty
df_cs.where((F.col('ap_id') =='5c-5b-35-1e-b5-63') &
            (F.col('client_rx_decrypt_failures')>0)
           ).orderBy(F.col('timestamp')).show(20, truncate=False)

In [ ]:
df_cs.where(F.col('client_rx_decrypt_failures')>0
           ).orderBy(F.col('timestamp')).show(20, truncate=False)

In [ ]:
date = '2022-02-10'
hour = '1*'
env ='production'
# ap stats
sites = ['0a878d43-e796-4120-8cd8-b7359600af16', '41c289fa-a8e5-4b83-aa28-fb9d265dab26']
ap_in = ['5c-5b-35-1e-70-8a', '5c-5b-35-1e-81-f6', '5c-5b-35-1e-b5-63']
ap_fields_ap = ['site_id',
             'org_id',
             'id',
             'model', 
             'total_client_count', 
             'active_client_count', 'terminator_timestamp', 'timestamp']
fields_in_data_ap  = ['rx_decrypt_failures', 'rx_pkts', 'rx_errors', 'tx_pkts', 'tx_errors']

# AP data 
df_ap = get_ap21_data_ap(date, hour)
# Client data 
df_c = get_es_client_data(date, hour, env, sites)

In [ ]:
df_ap.printSchema()

In [ ]:
df_ap.select('timestamp_h').dropDuplicates().orderBy(F.col('timestamp_h')).show(20)

In [ ]:
%%pretty
df_c.where((F.col('ap')== '5c5b351eb563')).orderBy(F.col('timestamp')).show(20, truncate=False)

In [ ]:
%%pretty
df_ap.where((F.col('id')== '5c-5b-35-1e-b5-63') & 
            (F.col('rx_decrypt_failures')>0)
           ).orderBy(F.col('rx_decrypt_failures').desc()).show(20, truncate=False)

In [ ]:
df_c.show(10, truncate=False)

In [ ]:
# select a list of AP for client data 
ap_in = ['5c5b351e708a', '5c5b351e81f6', '5c5b351eb563']
df_c_ap = df_c.where(F.col('ap').isin(ap_in))
df_c_ap = df_c_ap.withColumn("timestamp", F.date_trunc('hour',F.col('When')))
cols_out = ['org_id', 'site_id', 'wcid', 'ap', 'ev_type', 'metadata',  
            'title', 'wlan_id', 'text', 'When', 'timestamp']
df_c_ap = df_c_ap.select(cols_out)
## Select targeted events 
events = events_out + events_missing
df_c_ap = df_c_ap.where(F.col('ev_type').isin(events))


In [ ]:
# select a list of AP for client data 
ap_in = ['5c5b351e708a', '5c5b351e81f6', '5c5b351eb563']
df_c_ap = df_c.where(F.col('ap').isin(ap_in))
df_c_ap = df_c_ap.withColumn("timestamp", F.date_trunc('hour',F.col('When')))
cols_out = ['org_id', 'site_id', 'wcid', 'ap', 'ev_type', 'metadata',  
            'title', 'wlan_id', 'text', 'When', 'timestamp']
df_c_ap = df_c_ap.select(cols_out)
## Select targeted events 
events = events_out + events_missing
df_c_ap = df_c_ap.where(F.col('ev_type').isin(events))

# get counts per h 
entity_cols = ['org_id', 'site_id', 'ap', 'ev_type', 'timestamp']
count_col = 'When'
output_col = 'count_events'
df_c_ap = tools.get_counts(df_c_ap, entity_cols, count_col, output_col)

count_col = 'wcid'
output_col = 'count_clients_by_event'
df_c_ap = tools.get_distinct_counts(df_c_ap, entity_cols, count_col, output_col)

entity_cols = ['org_id', 'site_id', 'ap', 'timestamp']
count_col = 'wcid'
output_col = 'count_clients_by_ap'
df_c_ap = tools.get_distinct_counts(df_c_ap, entity_cols, count_col, output_col)
# add % of affected clients by AP 
df_c_ap = df_c_ap.withColumn('affected_clients', 
                             F.col('count_clients_by_event')/F.col('count_clients_by_ap')*100)

In [ ]:
df_ccc = df_cc.where(F.col('ap_id')=="5c-5b-35-1e-81-f6")

df_ccc.count()

|-- client_rx_bit_rate: integer (nullable = true)
 |-- client_rx_bytes: long (nullable = true)
 |-- client_rx_pkts: integer (nullable = true)
 |-- client_rx_mcast_pkts: integer (nullable = true)
 |-- client_rx_mcast_bytes: long (nullable = true)
 |-- client_rx_retried: integer (nullable = true)
 |-- client_rx_retries: integer (nullable = true)
 |-- client_rx_dups: integer (nullable = true)
 |-- client_rx_decrypt_failures: integer (nullable = true)
 |-- client_rxbps: integer (nullable = true)
 |-- client_rxpps: integer (nullable = true)
 |-- client_rx_probe_reqs24: integer (nullable = true)
 |-- client_rx_probe_reqs5: integer (nullable = true)

%%pretty
df_ccc.select(['timestamp', 'ap_id', 'site_id', 'org_id', 'model', 'wlans', 'client_wcid', 
               'client_connected_time_sec', 'client_inactive_time_milli_sec', 
               'client_tx_bit_rate', 
               'client_tx_pkts_sent', 
               'client_rx_bit_rate',
               'client_rx_pkts',
               'client_rxbps', 
               'client_rxpps', 
               'isActive',
               'client_os', 
               'client_model',
               'client_rx_retried',
               'client_rx_retries',
               'client_rx_decrypt_failures',               
               'ap_time']
             ).orderBy(F.col('timestamp')).show(20, truncate=False)

test = df_ccc.select(['timestamp', 'ap_id', 'site_id', 'org_id', 'model', 'wlans', 'client_wcid', 
               'client_connected_time_sec', 'client_inactive_time_milli_sec', 
               'client_tx_bit_rate', 
               'client_tx_pkts_sent', 
               'client_rx_bit_rate','client_rx_pkts',
               'client_rxbps', 'client_rxpps', 'isActive',
               'client_os', 'client_model', 'ap_time']
             )

# Investigation of cases across all data 

Client connects to AP21 but cannot pass any traffic
Wlan:
c6-74-dc-9d-f8-1e

APs:  
5c:5b:35:1e:81:f6
5c5b351e81f6 is assigned to Site[North Indy Campus] 
under Org[College Park Church]

possible candudate                     
5c:5b:35:1e:70:8a
5c5b351e708a is assigned to Site[North Indy Campus] 
under Org[College Park Church] 


5c5b351eb563
5c5b351eb563 is assigned to Site[Main Building] under Org[Mount Pleasant Christian Church]
                  

 Today's  data
 needed data:
 
rx_decrypt_failures

rx_pkts

rx_errors

tx_pkts

tx_pkts_sent

tx_pkts_failed  

tx_failed_arp - ? 

In [ ]:
ap21 = ['5c5b351e7422', '5c5b351f1896', '5c5b351f31cd', '5c5b351e815b', 
        '5c5b351f1f49', '5c5b351f777d', '5c5b351f05d6', '5c5b351eb829', 
        '5c5b351e91d7', '5c5b351ef983', '5c5b351f0266', '5c5b351f0621', 
        '5c5b351f0568', '5c5b351e93df', '5c5b351f247b', '5c5b351e6784', 
        '5c5b351e9371', '5c5b351e905b', '5c5b351eb42d', '5c5b351e75ee', 
        '5c5b351e9196', '5c5b351f6d2d', '5c5b351f6b3e', '5c5b351f69bd', 
        '5c5b351f4726', '5c5b351f74b2', '5c5b351ebb26', '5c5b351f3bff', 
        '5c5b351e84f8', '5c5b351e2404', '5c5b351f18c3', '5c5b351f6850', '5c5b351f18af', '5c5b351e85ca', '5c5b351eec36', '5c5b351f6aee', '5c5b351e904c', '5c5b351f6143', '5c5b351f3718', '5c5b351e6c89', '5c5b351e7d0f', '5c5b351e9876', '5c5b351f5b76', '5c5b351e21f2', '5c5b351e8af7', '5c5b351e7d14', '5c5b351e8b9c', '5c5b351f0d47', '5c5b351e8cdc', '5c5b351e725b', '5c5b351f04a0', '5c5b351f6297', '5c5b351f1ac6', '5c5b351f694a', '5c5b351f09dc', '5c5b351e90e2', '5c5b351e790e', '5c5b351f3bfa', '5c5b351ef889', '5c5b351f6e4a', '5c5b351f04b9', '5c5b351f73e5', '5c5b351f3808', '5c5b351f5941', '5c5b351f048c', '5c5b351eba9a', '5c5b351f0a6d', '5c5b351f1f1c', '5c5b351efacd', '5c5b351ef8ed', '5c5b351f67f6', '5c5b351e946b', '5c5b351f34c0', '5c5b351f2250', '5c5b351e84a8', '5c5b351e869c', '5c5b351f6b66', '5c5b351f700c', '5c5b351f65bc', '5c5b351ebb85', '5c5b351eb6cb', '5c5b351f0572', '5c5b351e676b', '5c5b351e91c8', '5c5b351f0e5a', '5c5b351f1fa8', '5c5b351f737c', '5c5b351f0c52', '5c5b351f684b', '5c5b351f366e', '5c5b351e9a6a', '5c5b351f0905', '5c5b351f087e', '5c5b351f3a97', '5c5b351f746c', '5c5b351f69e0', '5c5b351eb3fb', '5c5b351f1fee', '5c5b351eb45a', '5c5b351f028e', '5c5b351f07f2', '5c5b351e8bbf', '5c5b351f18d7', '5c5b351e9880', '5c5b351e92b8', '5c5b351f6c92', '5c5b351e277e', '5c5b351e2684', '5c5b351f071b', '5c5b351f5937', '5c5b351e9632', '5c5b351e995c', '5c5b351e9704', '5c5b351f6779', '5c5b351f1ada', '5c5b351e9ae7', '5c5b351f251b', '5c5b351f0770', '5c5b351f69b8', '5c5b351e99bb', '5c5b351e7d41', '5c5b351e8d95', '5c5b351f6026', '5c5b351f203e', '5c5b351f0707', '5c5b351e979f', '5c5b351f6053', '5c5b351f77e6', '5c5b351f1d1e', '5c5b351eb2c5', '5c5b351ef9bf', '5c5b351f3a0b', '5c5b351ebd29', '5c5b351e78e1', '5c5b351e91f5', '5c5b351e9646', '5c5b351f1ae9', '5c5b351eb801', '5c5b351f74fd', '5c5b351f3c59', '5c5b351e83c2', '5c5b351e8755', '5c5b351e8c46', '5c5b351f37cc', '5c5b351f1ee5', '5c5b351f0630', '5c5b351e8025', '5c5b351f584c', '5c5b351e7bd4', '5c5b351e9826', '5c5b351eb73e', '5c5b351f6c83', '5c5b351f769c', '5c5b351e80de', '5c5b351f32b3', '5c5b351f3ad8', '5c5b351f0950', '5c5b351e8f89', '5c5b351f76f6', '5c5b351e27f6', '5c5b351e9579', '5c5b351f6fc1', '5c5b351f0301', '5c5b351e2201', '5c5b351f053b', '5c5b351f12ce', '5c5b351f6328', '5c5b351ebb2b', '5c5b351ebb1c', '5c5b351f1f58', '5c5b351e8c87', '5c5b351f0766', '5c5b351f6bac', '5c5b351f17e7', '5c5b351f106c', '5c5b351e8d72', '5c5b351e744f', '5c5b351f079d', '5c5b351e876e', '5c5b351e93ee', '5c5b351f744e', '5c5b351f6ab2', '5c5b351ef98d', '5c5b351f37b3', '5c5b351e7f0d', '5c5b351f0414', '5c5b351efafa', '5c5b351f19ae', '5c5b351ef30c', '5c5b351f0ba8', '5c5b351f371d', '5c5b351e9916', '5c5b351f3be1', '5c5b351f67bf', '5c5b351f1e77', '5c5b351e6e91', '5c5b351e850c', '5c5b351eb577', '5c5b351f5b7b', '5c5b351f62fb', '5c5b351f775a', '5c5b351f5e3c', '5c5b351e847b', '5c5b351e6748', '5c5b351f073e', '5c5b351e6c75', '5c5b351f5b2b', '5c5b351f1fe4', '5c5b351f5793', '5c5b351e96ff', '5c5b351e865b', '5c5b351e9015', '5c5b351efa69', '5c5b351f5950', '5c5b351f1f4e', '5c5b351e966e', '5c5b351f7034', '5c5b351f0941', '5c5b351f35c9', '5c5b351f67a6', '5c5b351f7462', '5c5b351f0360', '5c5b351ebf45', '5c5b351f2098', '5c5b351e8917', '5c5b351f49dd', '5c5b351e7f8a', '5c5b351e78b9', '5c5b351e2422', '5c5b351e7cce', '5c5b351f1bca', '5c5b351efb59', '5c5b351e83e0', '5c5b351ec0da', '5c5b351f6d32', '5c5b351f77cd', '5c5b351f685f', '5c5b351e718e', '5c5b351f7665', '5c5b351f72b9', '5c5b351e6b5d', '5c5b351f3a60', '5c5b351f5b80', '5c5b351e7fa8', '5c5b351f20d4', '5c5b351f3588', '5c5b351eba7c', '5c5b351f206b', '5c5b351f6134', '5c5b351f361e', '5c5b351f5b1c', '5c5b351efac8', '5c5b351f72a0', '5c5b351f3510', '5c5b351e9aa6', '5c5b351e8be2', '5c5b351e7094', '5c5b351e22c9', '5c5b351e8412', '5c5b351f0946', '5c5b351f0234', '5c5b351f6981', '5c5b351e2738', '5c5b351e9439', '5c5b351f0626', '5c5b351f0405', '5c5b351f1c0b', '5c5b351e91dc', '5c5b351eb513', '5c5b351e6aef', '5c5b351e924a', '5c5b351e25c6', '5c5b351e918c', '5c5b351f6a3a', '5c5b351f3b19', '5c5b351f072a', '5c5b351f0257', '5c5b351f2093', '5c5b351f1ddc', '5c5b351eb58b', '5c5b351eb3ce', '5c5b351e9600', '5c5b351e8f9d', '5c5b351f02f7', '5c5b351eb78e', '5c5b351e98e9', '5c5b351ec0ad', '5c5b351f5815', '5c5b351f1e86', '5c5b351f625b', '5c5b351e8c4b', '5c5b351e8e3a', '5c5b351f3a24', '5c5b351e907e', '5c5b351f740d', '5c5b351e2710', '5c5b351e68c4', '5c5b351f0a27', '5c5b351f0919', '5c5b351f3803', '5c5b351f6ac6', '5c5b351e92a4', '5c5b351e7c47', '5c5b351f20e3', '5c5b351e9817', '5c5b351f6d0f', '5c5b351f6bb6', '5c5b351f0e4b', '5c5b351f3cbd', '5c5b351eef06', '5c5b351e73f5', '5c5b351e68ba', '5c5b351f5b0d', '5c5b351f68af', '5c5b351eed08', '5c5b351f6c56', '5c5b351efb5e', '5c5b351e8831', '5c5b351e843a', '5c5b351e8dc7', '5c5b351ebac2', '5c5b351e929f', '5c5b351f031a', '5c5b351f58ab', '5c5b351e7dbe', '5c5b351f3678', '5c5b351e9a29', '5c5b351eb3b0', '5c5b351eb4af', '5c5b351f6a2b', '5c5b351e8b83', '5c5b351e8296', '5c5b351e8e4e', '5c5b351f5bd0', '5c5b351f608a', '5c5b351e7ebd', '5c5b351f0793', '5c5b351e9245', '5c5b351f658f', '5c5b351f522f', '5c5b351f649a', '5c5b351f394d', '5c5b351f5978', '5c5b351f64e5', '5c5b351f71ce', '5c5b351f0757', '5c5b351f01e9', '5c5b351e8dd1', '5c5b351e8bb0', '5c5b351f0423', '5c5b351f03b5', '5c5b351f325e', '5c5b351e529e', '5c5b351f0400', '5c5b351e8692', '5c5b351e938a', '5c5b351e221a', '5c5b351f1157', '5c5b351f05bd', '5c5b351e988f', '5c5b351f1fe9', '5c5b351f1c38', '5c5b351f6be3', '5c5b351e6b44', '5c5b351e91aa', '5c5b351f1873', '5c5b351eec40', '5c5b351e85ed', '5c5b351e27a1', '5c5b351f3bd2', '5c5b351e9461', '5c5b351f26ba', '5c5b351e7634', '5c5b351f1e63', '5c5b351e87be', '5c5b351e7fa3', '5c5b351e271f', '5c5b351e976d', '5c5b351e959c', '5c5b351efaa0', '5c5b351ef9ec', '5c5b351e7d7d', '5c5b351f34ed', '5c5b351f04be', '5c5b351f4afa', '5c5b351f67ab', '5c5b351e8b38', '5c5b351e9178', '5c5b351eba8b', '5c5b351e8c82', '5c5b351f05a4', '5c5b351e9ab5', '5c5b351e8fb1', '5c5b351f0a9a', '5c5b351f0860', '5c5b351f57ed', '5c5b351f6c2e', '5c5b351e93f3', '5c5b351e8e76', '5c5b351e8f6b', '5c5b351f1e9f', '5c5b351f19ea', '5c5b351f09cd', '5c5b351e960f', '5c5b351f6459', '5c5b351f77ff', '5c5b351e66cb', '5c5b351f081a', '5c5b351e9128', '5c5b351eb33d', '5c5b351e6b71', '5c5b351e8e62', '5c5b351e7ec2', '5c5b351ebffe', '5c5b351eb99b', '5c5b351ef884', '5c5b351f199f', '5c5b351f2070', '5c5b351f2552', '5c5b351e99d9', '5c5b351f6a8a', '5c5b351e9335', '5c5b351eb392', '5c5b351e9533', '5c5b351e6f63', '5c5b351e24a4', '5c5b351f6b20', '5c5b351eee43', '5c5b351eb847', '5c5b351eeefc', '5c5b351f6c24', '5c5b351f0243', '5c5b351e7206', '5c5b351e7ecc', '5c5b351e816a', '5c5b351ef960', '5c5b351e7909', '5c5b351f1e8b', '5c5b351e8ddb', '5c5b351f1814', '5c5b351f3ab0', '5c5b351eba13', '5c5b351f0658', '5c5b351f6b57', '5c5b351f653f', '5c5b351f0af4', '5c5b351f1094', '5c5b351f697c', '5c5b351f1aa3', '5c5b351f69a4', '5c5b351e7d19', '5c5b351eb48c', '5c5b351f3d4e', '5c5b351e9835', '5c5b351e7cba', '5c5b351f709d', '5c5b351f1f53', '5c5b351e6775', '5c5b351e9754', '5c5b351f66cf', '5c5b351f6599', '5c5b351e9894', '5c5b351ebc4d', '5c5b351f61fc', '5c5b351e99de', '5c5b351f1f80', '5c5b351eaacd', '5c5b351e84f3', '5c5b351e6cf7', '5c5b351f12bf', '5c5b351f59b9', '5c5b351e7d46', '5c5b351f14c2', '5c5b351f0482', '5c5b351f0a0e', '5c5b351f5798', '5c5b351f0e32', '5c5b351eb996', '5c5b351f090f', '5c5b351eb621', '5c5b351e6739', '5c5b351e2594', '5c5b351f2e80', '5c5b351f1f35', '5c5b351f6ada', '5c5b351eb9eb', '5c5b351f0a5e', '5c5b351ebc9d', '5c5b351ef51e', '5c5b351f6567', '5c5b351f37bd', '5c5b351eb65d', '5c5b351efb36', '5c5b351f66f2', '5c5b351f70a2', '5c5b351e8efd', '5c5b351e8de5', '5c5b351f3989', '5c5b351e8eda', '5c5b351f062b', '5c5b351e839f', '5c5b351e827d', '5c5b351f68fa', '5c5b351ebce3', '5c5b351e92db', '5c5b351eb3c9', '5c5b351ef94c', '5c5b351e6c0c', '5c5b351e7cb0', '5c5b351f1300', '5c5b351efa5a', '5c5b351f64f4', '5c5b351e6761', '5c5b351ef88e', '5c5b351e97cc', '5c5b351f0527', '5c5b351f6d00', '5c5b351e861a', '5c5b351e90b5', '5c5b351f0900', '5c5b351f6ad0', '5c5b351eb536', '5c5b351e23c3', '5c5b351eeb55', '5c5b351f22aa', '5c5b351e6df1', '5c5b351f0595', '5c5b351e9a6f', '5c5b351f3943', '5c5b351f0b99', '5c5b351f3867', '5c5b351ea906', '5c5b351e9943', '5c5b351ebfb3', '5c5b351f08b5', '5c5b351f39de', '5c5b351ec085', '5c5b351f0379', '5c5b351f0216', '5c5b351e8615', '5c5b351e8d8b', '5c5b351f096e', '5c5b351f6a67', '5c5b351f0d56', '5c5b351f73b3', '5c5b351f0ae5', '5c5b351e7fb2', '5c5b351f5842', '5c5b351f6206', '5c5b351e816f', '5c5b351f02ca', '5c5b351e270b', '5c5b351f68ff', '5c5b351f6521', '5c5b351f68e1', '5c5b351f6ad5', '5c5b351f6319', '5c5b351ebe7d', '5c5b351e8bd8', '5c5b351f6f8a', '5c5b351f34c5', '5c5b351e9074', '5c5b351f3ae7', '5c5b351e52c1', '5c5b351e8dbd', '5c5b351efaf5', '5c5b351f0298', '5c5b351ef514', '5c5b351f3709', '5c5b351e9010', '5c5b351e8e8a', '5c5b351e79e0', '5c5b351f2192', '5c5b351f3a88', '5c5b351e7e72', '5c5b351f055e', '5c5b351f37f9', '5c5b351f6c7e', '5c5b351f09c8', '5c5b351f0928', '5c5b351f12f1', '5c5b351f2214', '5c5b351e2530', '5c5b351eb8e2', '5c5b351f763d', '5c5b351e67ac', '5c5b351f74f3', '5c5b351f5fdb', '5c5b351f1eef', '5c5b351f3119', '5c5b351f6d19', '5c5b351f07c0', '5c5b351f667f', '5c5b351e22c4', '5c5b351f1bac', '5c5b351efa32', '5c5b351f3592', '5c5b351e9763', '5c5b351e9691', '5c5b351e8fa7', '5c5b351f0a36', '5c5b351e5082', '5c5b351f3371', '5c5b351f65f3', '5c5b351f05ae', '5c5b351e7f5d', '5c5b351ebe5a', '5c5b351e8b7e', '5c5b351e6b2b', '5c5b351e81ba', '5c5b351eeb5f', '5c5b351eb220', '5c5b351f03ce', '5c5b351eb9d7', '5c5b351f5d4c', '5c5b351f4c8f', '5c5b351e91a5', '5c5b351f06e9', '5c5b351e95dd', '5c5b351e8b92', '5c5b351f74a8', '5c5b351f6b1b', '5c5b351f1adf', '5c5b351ea938', '5c5b351e817e', '5c5b351f4947', '5c5b351f1995', '5c5b351e9830', '5c5b351f1b5c', '5c5b351e5212', '5c5b351f603a', '5c5b351e9961', '5c5b351e8421', '5c5b351e6932', '5c5b351f05a9', 
        '5c5b351e8110', '5c5b351f5955', '5c5b351eba31', '5c5b351e7436', '5c5b351e253f', '5c5b351e6e69', '5c5b351eeb91', '5c5b351f36a0', '5c5b351e6fd1', '5c5b351f0211', '5c5b351f7773', '5c5b351f64cc', '5c5b351f2151', '5c5b351f0531', '5c5b351e8c32', '5c5b351f0b26', '5c5b351e8f0c', '5c5b351e91c3', '5c5b351f3a74', '5c5b351f72e1', '5c5b351f1f9e', '5c5b351e681f', '5c5b351f62ec', '5c5b351eb57c', '5c5b351f3b05', '5c5b351efac3', '5c5b351e8782', '5c5b351e84ad', '5c5b351f0a90', '5c5b351eb54f', '5c5b351f6733', '5c5b351f653a', '5c5b351f1c01', '5c5b351f1215', '5c5b351f6fe4', '5c5b351f068f', '5c5b351f76c9', '5c5b351e85ac', '5c5b351e990c', '5c5b351ef8d4', '5c5b351e94e8', '5c5b351e7d91', '5c5b351f5883', '5c5b351e8232', '5c5b351f73c7', '5c5b351f6486', '5c5b351f6f3a', '5c5b351f08bf', '5c5b351f3ac9', '5c5b351f1fcb', '5c5b351e2567', '5c5b351f5c20', '5c5b351eee25', '5c5b351e8acf', '5c5b351e762a', '5c5b351ebbc6', '5c5b351f766a', '5c5b351e93d5', '5c5b351e2535', '5c5b351f3a1a', '5c5b351f1a12', '5c5b351f0441', '5c5b351f0806', '5c5b351f4a91', '5c5b351e9925', '5c5b351e9501', '5c5b351f64b3', '5c5b351e99f7', '5c5b351eb5db', '5c5b351eb6e4', '5c5b351f46c2', '5c5b351e8453', '5c5b351e803e', '5c5b351e66da', '5c5b351f36fa', '5c5b351e2319', '5c5b351f7778', '5c5b351eed53', '5c5b351f2520', '5c5b351f6896', '5c5b351f5874', '5c5b351eb5ea', '5c5b351e2503', '5c5b351eb4d2', '5c5b351f21e7', '5c5b351ec049', '5c5b351f1a76', '5c5b351e94c5', '5c5b351f07de', '5c5b351e8ee4', '5c5b351f1ad0', '5c5b351e9376', '5c5b351eb9af', '5c5b351f0dfb', '5c5b351f68cd', '5c5b351e85cf', '5c5b351f0702', '5c5b351e8d31', '5c5b351f1bbb', '5c5b351f06f3', '5c5b351e678e', '5c5b351f188c', '5c5b351f784a', '5c5b351f065d', '5c5b351e7e86', '5c5b351f1fc1', '5c5b351f20d9', '5c5b351eb38d', '5c5b351f629c', '5c5b351f5969', '5c5b351f688c', '5c5b351f09e6', '5c5b351e8c1e', '5c5b351e91ff', '5c5b351f3b87', '5c5b351e927c', '5c5b351f0464', '5c5b351f2084', '5c5b351e2517', '5c5b351e21ca', '5c5b351f1c1a', '5c5b351e2526', '5c5b351f606c', '5c5b351f07a2', '5c5b351f01f8', '5c5b351f694f', '5c5b351f0671', '5c5b351e975e', '5c5b351f3286', '5c5b351e2472', '5c5b351eb464', '5c5b351e9934', '5c5b351e25df', '5c5b351ef9ba', '5c5b351e70c1', '5c5b351f07b1', '5c5b351f752f', '5c5b351e7efe', '5c5b351ebc39', '5c5b351e848f', '5c5b351e98c1', '5c5b351e7f44', '5c5b351eebb4', '5c5b351f0801', '5c5b351e66f3', '5c5b351f6f6c', '5c5b351ebc98', '5c5b351e7995', '5c5b351e7cdd', '5c5b351e9056', '5c5b351e2652', '5c5b351f039c', '5c5b351f34d9', '5c5b351e727e', '5c5b351e258a', '5c5b351e9768', '5c5b351eb72f', '5c5b351f66c5', '5c5b351f06d5', '5c5b351e27fb', '5c5b351f69cc', '5c5b351e7cfb', '5c5b351e675c', '5c5b351e83bd', '5c5b351f0784', '5c5b351eedc6', '5c5b351eec6d', '5c5b351f1882', '5c5b351e70d0', '5c5b351f02cf', '5c5b351f7057', '5c5b351eb43c', '5c5b351e952e', '5c5b351efb31', '5c5b351f06c6', '5c5b351f6102', '5c5b351e4ffb', '5c5b351e95f6', '5c5b351f6b2a', '5c5b351e8679', '5c5b351e92d1', '5c5b351e997a', '5c5b351e8d27', '5c5b351e21de', '5c5b351f03d3', '5c5b351e941b', '5c5b351f6fda', '5c5b351f042d', '5c5b351f5612', '5c5b351e8d04', '5c5b351f6b93', '5c5b351f6abc', '5c5b351f676f', '5c5b351f7719', '5c5b351f0a72', '5c5b351e81c9', '5c5b351eba22', '5c5b351ec00d', '5c5b351e9416', '5c5b351f30c9', '5c5b351e68a6', '5c5b351f665c', '5c5b351e8f52', '5c5b351f360a', '5c5b351f1f5d', '5c5b351f37e0', '5c5b351e25da', '5c5b351f618e', '5c5b351f36b9', '5c5b351e8642', '5c5b351f1ff3', '5c5b351f3aa1', '5c5b351e9998', '5c5b351eb450', '5c5b351f027a', '5c5b351f0540', '5c5b351f4f5a', '5c5b351f3cd6', '5c5b351f28d1', '5c5b351ef9d3', '5c5b351f10cb', '5c5b351f2499', '5c5b351e9772', '5c5b351e7d37', '5c5b351f0225', '5c5b351e83ef', '5c5b351f1f76', '5c5b351f081f', '5c5b351f570c', '5c5b351f519e', '5c5b351f2002', '5c5b351f3ce5', '5c5b351e71e3', '5c5b351f6369', '5c5b351f6b39', '5c5b351efa9b', '5c5b351ebc48', '5c5b351eeeb6', '5c5b351f4c4e', '5c5b351eee1b', '5c5b351f046e', '5c5b351f784f', '5c5b351e9a79', '5c5b351e257b', '5c5b351f5dd8', '5c5b351f5b17', '5c5b351e8f66', '5c5b351f047d', '5c5b351e7deb', '5c5b351f583d', '5c5b351f4a7d', '5c5b351e874b', '5c5b351efb72', '5c5b351e80c0', '5c5b351eb5e5', '5c5b351ead52', '5c5b351ef9a6', '5c5b351f3c18', '5c5b351f6eb8', '5c5b351f68a5', '5c5b351e253a', '5c5b351e8e12', '5c5b351e7904', '5c5b351eeca4', '5c5b351f266a', '5c5b351f2462', '5c5b351e6702', '5c5b351e2521', '5c5b351ebe87', '5c5b351e2170', '5c5b351f3c36', '5c5b351f5b30', '5c5b351e8e9e', '5c5b351f02d4', '5c5b351e96b9', '5c5b351f0d1a', '5c5b351f19fe', '5c5b351f6de1', '5c5b351e7f17', '5c5b351e238c', '5c5b351eb7e8', '5c5b351e8b42', '5c5b351f08ec', '5c5b351f3a56', '5c5b351e671b', '5c5b351e8c78', '5c5b351e7f94', '5c5b351f4e79', '5c5b351e9547', '5c5b351f69ea', '5c5b351e9493', '5c5b351f4a46', '5c5b351e8d0e', '5c5b351f1a71', '5c5b351f0dd3', '5c5b351f0202', '5c5b351e8e53', '5c5b351f0248', '5c5b351f6c38', '5c5b351f675b', '5c5b351e9033', '5c5b351ef717', '5c5b351f01e4', '5c5b351f082e', '5c5b351f2679', '5c5b351efb27', '5c5b351e932b', '5c5b351e9407', '5c5b351e7d50', '5c5b351f35c4', '5c5b351e961e', '5c5b351f208e', '5c5b351f1bb6', '5c5b351e96f5', '5c5b351e2648', '5c5b351e83a9', '5c5b351f396b', '5c5b351f6a08', '5c5b351e8994', '5c5b351e4f88', '5c5b351ea924', '5c5b351ebc20', '5c5b351f6035', '5c5b351f1fd5', '5c5b351f4bd6', '5c5b351f36f0', '5c5b351e8331', '5c5b351f1e40', '5c5b351ea7e9', '5c5b351e232d', '5c5b351f181e', '5c5b351f3f7e', '5c5b351f6990', '5c5b351f0c1b', '5c5b351ef8a2', '5c5b351f7043', '5c5b351e7418', '5c5b351e6824', '5c5b351e8fed', '5c5b351e875a', '5c5b351f6a94', '5c5b351e85de', '5c5b351e9853', '5c5b351e86f1', '5c5b351eb446', '5c5b351ef979', '5c5b351e91e1', '5c5b351f6364', '5c5b351e8002', '5c5b351e9097', '5c5b351e72b0', '5c5b351f4cb7', '5c5b351eb5c7', '5c5b351f767e', '5c5b351f0342', '5c5b351f5a3b', '5c5b351eb248', '5c5b351f4da7', '5c5b351f1fb2', '5c5b351e9650', '5c5b351f1ee0', '5c5b351ef924', '5c5b351e9141', '5c5b351f7377', '5c5b351f05c2', '5c5b351f18b9', '5c5b351e962d', '5c5b351e9169', '5c5b351ef8d9', '5c5b351f1bd9', '5c5b351e8d2c', '5c5b351f6ffd', '5c5b351f6a76', '5c5b351e98b2', '5c5b351f6afd', '5c5b351ebc43', '5c5b351f3dcb', '5c5b351f6a12', '5c5b351f03ba', '5c5b351e9a83', '5c5b351f1ffd', '5c5b351f6b70', '5c5b351e99b6', '5c5b351f764c', '5c5b351f0a31', '5c5b351f6f12', '5c5b351e7d96', '5c5b351e9902', '5c5b351f1a9e', '5c5b351e7e3b', '5c5b351e52d0', '5c5b351f299e', '5c5b351f3c90', '5c5b351e9790', '5c5b351f6ca1', '5c5b351e7f26', '5c5b351f1e09', '5c5b351f1b3e', '5c5b351e7bde', '5c5b351e9227', '5c5b351f037e', '5c5b351e9664', '5c5b351ebfe5', '5c5b351eeecf', '5c5b351f070c', '5c5b351ef86b', '5c5b351f359c', '5c5b351f0581', '5c5b351eb45f', '5c5b351e22e7', '5c5b351e80f2', '5c5b351f0270', '5c5b351e85d9', '5c5b351f65e9', '5c5b351f7516', '5c5b351e8651', '5c5b351ebcd9', '5c5b351f1e22', '5c5b351f6292', '5c5b351f069e', '5c5b351e23d2', '5c5b351e909c', '5c5b351e8449', '5c5b351e9957', '5c5b351e9911', '5c5b351e9ad3', '5c5b351f1cd8', '5c5b351e8d86', '5c5b351f18cd', '5c5b351eee98', '5c5b351f32ea', '5c5b351eb4e6', '5c5b351f6c65', '5c5b351efb86', '5c5b351f60b2', '5c5b351eb4dc', '5c5b351e9088', '5c5b351e9795', '5c5b351e6fb8', '5c5b351e9065', '5c5b351ef974', '5c5b351e21d4', '5c5b351f20fc', '5c5b351f0982', '5c5b351e7d69', '5c5b351e7fe9', '5c5b351e254e', '5c5b351efa64', '5c5b351eb39c', '5c5b351e9a01', '5c5b351f5928', '5c5b351f6b84', '5c5b351e935d', '5c5b351e99ed', '5c5b351f2057', '5c5b351f0590', '5c5b351e5000', '5c5b351f1e13', '5c5b351e8e67', '5c5b351f08c9', '5c5b351e2553', '5c5b351f6a85', '5c5b351f73ef', '5c5b351f1ce7', '5c5b351f03a1', '5c5b351f1d6e', '5c5b351e74c2', '5c5b351ef8ac', '5c5b351e9272', '5c5b351ebe23', '5c5b351f0955', '5c5b351f69db', '5c5b351e6c57', '5c5b351f65a3', '5c5b351e2788', '5c5b351e98fd', '5c5b351f1878', '5c5b351e7977', '5c5b351f589c', '5c5b351f24cb', '5c5b351e66e4', '5c5b351f03ab', '5c5b351e7f30', '5c5b351f7444', '5c5b351e9402', '5c5b351f210b', '5c5b351f28f4', '5c5b351e983f', '5c5b351e91af', '5c5b351e84bc', '5c5b351ebbbc', '5c5b351ef8bb', '5c5b351f689b', '5c5b351f6cf6', '5c5b351f3af1', '5c5b351f572f', '5c5b351f6f44', '5c5b351e83c7', '5c5b351ebc84', '5c5b351e991b', '5c5b351ebe14', '5c5b351f7782', '5c5b351f2048', '5c5b351f5f59', '5c5b351f680a', '5c5b351f0577', '5c5b351f1f17', '5c5b351f7386', '5c5b351f0220', '5c5b351e7d82', '5c5b351eee2a', '5c5b351f0c34', '5c5b351f06f8', '5c5b351e70f3', '5c5b351f0a8b', '5c5b351f058b', '5c5b351e8da4', '5c5b351e7f62', '5c5b351e6a40', '5c5b351f2a39', '5c5b351efb40', '5c5b351e7fda', '5c5b351f65df', '5c5b351f4cee', '5c5b351eb5d6', '5c5b351eee34', '5c5b351f7098', '5c5b351f4e47', '5c5b351f3952', '5c5b351f4ea6', '5c5b351f3367', '5c5b351e7f76', '5c5b351eb3e2', '5c5b351e7454', '5c5b351f0cb1', '5c5b351e9731', '5c5b351f6a80', '5c5b351e7963', '5c5b351f686e', '5c5b351f6283', '5c5b351eec45', '5c5b351f58d8', '5c5b351f09e1', '5c5b351f05fe', '5c5b351e22f1', '5c5b351e8d22', '5c5b351efb18', '5c5b351e260c', '5c5b351e8fcf', '5c5b351e944d', '5c5b351f0289', '5c5b351e7bd9', '5c5b351e7f53', '5c5b351eee93', '5c5b351ef99c', '5c5b351e8f11', '5c5b351f3376', '5c5b351f0775', '5c5b351ebbd0', '5c5b351f7714', '5c5b351eb3ab', '5c5b351f3583', '5c5b351f6099', '5c5b351f743f', '5c5b351e7ee5', '5c5b351e50aa', '5c5b351eb2ac', '5c5b351e8b8d', '5c5b351ef8f7', '5c5b351f5202', '5c5b351f6bfc', '5c5b351e6a68', '5c5b351f3623', '5c5b351e6734', '5c5b351e8aac', '5c5b351e7f6c', '5c5b351e677a', '5c5b351e9164', '5c5b351f7651', '5c5b351f741c', '5c5b351eef01', '5c5b351e931c', '5c5b351e7f58', '5c5b351e7d32', '5c5b351f0a40', '5c5b351e8bf6', '5c5b351f37fe', '5c5b351e8cd7', '5c5b351f6c47', '5c5b351e8f61', '5c5b351f1256', '5c5b351f4b95', '5c5b351eb22a', '5c5b351f3975', '5c5b351eb4a0', '5c5b351f1cb0', '5c5b351f02bb', '5c5b351e963c', '5c5b351f1fbc', '5c5b351e95a6', '5c5b351ebcc5', '5c5b351ebd74', '5c5b351f095f', '5c5b351f6a03', '5c5b351f5a22', '5c5b351e6b8a', '5c5b351e97c7', '5c5b351e84d5', '5c5b351e7a53', '5c5b351e694b', '5c5b351f3821', '5c5b351f3d2b', '5c5b351f6ef4', '5c5b351f1de1', '5c5b351f5bc1', '5c5b351f1f6c', '5c5b351f4e15', '5c5b351f10ad', '5c5b351e7dc8', '5c5b351e7d2d', '5c5b351e8cb9', '5c5b351e810b', '5c5b351e8624', '5c5b351e69f5', '5c5b351e924f', 
        '5c5b351e9457', '5c5b351eb4be', '5c5b351f7539', '5c5b351e6856', 
        '5c5b351e221f', '5c5b351f6936', '5c5b351f08f1', '5c5b351f3506', 
        '5c5b351f69b3', '5c5b351f3cf9', '5c5b351e7db4', '5c5b351f1bf2', 
        '5c5b351e97d6', '5c5b351e996b', '5c5b351ef8ca', '5c5b351efaf0', 
        '5c5b351e6ed2', '5c5b351f0676', '5c5b351f209d', '5c5b351e8c5f', 
        '5c5b351f1fdf', '5c5b351f66c0', '5c5b351f7511', '5c5b351e9051', '5c5b351f0428', '5c5b351e9114', '5c5b351f74b7', '5c5b351e90c9', '5c5b351f34f7', '5c5b351f0a09', '5c5b351f5a72', '5c5b351f0e00', '5c5b351f55fe', '5c5b351f1af3', '5c5b351f4e0b', '5c5b351f1e72', '5c5b351f5ce3', '5c5b351ebb49', '5c5b351f3cf4', '5c5b351f1a62', '5c5b351f1b98', '5c5b351f6864', '5c5b351f5964', '5c5b351efa37', '5c5b351e951f', '5c5b351e505a', '5c5b351f74df', '5c5b351e958d', '5c5b351f207f', '5c5b351f39fc', '5c5b351f5bfd', '5c5b351f0392', '5c5b351e939e', '5c5b351eb41e', '5c5b351f4c76', '5c5b351ebbda', '5c5b351f0306', '5c5b351e6711', '5c5b351e920e', '5c5b351e97ae', '5c5b351eb5e0', '5c5b351f04b4', '5c5b351ea8ca', '5c5b351f68c3', '5c5b351f69c7', '5c5b351f5833', '5c5b351ebebe', '5c5b351e984e', '5c5b351f578e', '5c5b351e95ec', '5c5b351efb4f', '5c5b351f07e3', '5c5b351e7c42', '5c5b351f023e', '5c5b351e9556', '5c5b351f3a5b', '5c5b351e670c', '5c5b351e21b1', '5c5b351f35ab', '5c5b351ef96f', '5c5b351e9259', '5c5b351f09eb', '5c5b351f0509', '5c5b351f351a', '5c5b351e70b2', '5c5b351ebaae', '5c5b351e7d3c', '5c5b351e9605', '5c5b351eb478', '5c5b351e99a7', '5c5b351e6de2', '5c5b351f3150', '5c5b351f6fcb', '5c5b351f0374', '5c5b351f7787', '5c5b351e9565', '5c5b351f5860', '5c5b351f4f78', '5c5b351e9466', '5c5b351e9132', '5c5b351f1841', '5c5b351e845d', '5c5b351f37c2', '5c5b351eec4f', '5c5b351f6940', '5c5b351e9240', '5c5b351e8ceb', '5c5b351f1b39', '5c5b351e8c73', '5c5b351e776f', '5c5b351e672f', '5c5b351e8ff7', '5c5b351e8abb', '5c5b351f089c', '5c5b351e8eb2', '5c5b351e9ac4', '5c5b351e97bd', '5c5b351f6783', '5c5b351e7251', '5c5b351e9899', '5c5b351e9204', '5c5b351e6a59', '5c5b351e9a92', '5c5b351f056d', '5c5b351e8e26', '5c5b351f1823', '5c5b351f0937', '5c5b351e50e6', '5c5b351f0991', '5c5b351e6a36', '5c5b351e9146', '5c5b351e23c8', '5c5b351e8d45', '5c5b351f6689', '5c5b351f674c', '5c5b351f0bf8', '5c5b351f3cdb', '5c5b351efa28', '5c5b351ef91a', '5c5b351f05c7', '5c5b351e672a', '5c5b351f1bcf', '5c5b351f0ca2', '5c5b351e98c6', '5c5b351e9af1', '5c5b351e94d4', '5c5b351e2314', '5c5b351f0347', '5c5b351f614d', '5c5b351f6ce7', '5c5b351e22e2', '5c5b351e99f2', '5c5b351e7616', '5c5b351f7124', '5c5b351e6f22', '5c5b351e6efa', '5c5b351e8c19', '5c5b351e7f99', '5c5b351f1c15', '5c5b351f352e', '5c5b351f76e2', '5c5b351f1aee', '5c5b351f609e', '5c5b351f7381', '5c5b351e9268', '5c5b351f6cb5', '5c5b351f0383', '5c5b351eb798', '5c5b351f74c1', '5c5b351f6aa3', '5c5b351e8a98', '5c5b351f083d', '5c5b351f6ef9', '5c5b351f515d', '5c5b351f1d3c', '5c5b351f1a26', '5c5b351e263e', '5c5b351e7f2b', '5c5b351f1869', '5c5b351ebca7', '5c5b351e90b0', '5c5b351f648b', '5c5b351f5ba8', '5c5b351f06da', '5c5b351eb473', '5c5b351f07ed', '5c5b351f0667', '5c5b351f20c5', '5c5b351f0824', '5c5b351f025c', '5c5b351e8160', '5c5b351f1b93', '5c5b351f31d7', '5c5b351f7601', '5c5b351e6a4f', '5c5b351e8f93', '5c5b351f57ac', '5c5b351f098c', '5c5b351f5766', '5c5b351e9191', '5c5b351eb9a5', '5c5b351f03e2', '5c5b351e6e87', '5c5b351e6757', '5c5b351f6639', '5c5b351f6bd9', '5c5b351f1b8e', '5c5b351e99e3', '5c5b351f5e64', '5c5b351e93da', '5c5b351eecae', '5c5b351f67b5', '5c5b351eb4c8', '5c5b351e98ad', '5c5b351e9af6', '5c5b351e8660', '5c5b351f0d06', '5c5b351ef8e3', '5c5b351f3b46', '5c5b351f22be', '5c5b351e9ac9', '5c5b351f09d2', '5c5b351e967d', '5c5b351eeea7', '5c5b351f753e', '5c5b351e9849', '5c5b351ebcf2', '5c5b351e8bdd', '5c5b351e7f3f', '5c5b351eee66', '5c5b351f668e', '5c5b351e8b24', '5c5b351f67b0', '5c5b351f30e2', '5c5b351e23aa', '5c5b351f750c', '5c5b351efae6', '5c5b351f0aea', '5c5b351eb5f9', '5c5b351ebec8', '5c5b351e868d', '5c5b351efad7', '5c5b351e8c7d', '5c5b351f085b', '5c5b351f0e55', '5c5b351f0324', '5c5b351e91e6', '5c5b351f58c4', '5c5b351e9736', '5c5b351ebc89', '5c5b351f6a49', '5c5b351f76c4', '5c5b351ebc07', '5c5b351f6a4e', '5c5b351f6b2f', '5c5b351f77b9', '5c5b351ebce8', '5c5b351e97b8', '5c5b351ef9ab', '5c5b351e994d', '5c5b351e96dc', '5c5b351ebf13', '5c5b351efa05', '5c5b351e26ca', '5c5b351f0815', '5c5b351f630a', '5c5b351f3353', '5c5b351e8142', '5c5b351e8ce6', '5c5b351e6743', '5c5b351e2486', '5c5b351f5923', '5c5b351e8da9', '5c5b351e957e', '5c5b351e84c1', '5c5b351e96c8', '5c5b351e8cc8', '5c5b351e93cb', '5c5b351e9060', '5c5b351e8bd3', '5c5b351e91cd', '5c5b351e9a3d', '5c5b351e97c2', '5c5b351f73a9', '5c5b351e979a', '5c5b351f6a30', '5c5b351e67de', '5c5b351e8007', '5c5b351e9592', '5c5b351e953d', '5c5b351f6bc5', '5c5b351efa55', '5c5b351e6eb4', '5c5b351e7e95', '5c5b351e90ab', '5c5b351e8516', '5c5b351f04dc', '5c5b351f6094', '5c5b350eb23f', '5c5b351f6968', '5c5b351f6a99', '5c5b351e7ff3', '5c5b351f5a63', '5c5b351e8e3f', '5c5b351e795e', '5c5b351f7354', '5c5b351ef992', '5c5b351f681e', '5c5b351f0789', '5c5b351e4fba', '5c5b351e69ff', '5c5b351e8ab6', '5c5b351ebda1', '5c5b351eb2f2', '5c5b351e8cbe', '5c5b351eb47d', '5c5b351eb46e', '5c5b351e94e3', '5c5b351e7611', '5c5b351f03fb', '5c5b351f6814', '5c5b351e9aa1', '5c5b351f09b4', '5c5b351e942a', '5c5b351e970e', '5c5b351e974a', '5c5b351f0275', '5c5b351f0680', '5c5b351e866a', '5c5b351ebdd3', '5c5b351eee0c', '5c5b351ef89d', '5c5b351ebec3', '5c5b351f4a28', '5c5b351e688d', '5c5b351e95fb', '5c5b351f5761', '5c5b351f1828', '5c5b351e9399', '5c5b351e8ea8', '5c5b351f24bc', '5c5b351e914b', '5c5b351e9777', '5c5b351f32db', '5c5b351f111b', '5c5b351ebafe', '5c5b351e2580', '5c5b351f04c8', '5c5b351f3d6c', '5c5b351e8e8f', '5c5b351eacc1', '5c5b351e70b7', '5c5b351ebbf3', '5c5b351f4b8b', '5c5b351f0554', '5c5b351f69d1', '5c5b351f6710', '5c5b351e8674', '5c5b351f6170', '5c5b351e9781', '5c5b351f6b5c', '5c5b351f485c', '5c5b351e6edc', '5c5b351e8101', '5c5b351f5932', '5c5b351f6ac1', '5c5b351f0cf7', '5c5b351e9993', '5c5b351eb617', '5c5b351f64ea', '5c5b351e8df9', '5c5b351e23f5', '5c5b351f0e41', '5c5b351f617f', '5c5b351e99e8', '5c5b351e72ec', '5c5b351ebdf6', '5c5b351e98a8', '5c5b351ebf81', '5c5b351e7cec', '5c5b351eb275', '5c5b351e7ef9', '5c5b351e24f9', '5c5b351f5905', '5c5b351e8e5d', '5c5b351f1f03', '5c5b351f1f21', '5c5b351e8ec1', '5c5b351e6707', '5c5b351efaaf', '5c5b351f03dd', '5c5b351e9aba', '5c5b351f6256', '5c5b351f7796', '5c5b351e8cc3', '5c5b351e7161', '5c5b351e98df', '5c5b351f3ace', '5c5b351e99cf', '5c5b351f696d', '5c5b351ebe64', '5c5b351e9a5b', '5c5b351ea84d', '5c5b351e8bc4', '5c5b351f2011', '5c5b351ebda6', '5c5b351f3ca9', '5c5b351f3853', '5c5b351f3d7b', '5c5b351f3597', '5c5b351f049b', '5c5b351f58f6', '5c5b351e7e31', '5c5b351f1846', '5c5b351e93c6', '5c5b351e9150', '5c5b351f6e09', '5c5b351e9682', '5c5b351f0932', '5c5b351e96d2', '5c5b351e8d09', '5c5b351e8d18', '5c5b351f74e9', '5c5b351e2445', '5c5b351e7d23', '5c5b351f0c70', '5c5b351f3d03', '5c5b351e721f', '5c5b351f091e', '5c5b351ebf7c', '5c5b351e7cc9', '5c5b351e96d7', '5c5b351f1a49', '5c5b351f12ba', '5c5b351e910f', '5c5b351e738c', '5c5b351e2576', '5c5b351ebe96', '5c5b351f3c54', '5c5b351ef8b6', '5c5b351f6e8b', '5c5b351f0847', '5c5b351f6b34', '5c5b351e8b1f', '5c5b351f5621', '5c5b351f1b0c', '5c5b351e9871', '5c5b351e8322', '5c5b351f6e86', '5c5b351f6a17', '5c5b351f7548', '5c5b351f355b', '5c5b351f1cb5', '5c5b351f3b55', '5c5b351f1f12', '5c5b351f654e', '5c5b351f68aa', '5c5b351e8435', '5c5b351ef893', '5c5b351f65ee', '5c5b351e8fc5', '5c5b351e690a', '5c5b351f0cd4', '5c5b351f67ba', '5c5b351f39f2', '5c5b351f67f1', '5c5b351f37f4', '5c5b351f07ca', '5c5b351e7d73', '5c5b351efa41', '5c5b351e9510', '5c5b351f3830', '5c5b351e93fd', '5c5b351e806b', '5c5b351f183c', '5c5b351efb04', '5c5b351e23cd', '5c5b351ebc3e', '5c5b351e97f9', '5c5b351f4b9a', '5c5b351e6964', '5c5b351f6611', '5c5b351e6ba8', '5c5b351ebe19', '5c5b351e8d3b', '5c5b351ef898', '5c5b351e913c', '5c5b351f19db', '5c5b351f68c8', '5c5b351e7eef', '5c5b351f2043', '5c5b351e91fa', '5c5b351f036f', '5c5b351e24fe', '5c5b351f24b2', '5c5b351f65e4', '5c5b351f0a9f', '5c5b351e9907', '5c5b351f74a3', '5c5b351e66df', '5c5b351f5603', '5c5b351f0608', '5c5b351ebe46', '5c5b351f0446', '5c5b351ebf0e', '5c5b351e97fe', '5c5b351e96a5', '5c5b351e83ea', '5c5b351f6b07', '5c5b351f0c57', '5c5b351e8f34', '5c5b351f04a5', '5c5b351e9330', '5c5b351f6bd4', '5c5b351ebd01', '5c5b351efb6d', '5c5b351f088d', '5c5b351eeb96', '5c5b351f6152', '5c5b351f5fcc', '5c5b351f1c33', '5c5b351e9105', '5c5b351f0842', '5c5b351f2e5d', '5c5b351e8020', '5c5b351f0e2d', '5c5b351e6dab', '5c5b351f3bc8', '5c5b351e2413', '5c5b351e7e63', '5c5b351ef87a', '5c5b351e9727', '5c5b351f5cd4', '5c5b351e9295', '5c5b351eee11', '5c5b351ebf40', '5c5b351e974f', '5c5b351f0d6a', '5c5b351f7390', '5c5b351f72c8', '5c5b351f34e3', '5c5b351f08d3', '5c5b351eba27', '5c5b351e9920', '5c5b351e6c66', '5c5b351ebc16', '5c5b351f07d4', '5c5b351f18aa', '5c5b351e9420', '5c5b351e7f9e', '5c5b351e27ec', '5c5b351f752a', '5c5b351eec72', '5c5b351f36a5', '5c5b351f6b25', '5c5b351f200c', '5c5b351f31b9', '5c5b351f04f5', '5c5b351f37ef', '5c5b351f3b0a', '5c5b351e93b2', '5c5b351f613e', '5c5b351f185f', '5c5b351f1ebd', '5c5b351eb3d8', '5c5b351f6909', '5c5b351f0694', '5c5b351e80e3', '5c5b351f318c', '5c5b351f0419', '5c5b351f678d', '5c5b351e6a90', '5c5b351ef9ce', '5c5b351e7e77', '5c5b351e912d', '5c5b351f29f8', '5c5b351e9290', '5c5b351f067b', '5c5b351f3a29', '5c5b351f06b2', '5c5b351e8cff', '5c5b351e7eb8', '5c5b351e66c6', '5c5b351e8fb6', '5c5b351ec071', '5c5b351ef938', '5c5b351e99c5', '5c5b351e8156', '5c5b351efabe', '5c5b351ef73f', '5c5b351f7507', '5c5b351e6eb9', '5c5b351ebbf8', '5c5b351e268e', '5c5b351f0da1', '5c5b351f6b02', '5c5b351e8f16', '5c5b351f3cb8', '5c5b351f125b', '5c5b351e684c', '5c5b351f65d5', '5c5b351f1b25', '5c5b351e9a60', '5c5b351ebc7f', '5c5b351f1ba7', '5c5b351e6d9c', '5c5b351f020c', '5c5b351f11cf', '5c5b351f0c84', '5c5b351f05b3', '5c5b351e9083', '5c5b351ef7da', '5c5b351eb49b', '5c5b351e9a1f', '5c5b351e9344', '5c5b351eed1c', '5c5b351f6774', '5c5b351f3c31', '5c5b351eebe1', '5c5b351e66b7', '5c5b351e929a', '5c5b351f3f2e', '5c5b351f7066', '5c5b351eaefb', '5c5b351f73bd', '5c5b351f4b77', '5c5b351f1e9a', '5c5b351f0518', '5c5b351e8ea3', '5c5b351eb3bf', '5c5b351e82af', '5c5b351eb3ba', '5c5b351f0748', '5c5b351e7f35', '5c5b351f6715', '5c5b351e7e8b', '5c5b351e93c1', '5c5b351e75e9', '5c5b351f1ea4', '5c5b351f5afe', '5c5b351f5af4', '5c5b351e824b', '5c5b351e9326', '5c5b351f19d6', '5c5b351f0810', '5c5b351ebd1f', '5c5b351e903d', '5c5b351e91d2', '5c5b351eeee8', '5c5b351eeea2', '5c5b351e7dc3', '5c5b351e6cb1', '5c5b351f6fdf', '5c5b351efa0f', '5c5b351ef71c', '5c5b351eaccb', '5c5b351f5b12', '5c5b351f215b', '5c5b351e981c', '5c5b351f736d', '5c5b351f667a', '5c5b351e97a4', '5c5b351f5c02', '5c5b351f57a7', '5c5b351f27a0', '5c5b351ebe73', '5c5b351f5775', '5c5b351e8c55', '5c5b351f5752', '5c5b351f6d46', '5c5b351e9254', '5c5b351e910a', '5c5b351f0469', '5c5b351f09c3', '5c5b351e8f75', '5c5b351e9155', '5c5b351eb428', '5c5b351e6f5e', '5c5b351f21f1', '5c5b351e6e78', '5c5b351f336c', '5c5b351eb581', '5c5b351f72d2', '5c5b351ebb8f', '5c5b351e8e94', '5c5b351e8016', '5c5b351eb53b', '5c5b351f6788', '5c5b351e2634', '5c5b351f108f', '5c5b351e9a65', '5c5b351f3c72', '5c5b351f36eb', '5c5b351e9358', '5c5b351e21ac', '5c5b351ebed2', '5c5b351eeec0', '5c5b351f7755', '5c5b351f02ed', '5c5b351e8d40', '5c5b351e7fe4', '5c5b351f040a', '5c5b351f70b6', '5c5b351e8de0', '5c5b351f18a5', '5c5b351e273d', '5c5b351f6ae9', '5c5b351e760c', '5c5b351f732c', '5c5b351e7c9c', '5c5b351eb77f', '5c5b351ebeaf', '5c5b351f1f08', '5c5b351e7481', '5c5b351eecc7', '5c5b351e902e', '5c5b351efa0a', '5c5b351f3a83', '5c5b351f5847', '5c5b351efa96', '5c5b351f0abd', '5c5b351ef93d', '5c5b351ef8c5', '5c5b351f0e19', '5c5b351f588d', '5c5b351f62f1', '5c5b351f08ba', '5c5b351e8d13', '5c5b351e5064', '5c5b351f18ff', '5c5b351f10f8', '5c5b351f768d', '5c5b351f4f5f', '5c5b351f20a2', '5c5b351e25ad', '5c5b351f021b', '5c5b351ebca2', '5c5b351f3268', '5c5b351e70cb', '5c5b351f03e7', '5c5b351e8c05', '5c5b351f02a2', '5c5b351e8ebc', '5c5b351e8d9a', '5c5b351eb6da', '5c5b351f02e3', '5c5b351ebd2e', '5c5b351f5a68', '5c5b351f0293', '5c5b351f5fb8', '5c5b351ea794', '5c5b351f6a53', '5c5b351f68be', '5c5b351e6ebe', '5c5b351f3d71', '5c5b351ebcf7', '5c5b351f3682', '5c5b351e66d0', '5c5b351f1f99', '5c5b351e24d1', '5c5b351f527f', '5c5b351efa2d', '5c5b351e8c41', '5c5b351f0545', '5c5b351e258f', '5c5b351f69f9', '5c5b351e8d4a', '5c5b351f20f2', '5c5b351e80cf', '5c5b351e8575', '5c5b351f3c68', '5c5b351f030b', '5c5b351f4ccb', '5c5b351efa5f', '5c5b351e933a', '5c5b351f1b20', '5c5b351eb9cd', '5c5b351f6bb1', '5c5b351f7598', '5c5b351e8dea', '5c5b351e6a54', '5c5b351e9687', '5c5b351eba72', '5c5b351e96cd', '5c5b351e9669', '5c5b351f0720', '5c5b351e99d4', '5c5b351e2139', '5c5b351e7f08', '5c5b351e2369', '5c5b351e866f', '5c5b351f1a6c', '5c5b351f31f5', '5c5b351e862e', '5c5b351e84ee', '5c5b351f36d7', '5c5b351f1bf7', '5c5b351e2742', '5c5b351e999d', '5c5b351efb81', '5c5b351f6869', '5c5b351f3358', '5c5b351f0e1e', '5c5b351e906a', '5c5b351e9367', '5c5b351f075c', '5c5b351f75b1', '5c5b351f3bc3', '5c5b351f677e', '5c5b351e81a1', '5c5b351f1184', '5c5b351f077f', '5c5b351f35e7', '5c5b351ebdc4', '5c5b351f1be3', '5c5b351f3c22', '5c5b351e969b', '5c5b351e9385', '5c5b351eb572', '5c5b351f4b13', '5c5b351f64b8', '5c5b351e6766', '5c5b351e7eb3', '5c5b351f0a04', '5c5b351f3beb', '5c5b351eedfd', '5c5b351f698b', '5c5b351f2282', '5c5b351f31eb', '5c5b351e8bf1', '5c5b351e6e5f', '5c5b351e7f85', '5c5b351e6c61', '5c5b351f06e4', '5c5b351f1ec2', '5c5b351f76bf', '5c5b351f591e', '5c5b351f660c', '5c5b351f1afd', '5c5b351f05f9', '5c5b351f5b08', '5c5b351f09aa', '5c5b351f68f5', '5c5b351e9542', '5c5b351ebea0', '5c5b351e9a15', '5c5b351e94fc', '5c5b351f07d9', '5c5b351f57b1', '5c5b351e24ea', '5c5b351eb9ff', '5c5b351e92e5', '5c5b351f781d', '5c5b351e83db', '5c5b351f05e0', '5c5b351f6693', '5c5b351e67ca', '5c5b351f3a92', '5c5b351f1eb3', '5c5b351ebe0a', '5c5b351f0914', '5c5b351f60ee', '5c5b351efb0e', '5c5b351e92c2', '5c5b351f6841', '5c5b351f4cc6', '5c5b351f5856', '5c5b351f6b0c', '5c5b351f4d84', '5c5b351e8769', '5c5b351eb379', '5c5b351f34bb', '5c5b351ebe1e', '5c5b351f577a', '5c5b351f262e', '5c5b351e6a95', '5c5b351f6e13', '5c5b351e8e03', '5c5b351e8741', '5c5b351f04aa', '5c5b351f1e31', '5c5b351e6f0e', '5c5b351f2089', '5c5b351e8647', '5c5b351f598c', '5c5b351f3a2e', '5c5b351f022a', '5c5b351e8174', '5c5b351e983a', '5c5b351e7a8f', '5c5b351e7279', '5c5b351e908d', '5c5b351e241d', '5c5b351ef9d8', '5c5b351efb77', '5c5b351e97e5', '5c5b351f02b1', '5c5b351f3669', '5c5b351f06b7', '5c5b351e78fa', '5c5b351e7f80', '5c5b351e7f49', '5c5b351f0617', '5c5b351e85e3', '5c5b351f3524', '5c5b351f6585', '5c5b351e923b', '5c5b351e6752', '5c5b351e6c9d', '5c5b351f3646', '5c5b351ebe05', '5c5b351f3be6', '5c5b351e521c', '5c5b351e8ffc', '5c5b351e93bc', '5c5b351f4843', '5c5b351f1927', '5c5b351e7cc4', '5c5b351e9231', '5c5b351f0833', '5c5b351e95d3', '5c5b351e2382', '5c5b351f08dd', '5c5b351e85f2', '5c5b351f603f', '5c5b351e7af8', '5c5b351e8c9b', '5c5b351f0356', '5c5b351e6b1c', '5c5b351e730a', '5c5b351e98b7', '5c5b351e9a51', '5c5b351eec59', '5c5b351e8dae', '5c5b351f3957', '5c5b351f49f1', '5c5b351f748f', '5c5b351f596e', '5c5b351ebf6d', '5c5b351f060d', '5c5b351e9308', '5c5b351f040f', '5c5b351f58b0', '5c5b351f68d2', '5c5b351f76fb', '5c5b351f7499', '5c5b351ef9fb', '5c5b351eec27', '5c5b351e8480', '5c5b351e511d', '5c5b351f0c5c', '5c5b351f673d', '5c5b351f3a6a', '5c5b351f7426', '5c5b351ebf4f', '5c5b351f04fa', '5c5b351e936c', '5c5b351f12b5', '5c5b351f6bde', '5c5b351ef875', '5c5b351f7485', '5c5b351e980d', '5c5b351f07fc', '5c5b351f1eb8', '5c5b351e917d', '5c5b351f223c', '5c5b351f3948', '5c5b351ebc6b', '5c5b351eb54a', '5c5b351f739f', '5c5b351f2197', '5c5b351e7661', '5c5b351eb509', '5c5b351eb21b', '5c5b351ebcb6', '5c5b351f27af', '5c5b351e9092', '5c5b351f749e', '5c5b351e66d5', '5c5b351f01f3', '5c5b351e9673', '5c5b351f701b', '5c5b351f02b6', '5c5b351f5aa9', '5c5b351f3aab', '5c5b351f0838', '5c5b351f469f', '5c5b351e74d6', '5c5b351e2666', '5c5b351f778c', '5c5b351f76e7', '5c5b351f0c20', '5c5b351f6738', '5c5b351e98d5', '5c5b351e90bf', '5c5b351f68e6', '5c5b351f5b49', '5c5b351f18f0', '5c5b351f32cc', '5c5b351f7827', '5c5b351f0851', '5c5b351e6946', '5c5b351f0a86', '5c5b351f5fbd', '5c5b351f39f7', '5c5b351e8606', '5c5b351f6760', '5c5b351f05f4', '5c5b351ebe5f', '5c5b351f07c5', '5c5b351e930d', '5c5b351e9970', '5c5b351e971d', '5c5b351e708a', '5c5b351ebcca', '5c5b351f3ae2', '5c5b351ef8fc', '5c5b351f05e5', '5c5b351e9add', '5c5b351f6670', '5c5b351f5a0e', '5c5b351e9ad8', '5c5b351e9a0b', '5c5b351f3c2c', '5c5b351e80f7', '5c5b351f0aef', '5c5b351f3812', '5c5b351f6576', '5c5b351f1f44', '5c5b351ebab8', '5c5b351f07ac', '5c5b351f6bc0', '5c5b351e8f2f', '5c5b351f39d9', '5c5b351f561c', '5c5b351e993e', '5c5b351e6bfd', '5c5b351e2454', '5c5b351eb68a', '5c5b351e8b0b', '5c5b351e8c5a', '5c5b351eeed4', '5c5b351f3c7c', '5c5b351f77a0', '5c5b351eb540', '5c5b351f0d88', '5c5b351e96eb', '5c5b351e84a3', '5c5b351e7adf', '5c5b351e90f6', '5c5b351e9745', '5c5b351f73a4', '5c5b351ebe0f', '5c5b351efad2', '5c5b351eb63f', '5c5b351f2110', '5c5b351e811a', '5c5b351f20ac', '5c5b351e925e', '5c5b351f36c8', '5c5b351f6503', '5c5b351f0a45', '5c5b351e8e71', '5c5b351f6846', '5c5b351e915a', '5c5b351f074d', '5c5b351f08fb', '5c5b351e7b84', '5c5b351e8179', '5c5b351f6634', '5c5b351efb13', '5c5b351e7ed6', '5c5b351f3baf', '5c5b351f0315', '5c5b351e9722', '5c5b351f054f', '5c5b351e9628', '5c5b351f2106', '5c5b351f1a7b', '5c5b351f66fc', '5c5b351ebc61', '5c5b351e8cfa', '5c5b351e988a', '5c5b351e8ead', '5c5b351f70ac', '5c5b351e6afe', '5c5b351ebd24', '5c5b351f3cb3', '5c5b351f094b', '5c5b351e8444', '5c5b351ebb12', '5c5b351e7ea9', '5c5b351f5b21', '5c5b351e7085', '5c5b351f0a63', '5c5b351e916e', '5c5b351f0612', '5c5b351f084c', '5c5b351f113e', '5c5b351f4f19', '5c5b351e838b', '5c5b351f6a5d', '5c5b351f3afb', '5c5b351f5b94', '5c5b351e23fa', '5c5b351f6b4d', '5c5b351e7ce2', '5c5b351e8c0f', '5c5b351f5c4d', '5c5b351ea81b', '5c5b351f55cc', '5c5b351f7417', '5c5b351f1eae', '5c5b351f6995', '5c5b351e8e58', '5c5b351e9213', '5c5b351f34ca', '5c5b351e94de', '5c5b351f1e3b', '5c5b351e25cb', '5c5b351e978b', '5c5b351f68a0', '5c5b351eeebb', '5c5b351f0c4d', '5c5b351f5fae', '5c5b351f6643', '5c5b351e69f0', '5c5b351e216b', '5c5b351f65f8', '5c5b351f077a', '5c5b351efa1e', '5c5b351f58ce', '5c5b351f6a8f', '5c5b351e99fc', '5c5b351e24ae', '5c5b351e68dd', '5c5b351e4f3d', '5c5b351e25e9', '5c5b351f18e6', '5c5b351eb3b5', '5c5b351f7476', '5c5b351e85a7', '5c5b351e279c', '5c5b351eb531', '5c5b351e2657', '5c5b351e96f0', '5c5b351f0365', '5c5b351e844e', '5c5b351e85d4', '5c5b351e7765', '5c5b351e9a42', '5c5b351e7170', '5c5b351ead8e', '5c5b351f333f', '5c5b351f2124', '5c5b351f1deb', '5c5b351e986c', '5c5b351f6d28', '5c5b351e8395', '5c5b351f024d', '5c5b351f0bad', '5c5b351e7fd5', '5c5b351f127e', '5c5b351e928b', '5c5b351e7de1', '5c5b351f76d8', '5c5b351e73fa', '5c5b351f757a', '5c5b351f7408', '5c5b351e98f3', '5c5b351f0892', '5c5b351e9939', '5c5b351f07f7', '5c5b351e94cf', '5c5b351f5784', '5c5b351f57bb', '5c5b351e9394', '5c5b351e8e30', '5c5b351e26a7', '5c5b351e7fbc', '5c5b351e6793', '5c5b351f360f', '5c5b351f5adb', '5c5b351e9a1a', '5c5b351f3899', '5c5b351e7d87', '5c5b351f7859', '5c5b351f06cb', '5c5b351e6ee1', '5c5b351e67d4', '5c5b351f6b98', '5c5b351f4b90', '5c5b351e8ec6', '5c5b351f6756', '5c5b351e8df4', '5c5b351e8c23', '5c5b351e8f7a', '5c5b351f34e8', '5c5b351efb63', '5c5b351e6bc1', '5c5b351e679d', '5c5b351f1ce2', '5c5b351e9844', '5c5b351e9a33', '5c5b351e960a', '5c5b351f6224', '5c5b351f059f', '5c5b351f5694', '5c5b351f132d', '5c5b351e753f', '5c5b351f685a', '5c5b351f6c60', '5c5b351e6798', '5c5b351f7061', '5c5b351f59af', '5c5b351e84cb', '5c5b351e6720', '5c5b351eb234', '5c5b351e8f3e', '5c5b351f36c3', '5c5b351eb84c', '5c5b351e92f4', '5c5b351f3e34', '5c5b351f58ba', '5c5b351f7070', '5c5b351eb26b', '5c5b351f1a21', '5c5b351f5b85', '5c5b351f6260', '5c5b351f12ab', '5c5b351e8db3', '5c5b351f0c61', '5c5b351f18eb', '5c5b351f73db', '5c5b351efa46', '5c5b351f2c8c', '5c5b351e8ce1', '5c5b351e8dd6', '5c5b351efa23', '5c5b351e8c69', '5c5b351eeb9b', '5c5b351f6a44', '5c5b351eee6b', '5c5b351e7283', '5c5b351ead1b', '5c5b351f06bc', '5c5b351f04e6', '5c5b351efadc', '5c5b351f58b5', '5c5b351f086a', '5c5b351e8f98', '5c5b351f60bc', '5c5b351f0487', '5c5b351f6daf', '5c5b351f0ce8', '5c5b351f3529', '5c5b351e2616', '5c5b351f1d46', '5c5b351f0513', '5c5b351e85fc', '5c5b351eb563', '5c5b351f3c3b', '5c5b351e6c43', '5c5b351f5abd', '5c5b351e8c37', '5c5b351eb351', '5c5b351f6e40', '5c5b351f5ae5', '5c5b351ef910', '5c5b351e98bc', '5c5b351f0603', '5c5b351f6b89', '5c5b351eb2cf', '5c5b351f585b', '5c5b351f5aea', '5c5b351e8e44', '5c5b351f199a', '5c5b351f6cba', '5c5b351f0987', '5c5b351f4866', '5c5b351e80e8', '5c5b351e25c1', '5c5b351ebbb7', '5c5b351e9619', '5c5b351e9abf', '5c5b351e2558', '5c5b351e900b', '5c5b351e96a0', '5c5b351ea7ee', '5c5b351f0491', '5c5b351f3d1c', '5c5b351f0978', '5c5b351ebf27', '5c5b351f1ac1', '5c5b351f090a', '5c5b351e95a1', '5c5b351f3bcd', '5c5b351f6aa8', '5c5b351e9a88', '5c5b351f3d12', '5c5b351f0739', '5c5b351eb3f1', '5c5b351efaff', '5c5b351f671f', '5c5b351e68c9', '5c5b351eb487', '5c5b351f064e', '5c5b351f370e', '5c5b351f080b', '5c5b351f3727', '5c5b351e707b', '5c5b351e964b', '5c5b351e95ce', '5c5b351e7d6e', '5c5b351f0a95', '5c5b351f6bf7', '5c5b351ebc11', '5c5b351f050e', '5c5b351f05b8', '5c5b351f0397', '5c5b351e8ecb', '5c5b351e7c88', '5c5b351f0559', '5c5b351f487f', '5c5b351f5ff9', '5c5b351f7025', '5c5b351e6941', '5c5b351e7f71', '5c5b351f128d', '5c5b351f35fb', '5c5b351e98cb', '5c5b351f67fb', '5c5b351f6805', '5c5b351f0333', '5c5b351f1e36', '5c5b351e9597', '5c5b351e8dc2', '5c5b351e9353', '5c5b351e8fac', '5c5b351f1f71', '5c5b351f6e4f', '5c5b351e9a56', '5c5b351efaeb', '5c5b351f5ec3', '5c5b351f6a0d', '5c5b351f022f', '5c5b351f7395', '5c5b351f05ea', '5c5b351e875f', '5c5b351ef8f2', '5c5b351e7229', '5c5b351ef9e7', '5c5b351f1cbf', '5c5b351f76a1', '5c5b351efb68', '5c5b351e4f60', '5c5b351f70a7', '5c5b351f1cce', '5c5b351f0897', '5c5b351f06c1', '5c5b351f39ed', '5c5b351e6f3b', '5c5b351ebf86', '5c5b351f2e4e', '5c5b351f739a', '5c5b351e839a', '5c5b351e8e2b', '5c5b351f211f', '5c5b351e69d2', '5c5b351f04ff', '5c5b351e8cd2', '5c5b351f5e14', '5c5b351e7062', '5c5b351f02d9', '5c5b351f6c97', '5c5b351e987b', '5c5b351e236e', '5c5b351e27a6', '5c5b351eb423', '5c5b351f1f3a', '5c5b351e93f8', '5c5b351f4f41', '5c5b351e8cf0', '5c5b351e8f5c', '5c5b351f01ee', '5c5b351f6adf', '5c5b351f1a5d', '5c5b351eec31', '5c5b351f56ee', '5c5b351f775f', '5c5b351e523a', '5c5b351f5fe5', '5c5b351f130f', '5c5b351eb324', '5c5b351e7ffd', '5c5b351f0752', '5c5b351f0d9c', '5c5b351f1e7c', '5c5b351ebe82', '5c5b351f3817', '5c5b351e90ec', '5c5b351f6913', '5c5b351efb22', '5c5b351e802a', '5c5b351f676a', '5c5b351e8bab', '5c5b351ebc75', '5c5b351f5fd6', '5c5b351e69d7', '5c5b351f3664', '5c5b351e9a4c', '5c5b351f031f', '5c5b351e83fe', '5c5b351f0cc0', '5c5b351f392a', '5c5b351f6cab', '5c5b351ebd06', '5c5b351e91b9', '5c5b351f0207', '5c5b351e66bc', '5c5b351f3844', '5c5b351f72a5', '5c5b351ebb4e', '5c5b351ef7e9', '5c5b351e8c8c', '5c5b351e8eb7', '5c5b351e84c6', '5c5b351e93a3', '5c5b351f227d', '5c5b351e911e', '5c5b351f46a4', '5c5b351f6f30', '5c5b351e7eea', '5c5b351e23f0', '5c5b351e95b0', '5c5b351e8caa', '5c5b351e968c', '5c5b351e9a10', '5c5b351f08b0', '5c5b351f77f5', '5c5b351e9173', '5c5b351f04c3', '5c5b351e8fe8', '5c5b351eeb82', '5c5b351f100d', '5c5b351f74bc', '5c5b351f7818', '5c5b351ef72b', '5c5b351f6df5', '5c5b351e9ae2', '5c5b351f6ba2', '5c5b351f6625', '5c5b351f34b6', '5c5b351eb3d3', '5c5b351e2544', '5c5b351eeb78', '5c5b351f1d32', '5c5b351f743a', '5c5b351e235a', '5c5b351ebbe9', '5c5b351f69ef', '5c5b351f1a58', '5c5b351e8278', '5c5b351f1ecc', '5c5b351f608f', '5c5b351e69aa', '5c5b351f3c6d', '5c5b351f5aa4', '5c5b351eb644', '5c5b351f03c4', '5c5b351e9aab', '5c5b351f05cc', '5c5b351ebe37', '5c5b351f4b72', '5c5b351e691e', '5c5b351f061c', '5c5b351e25a3', '5c5b351e982b', '5c5b351f05d1', '5c5b351f3dad', '5c5b351f076b', '5c5b351f738b', '5c5b351f6dc8', '5c5b351f1b4d', '5c5b351f12fb', '5c5b351f7813', '5c5b351f60d5', '5c5b351f1f85', '5c5b351f6cfb', '5c5b351f4ce4', '5c5b351f052c', '5c5b351f4bc2', '5c5b351f3a10', '5c5b351f6b16', '5c5b351e73a5', '5c5b351ef8c0', '5c5b351e858e', '5c5b351f1a3f', '5c5b351f76ec', '5c5b351f5ba3', '5c5b351e8c00', '5c5b351eb441', '5c5b351f0a68', '5c5b351f1b84', '5c5b351f6b43', '5c5b351f06a8', '5c5b351f3baa', '5c5b351f204d', '5c5b351f5b53', '5c5b351f0a4a', '5c5b351f6c3d', '5c5b351f3f60', '5c5b351f384e', '5c5b351e8133', '5c5b351eadac', '5c5b351f56ad', '5c5b351f029d', '5c5b351eed80', '5c5b351ea942', '5c5b351e674d', '5c5b351e96c3', '5c5b351f05db', '5c5b351f5a13', '5c5b351e8fa2', '5c5b351e9551', '5c5b351efa82', '5c5b351ead5c', '5c5b351e23dc', '5c5b351f6d41', '5c5b351e90a1', '5c5b351f17fb', '5c5b351e92a9', '5c5b351f032e', '5c5b351ebcc0', '5c5b351e24bd', '5c5b351e9aec', '5c5b351e25bc', '5c5b351f74d5', '5c5b351e9a2e', '5c5b351e6d06', '5c5b351f04f0', '5c5b351f771e', '5c5b351f02c5', '5c5b351f6ff8', '5c5b351ebc0c', '5c5b351e8e99', '5c5b351f0a22', '5c5b351e8138', '5c5b351f0bd5', '5c5b351e7d05', '5c5b351e8426', '5c5b351e6789', '5c5b351ebc2f', '5c5b351e86c9', '5c5b351f0973', '5c5b351f3a4c', '5c5b351e94ed', '5c5b351efa91', '5c5b351f77aa', '5c5b351e92d6', '5c5b351f6a58', '5c5b351f0829', '5c5b351e9803', '5c5b351f06a3', '5c5b351eb9f5', '5c5b351f3af6', '5c5b351f038d', '5c5b351eb3c4', '5c5b351e275b', '5c5b351e91b4', '5c5b351f1837', '5c5b351e8f4d', '5c5b351ef956', '5c5b351f691d', '5c5b351e6e05', '5c5b351f249e', '5c5b351f1ea9', '5c5b351f0329', '5c5b351f08ce', '5c5b351f6c6a', '5c5b351e6ae5', '5c5b351e255d', '5c5b351f6d05', '5c5b351f6233', '5c5b351f033d', '5c5b351e7e81', '5c5b351e9a8d', '5c5b351eb51d', '5c5b351f671a', '5c5b351f3d26', '5c5b351efb54', '5c5b351f09fa', '5c5b351f09be', '5c5b351e956f', '5c5b351ec003', '5c5b351f6495', '5c5b351f0ed7', '5c5b351e81f6', '5c5b351e9a9c', '5c5b351ef9b0', '5c5b351f1f94', '5c5b351ef906', '5c5b351f198b', '5c5b351e7ea4', '5c5b351f4c35', '5c5b351ebdfb', '5c5b351ebe4b', '5c5b351f4e1a', '5c5b351f37a4', '5c5b351e8638', '5c5b351f76d3', '5c5b351f73cc', '5c5b351f5bad', '5c5b351f1fad', '5c5b351e8147', '5c5b351e7463', '5c5b351e276a', '5c5b351f1dd7', '5c5b351efab9', '5c5b351f650d', '5c5b351f69a9', '5c5b351f75ac', '5c5b351f579d', '5c5b351f0239', '5c5b351e8601', '5c5b351e7fad', '5c5b351f6b52', '5c5b351e7d9b', '5c5b351e9740', '5c5b351f1986', '5c5b351e99ac', '5c5b351e7729', '5c5b351e9623', '5c5b351e8318', '5c5b351ef965', '5c5b351e8c91', '5c5b351e764d', '5c5b351e8a6b', '5c5b351f34ac', '5c5b351e8fc0', '5c5b351e8ae3', '5c5b351eb405', '5c5b351ebacc', '5c5b351f3a8d', '5c5b351e7f03', '5c5b351f2115', '5c5b351e99a2', '5c5b351f67ec', '5c5b351e84d0', '5c5b351eb310', '5c5b351e7742', '5c5b351e93e9', '5c5b351f6792', '5c5b351f1251', '5c5b351e96af', '5c5b351e8d36', '5c5b351f679c', '5c5b351f5d2e', '5c5b351e85e8', '5c5b351f4c08', '5c5b351e90e7', '5c5b351e25b2', '5c5b351f01df', '5c5b351f2a07', '5c5b351f09af', '5c5b351f3a01', '5c5b351f6986', '5c5b351f08e2', '5c5b351f734f', '5c5b351e2698', '5c5b351e97db', '5c5b351f1864', '5c5b351efaaa', '5c5b351f2e85', '5c5b351e6b76', '5c5b351e8a75', '5c5b351f0879', '5c5b351f6490', '5c5b351f5c3e', '5c5b351f6003', '5c5b351e9984', '5c5b351ebd5b', '5c5b351e985d', '5c5b351f6553', '5c5b351e9966', '5c5b351e873c', '5c5b351e8d7c', '5c5b351efaa5', '5c5b351e7ba2', '5c5b351f72c3', '5c5b351f0504', '5c5b351f69c2', '5c5b351e814c', '5c5b351e8ff2', '5c5b351f0455', '5c5b351f67d8', '5c5b351f59c3', '5c5b351f34fc', '5c5b351f2e6c', '5c5b351ebcbb', '5c5b351e85bb', '5c5b351ec017', '5c5b351ef951', '5c5b351f02ac', '5c5b351e9a06', '5c5b351f383a', '5c5b351eb496', '5c5b351f77e1', '5c5b351e719d', '5c5b351eb419', '5c5b351e8db8', '5c5b351e9655', '5c5b351eb4a5', '5c5b351ef942', '5c5b351e8304', '5c5b351e7f12', '5c5b351e6a6d', '5c5b351e7d28', '5c5b351e67a2', '5c5b351e7d78', '5c5b351f6de6', '5c5b351f095a', '5c5b351ebc1b', '5c5b351e7346', '5c5b351e761b', '5c5b351f6c51', '5c5b351ebe78', '5c5b351f3925', '5c5b351f3c09', '5c5b351f2061', '5c5b351e934e', '5c5b351e8561', '5c5b351e7e59', '5c5b351e9123', '5c5b351f20cf', '5c5b351e8610', '5c5b351f1ae4', '5c5b351f3c95', '5c5b351e9821', '5c5b351f5fc7', '5c5b351e9560', '5c5b351f3aa6', '5c5b351e9277', '5c5b351efa8c', '5c5b351e9637', '5c5b351e74e5', '5c5b351f1c06', '5c5b351f2179', '5c5b351e7107', '5c5b351e7e90', '5c5b351f70cf', '5c5b351e8caf', '5c5b351e7738', '5c5b351efa3c', '5c5b351efa4b', '5c5b351f6c8d', '5c5b351f06df', '5c5b351f6724', '5c5b351ebcfc', '5c5b351f0874', '5c5b351f6c74', '5c5b351e8ccd', '5c5b351f0473', '5c5b351e8cf5', '5c5b351e84b2', '5c5b351efa78', '5c5b351f2471', '5c5b351f6008', '5c5b351e8cb4', '5c5b351e9a74', '5c5b351e8043', '5c5b351eb432', '5c5b351efae1', '5c5b351f6f99', '5c5b351f3d30', '5c5b351efb2c', '5c5b351f2caa', '5c5b351efa50', '5c5b351f035b', '5c5b351f6c10', '5c5b351f6e2c', '5c5b351f33bc', '5c5b351e5217', '5c5b351e7cf6', '5c5b351f7525', '5c5b351e7076', '5c5b351f08c4', '5c5b351f62ba', '5c5b351ef97e', '5c5b351f08e7', '5c5b351f6b48', '5c5b351f644f', '5c5b351e9989', '5c5b351f03c9', '5c5b351f10e9', '5c5b351f092d', '5c5b351f597d', '5c5b351f182d', '5c5b351e9524', '5c5b351f34a7', '5c5b351f0964', '5c5b351f35e2', '5c5b351f75cf', '5c5b351eb4ff', '5c5b351ef776', '5c5b351e6c11', '5c5b351e520d', '5c5b351f6b7a', '5c5b351e80b6', '5c5b351f6ae4', '5c5b351f330d', '5c5b351e6be4', '5c5b351f2683', '5c5b351f01d5', '5c5b351e90f1', '5c5b351e8f39', '5c5b351e9ab0', '5c5b351eb518', '5c5b351e9a24', '5c5b351e9641', '5c5b351f4c44', '5c5b351f2052', '5c5b351f3772', '5c5b351f0856', '5c5b351e2756', '5c5b351f08a6', '5c5b351f0865', '5c5b351e66e9', '5c5b351e67f7', '5c5b351e8ee9', '5c5b351ef91f', '5c5b351e954c', '5c5b351ef9b5', '5c5b351ef9dd', '5c5b351e965f', '5c5b351f02a7', '5c5b351f0388', '5c5b351f0644', '5c5b351e9759', '5c5b351f0743', '5c5b351f6b9d', '5c5b351e8633', '5c5b351e7562', '5c5b351f3e0c', '5c5b351ebb5d', '5c5b351ef604', '5c5b351ebadb', '5c5b351e93d0', '5c5b351f5b58', '5c5b351efa00', '5c5b351f6210', '5c5b351e9137', '5c5b351e6e1e', '5c5b351f09f5', '5c5b351f0888', '5c5b351eeeca', '5c5b351e96e1', '5c5b351e6c16', '5c5b351f6c0b', '5c5b351eb306', '5c5b351e2562', '5c5b351f6878', '5c5b351f3c86', '5c5b351e856b', '5c5b351f6d8c', '5c5b351f7692', '5c5b351f31f0', '5c5b351e97e0', '5c5b351f02c0', '5c5b351f761f', '5c5b351e843f', '5c5b351eb5cc', '5c5b351f67ce', '5c5b351f20a7', '5c5b351f59d2', '5c5b351f60c6', '5c5b351efb1d', '5c5b351e901f', '5c5b351e6dc4', '5c5b351f0711', '5c5b351f1b11', '5c5b351f65fd', '5c5b351e6842', '5c5b351ef8e8', '5c5b351f06fd', '5c5b351e8d81', '5c5b351f6df0', '5c5b351f3ce0', '5c5b351f0a4f', '5c5b351f31be', '5c5b351f6d5f', '5c5b351f129c', '5c5b351e9362', '5c5b351f6751', '5c5b351e7ef4', '5c5b351e98da', '5c5b351e26cf', '5c5b351e2206', '5c5b351e997f', '5c5b351f7430', '5c5b351e8106', '5c5b351f6922', '5c5b351e83a4', '5c5b351f1e2c', '5c5b351f5bf8', '5c5b351eb3f6', '5c5b351f6d23', '5c5b351eb4c3', '5c5b351e7f7b', '5c5b351e7189', '5c5b351e52e4', '5c5b351eb595', '5c5b351f3a33', '5c5b351ebf54', '5c5b351f6832', '5c5b351e6919', '5c5b351e7fc6', '5c5b351f5630', '5c5b351f0d60', '5c5b351e7d5a', '5c5b351e926d', '5c5b351f6acb', '5c5b351f03bf', '5c5b351eb437', '5c5b351e9588', '5c5b351f3a65', '5c5b351ebea5', '5c5b351f68f0', '5c5b351f4ba9', '5c5b351f0432', '5c5b351e8467', '5c5b351e9100', '5c5b351f2589', '5c5b351ef8de', '5c5b351f02fc', '5c5b351e8f70', '5c5b351efa7d', '5c5b351f045f', '5c5b351efa73', '5c5b351eee8e', '5c5b351e677f', '5c5b351f788b', '5c5b351e9411', '5c5b351e8c14', '5c5b351e898f', '5c5b351f36af', '5c5b351f546e', '5c5b351f6cb0', '5c5b351f4852', '5c5b351f0d3d', '5c5b351e2495', '5c5b351f1e81', '5c5b351f1e4f', '5c5b351f6e36', '5c5b351f1dcd', '5c5b351f3632', '5c5b351f17f1', '5c5b351ef929', '5c5b351e6716', '5c5b351e7b2f', '5c5b351f04af', '5c5b351e8f84', '5c5b351f21dd', '5c5b351f48e8', '5c5b351e5104', '5c5b351f03ec', '5c5b351f31fa', '5c5b351e261b', '5c5b351efb3b', '5c5b351efb7c', '5c5b351e6d6f', '5c5b351e66f8', '5c5b351f211a', '5c5b351e83b8', '5c5b351f078e', '5c5b351f6af3', '5c5b351eed9e', '5c5b351f24ee', '5c5b351f6b75', '5c5b351ef870', '5c5b351e989e', '5c5b351f6d1e', '5c5b351e871e', '5c5b351f37e5', '5c5b351ec008', '5c5b351f0635', '5c5b351f5ad6', '5c5b351f0761', '5c5b351e736e', '5c5b351e690f', '5c5b351e8458', '5c5b351e8ac5', '5c5b351e251c', '5c5b351e87a0', '5c5b351e673e', '5c5b351f379f', '5c5b351f59c8', '5c5b351f695e', '5c5b351f1e6d', '5c5b351e9808', '5c5b351e98f8', '5c5b351f1f67', '5c5b351f0310', '5c5b351ebcd4', '5c5b351f1319', '5c5b351f6cc4', '5c5b351efb4a', '5c5b351f1b02', '5c5b351f4a0a', '5c5b351f0522', '5c5b351e8dfe', '5c5b351e72ab', '5c5b351f09a0', '5c5b351f73fe', '5c5b351e7ca6', '5c5b351f1bde', '5c5b351eba81', '5c5b351e7d1e', '5c5b351e7099', '5c5b351e7e9a', '5c5b351f07a7', '5c5b351f687d', '5c5b351e96e6', '5c5b351f0c75', '5c5b351e52a3', '5c5b351ef8cf', '5c5b351e8e6c', '5c5b351f10b7', '5c5b351f7624', '5c5b351e9222', '5c5b351eb9aa', '5c5b351f1940', '5c5b351f3a42', '5c5b351f2039', '5c5b351e8aed', '5c5b351f205c', '5c5b351f0496', '5c5b351e8def', '5c5b351f3c04', '5c5b351f0a54', '5c5b351f7697', '5c5b351f08f6', '5c5b351eb4eb', '5c5b351e8732', '5c5b351f1a30', '5c5b351e85b1', '5c5b351f1bc5', '5c5b351f6a9e', '5c5b351e6e6e', '5c5b351e972c', '5c5b351f7093', '5c5b351f066c', '5c5b351eb522', '5c5b351e52cb', '5c5b351e8e35', '5c5b351e23be', '5c5b351e97ea', '5c5b351f6b8e', '5c5b351eb590', '5c5b351e6815', '5c5b351f5fea', '5c5b351f6e9a', '5c5b351f64ef', '5c5b351e8039', '5c5b351f09a5', '5c5b351e6770', '5c5b351e7e7c', '5c5b351e938f', '5c5b351ebccf', '5c5b351f063f', '5c5b351ef96a', '5c5b351f721e', '5c5b351f586f', '5c5b351f735e', '5c5b351e6b58', '5c5b351f624c', '5c5b351f5ff4', '5c5b351f0d83', '5c5b351e9948', '5c5b351e9696', '5c5b351f72e6', '5c5b351ef8a7', '5c5b350eb221', '5c5b351e915f', '5c5b351f3cc2', '5c5b351f19cc', '5c5b351f7412', '5c5b351f1ec7', '5c5b351f0dab', '5c5b351f01fd', '5c5b351e8edf', '5c5b351f6d6e', '5c5b351e7652', '5c5b351f5b8f', '5c5b351e2481', '5c5b351f0cd9', '5c5b351f6512', '5c5b351e7f1c', '5c5b351f62d8', '5c5b351f20de', '5c5b351f6e81', '5c5b351f7895', '5c5b351f1f30', '5c5b351f045a', '5c5b351e66ee', '5c5b351f4a5f', '5c5b351e94f2', '5c5b351f67e2', '5c5b351f20bb', '5c5b351ea99c', '5c5b351f2007', '5c5b351f06ad', '5c5b351eb7ac', '5c5b351f6b6b', '5c5b351eb5ae', '5c5b351e9975', '5c5b351f1337', '5c5b351ef95b', '5c5b351f068a', '5c5b351e84e9', '5c5b351f3aec', '5c5b351e8f48', '5c5b351f0725', '5c5b351e9218', '5c5b351f036a', '5c5b351e992a', '5c5b351f222d', '5c5b351e8e17', '5c5b351e87d2', '5c5b351f581f', '5c5b351f0cbb', '5c5b351f2138', '5c5b351e977c', '5c5b351f059a', '5c5b351e8011', '5c5b351f1b16', '5c5b351e6810', '5c5b351e85c5', '5c5b351f0338', '5c5b351f66d4', '5c5b351f0734', '5c5b351ebc52', '5c5b351e9024', '5c5b351e90ba', '5c5b351f1bb1', '5c5b351f72cd', '5c5b351f5770', '5c5b351f3ab5', '5c5b351f669d', '5c5b351f6508', '5c5b351e8c28', '5c5b351e9a7e', '5c5b351f0252', '5c5b351e6c7a', '5c5b351f7863', '5c5b351ea7df', '5c5b351f04d2', '5c5b351f1f3f', '5c5b351f68b9', '5c5b351e681a', '5c5b351e8fd4', '5c5b351f4c94', '5c5b351eb36f', '5c5b351ebe41', '5c5b351f0685', '5c5b351f3aba', '5c5b351e6a81', '5c5b351f0478', '5c5b351f2016', '5c5b351e7bed', '5c5b351f3b7d', '5c5b351e8485', '5c5b351f6189', '5c5b351f6e1d', '5c5b351f0662', '5c5b351f6945', '5c5b351e802f', '5c5b351f69ae', '5c5b351f12f6', '5c5b351e8d5e', '5c5b351eb4d7', '5c5b351f6931', '5c5b351f0450', '5c5b351f47ad', '5c5b351f63af', '5c5b351f1ff8', '5c5b351f5b9e', '5c5b351f7809', '5c5b351f380d', '5c5b351e9952', '5c5b351e96be', '5c5b351e95e7', '5c5b351e8750', '5c5b351f680f', '5c5b351ec01c', '5c5b351e8d68', '5c5b351f335d', '5c5b351ebf5e', '5c5b351e267a', '5c5b351f1b2f', '5c5b351e8e1c', '5c5b351f73ae', '5c5b351f68dc', '5c5b351ef901', '5c5b351e8502', '5c5b351e96b4', '5c5b351f3731', '5c5b351eb50e', '5c5b351e92ea', '5c5b351f64bd', '5c5b351e7ee0', '5c5b351f590f', '5c5b351f67a1', '5c5b351f7345', '5c5b351e67b1', '5c5b351e9a97', '5c5b351f2660', '5c5b351e7319', '5c5b351f1edb', '5c5b351e7eae', '5c5b351f2363', '5c5b351e9079', '5c5b351f3713', '5c5b351f130a', '5c5b351f20e8', '5c5b351e9867', '5c5b351f072f', '5c5b351f69d6', '5c5b351e8ca5', '5c5b351e7355', '5c5b351f5829', '5c5b351f3c9a', '5c5b351f03d8', '5c5b351eaeba', '5c5b351f6918', '5c5b351e8764', '5c5b351f62c4', '5c5b351e6937', '5c5b351f1cc4', '5c5b351f6c9c', '5c5b351e98e4', '5c5b351eb7a7', '5c5b351e732d', '5c5b351f0923', '5c5b351f31a5', '5c5b351f3182', '5c5b351ef311', '5c5b351e8c64', '5c5b351e6ec8', '5c5b351e8c96', '5c5b351f3bbe', '5c5b351e8fbb', '5c5b351f348e', '5c5b351f36be', '5c5b351e9312', '5c5b351f3c40', '5c5b351ebd97', '5c5b351f7606', '5c5b351e8f7f', '5c5b351f67c9', '5c5b351f18e1', '5c5b351f0a59', '5c5b351f063a', '5c5b351f766f', '5c5b351f4d43', '5c5b351e8e08', '5c5b351f66ca', '5c5b351f3605', '5c5b351e933f', '5c5b351f1c10', '5c5b351eb4aa', '5c5b351ebe8c', '5c5b351f706b', '5c5b351e998e', '5c5b351e25d0', '5c5b351f09d7', '5c5b351ef90b', '5c5b351e9718', '5c5b351e8c0a', '5c5b351eb374', '5c5b351eb4e1', '5c5b351f09ff', '5c5b351f5b35', '5c5b351e6d88', '5c5b351f762e', '5c5b351f0284', '5c5b351e8e80', '5c5b351f6cbf', '5c5b351e6950', '5c5b351eb527', '5c5b351ebc8e', '5c5b351e2585', '5c5b351e8d1d', '5c5b351f07bb', '5c5b351e699b', '5c5b351e84b7', '5c5b351f6c33', '5c5b351f5eb4', '5c5b351e6725', '5c5b351eb77a', '5c5b351f5f6d', '5c5b351e7ad5', '5c5b351e9786', '5c5b351efb09', '5c5b351e8e85', '5c5b351f3862', '5c5b351efa6e', '5c5b351f7589', '5c5b351e992f', '5c5b351f04eb', '5c5b351f228c', '5c5b351f6c5b', '5c5b351f202f', '5c5b351f1346', '5c5b351f57a2', '5c5b351f1f8a', '5c5b351e91eb', '5c5b351f1af8', '5c5b351f1e95', '5c5b351e5208', '5c5b351ebe9b', '5c5b351e7e5e', '5c5b351e7e6d', '5c5b351f692c', '5c5b351e6ffe', '5c5b351ebb3f', '5c5b351f0563', '5c5b351e906f', '5c5b351f3c9f', '5c5b351f56a3', '5c5b351f5ffe', '5c5b351f6dd2', '5c5b351e9209', '5c5b351e8c6e', '5c5b351f07e8', '5c5b351e86a1', '5c5b351e7ed1', '5c5b351f6bbb', '5c5b351f0699', '5c5b351f11bb', '5c5b351e93b7', '5c5b351e243b', '5c5b351ef730', '5c5b351f6b7f', '5c5b351e8e21', '5c5b351e9709', '5c5b351f044b', '5c5b351f246c', '5c5b351f03f6', '5c5b351f1e90', '5c5b351e940c', '5c5b351e85f7', '5c5b351f38f3', '5c5b351f027f', '5c5b351f0351', '5c5b351e2599', '5c5b351f6db4', '5c5b351ebdba', '5c5b351ef947', '5c5b351e67ed', '5c5b351e6996', '5c5b351f782c', '5c5b351f6fd5', '5c5b351f76f1', '5c5b351efab4', '5c5b351f3cc7', '5c5b351e93a8', '5c5b351ef9c9', '5c5b351e4fd3', '5c5b351ebb71', '5c5b351f758e', '5c5b351e9042', '5c5b351ef915', '5c5b351f086f', '5c5b351e8f8e', '5c5b351f034c', '5c5b351f099b', '5c5b351f20b6', '5c5b351e965a', '5c5b351e99b1', '5c5b351f7142', '5c5b351f3641', '5c5b351f4893', '5c5b351e8656', '5c5b351eebe6', '5c5b351e9885', '5c5b351e6ddd', '5c5b351f64d6', '5c5b351efa87', '5c5b351ebdb5', '5c5b351f3312', '5c5b351f5711', '5c5b351e2490', '5c5b351f6d3c', '5c5b351eb82e', '5c5b351f6837', '5c5b351ef92e', '5c5b351e8034', '5c5b351e7edb', '5c5b351f66e8', '5c5b351e87af', '5c5b351f0a2c', '5c5b351eb725', '5c5b351f760b', '5c5b351e74e0', '5c5b351e66fd', '5c5b351e94f7', '5c5b351e8151', '5c5b351e2341', '5c5b351f6dcd', '5c5b351e7747', '5c5b351efa19', '5c5b351f08d8', '5c5b351f34cf', '5c5b351f662a', '5c5b351f66ed', '5c5b351f07b6', '5c5b351f55a4', '5c5b351e9ace', '5c5b351f051d', '5c5b351ebd56', '5c5b351f32d6', '5c5b351ef9a1', '5c5b351f0261', '5c5b351f2025', '5c5b351eb40a', '5c5b351e90a6', '5c5b351e8e49', '5c5b351e9182', '5c5b351ef933', '5c5b351e8bc9', '5c5b351ebc34', '5c5b351e8c50', '5c5b351e8462', '5c5b351f4b68', '5c5b351efb45', '5c5b351e7cd3', '5c5b351f1f8f', '5c5b351f6b11', '5c5b351e861f', '5c5b351eb9b4', '5c5b351e78ff', '5c5b351f5fd1', '5c5b351e98a3', '5c5b351e7be3', '5c5b351f770a', '5c5b351ef988']


## DATA COLLECTION STATS FOR AP21

In [24]:
def get_joined_data(date, hour, env, models_in=ap_models):
    df_ap = get_ap21_data_ap(date, hour, env, models_in=ap_models)
    df_ap = df_ap.withColumn("time", F.date_trunc('hour',F.col('timestamp')))
    ap21_out = df_ap.select('ap').dropDuplicates().collect()
    ap21_out = [a.ap for a in ap21_out]
    
    df_c = get_ap21_data_cl_ev(date, hour, env)
    df_c_ap = df_c.where(F.col('ap').isin(ap21_out))
    
    
    ## Count events by type for each AP 
    df_ap_ag = df_ap.groupBy(['org_id',
                              'site_id',
                              'ap',  
                              'model', 
                              'dev', 
                              'band',
                              'time']).agg(F.sum('rx_decrypt_failures').alias('rx_decrypt_failures'),
                                            F.sum('rx_pkts').alias('rx_pkts'),
                                            F.sum('tx_errors').alias('tx_errors'),
                                            F.sum('tx_pkts').alias('tx_pkts'),
                                            F.sum('re_init').alias('re_init'),
                                            F.mean('total_client_count').alias('mean_total_client_count'),
                                            F.mean('active_client_count').alias('mean_active_client_count')
                                       ).persist()
    ## Count events by type for each AP 
    df_cc_ap_ag = df_c_ap.where(F.col('ev_type').isin(events_out)
                               ).groupBy(['org_id',
                                          'site_id',
                                          'ap',
                                          'band']
                                        ).pivot('ev_type').agg(F.countDistinct('wcid').alias('clients'),
                                                               F.count('When').alias('events')).persist()
    df_cc_ap_ag = df_cc_ap_ag.fillna(0)
    df_ap_tot = df_ap_ag.join(df_cc_ap_ag, ['org_id', 'site_id', 'ap', 'band'])
    cols_out = [x+"_events" for x in events_out if x + "_events" in df_ap_tot.columns]
    df_ap_tot = df_ap_tot.withColumn('events_tot', reduce(add, [F.col(cc) for cc in cols_out]))
    df_ap_tot = df_ap_tot.join(t_org_1, 'org_id')
    df_ap_tot = df_ap_tot.join(t_org_2, 'site_id')
    return df_ap_tot
    

FloatProgress(value=0.0, bar_style='info', description='Progress:', layout=Layout(height='25px', width='50%'),…

In [70]:
dates = ['2022-06-09']
# hours = ['01', '02', '03', '04', '05', '06', '07', '08','09', '10',  '12', '13', '14', '15' ]
env ='production'
hours = ['09', '11', '16','17', '18', '19', '20', '21', '22', '23' ]
# hours = ['11' ]
for date in dates:
    print(date)    
    for hour in hours:
        print(hour)
        df_ap_tot = get_joined_data(date, hour, env, models_in=ap_models)
        ## Save data 
        save_path = "s3://mist-data-science-dev/marina/ap21/ap-stats-combined-analytics_v2/dt="+ date + "/hr=" + hour +"/" 
        print(save_path)
        df_ap_tot.coalesce(1).write.save(save_path, format='parquet', mode='overwrite', header=True)

FloatProgress(value=0.0, bar_style='info', description='Progress:', layout=Layout(height='25px', width='50%'),…

An error was encountered:
An error occurred while calling o7982.save.
: org.apache.spark.SparkException: Job aborted.
	at org.apache.spark.sql.execution.datasources.FileFormatWriter$.write(FileFormatWriter.scala:231)
	at org.apache.spark.sql.execution.datasources.InsertIntoHadoopFsRelationCommand.run(InsertIntoHadoopFsRelationCommand.scala:195)
	at org.apache.spark.sql.execution.command.DataWritingCommandExec.sideEffectResult$lzycompute(commands.scala:108)
	at org.apache.spark.sql.execution.command.DataWritingCommandExec.sideEffectResult(commands.scala:106)
	at org.apache.spark.sql.execution.command.DataWritingCommandExec.doExecute(commands.scala:131)
	at org.apache.spark.sql.execution.SparkPlan.$anonfun$execute$1(SparkPlan.scala:194)
	at org.apache.spark.sql.execution.SparkPlan.$anonfun$executeQuery$1(SparkPlan.scala:232)
	at org.apache.spark.rdd.RDDOperationScope$.withScope(RDDOperationScope.scala:151)
	at org.apache.spark.sql.execution.SparkPlan.executeQuery(SparkPlan.scala:229)
	at

In [23]:
a=1

FloatProgress(value=0.0, bar_style='info', description='Progress:', layout=Layout(height='25px', width='50%'),…

### GET COLLECTED DATA

In [ ]:
folder = "s3://mist-data-science-dev/marina/ap21/ap-stats-combined-analytics_v2/dt=2022-06-08/hr=10/*.parquet"
folder = "s3://mist-data-science-dev/marina/ap21/ap-stats-combined-analytics_v2/dt=2022-06-09/hr=05/*.parquet"

In [25]:
schema_tt = StructType([StructField("site_id",StringType(), True),
                          StructField("org_id",StringType(), True),
                          StructField("ap",StringType(), True),
                          StructField("band",StringType(), True),
                          StructField("model",StringType(), True),
                          StructField("dev",StringType(),True),
                          StructField("time",TimestampType(),True),
                          StructField("rx_decrypt_failures",LongType(),True),
                          StructField("rx_pkts",LongType(),True),
                          StructField("tx_errors",LongType(),True),
                          StructField("tx_pkts",LongType(),True),
                          StructField("re_init",LongType(),True),
                          StructField("mean_total_client_count",DoubleType(),True),
                          StructField("mean_active_client_count",DoubleType(),True),
                          StructField("CLIENT_ASSOCIATION_clients",LongType(),True),
                          StructField("CLIENT_ASSOCIATION_events",LongType(),True),
                          StructField("CLIENT_AUTHENTICATED_11R_clients",LongType(),True),
                          StructField("CLIENT_AUTHENTICATED_11R_events",LongType(),True),
                          StructField("CLIENT_AUTH_ASSOCIATION_clients",LongType(),True),
                          StructField("CLIENT_AUTH_ASSOCIATION_events",LongType(),True),
                          StructField("CLIENT_AUTH_REASSOCIATION_clients",LongType(),True),
                          StructField("CLIENT_AUTH_REASSOCIATION_events",LongType(),True),
                          StructField("CLIENT_AUTH_REASSOCIATION_11R_clients",LongType(),True),
                          StructField("CLIENT_AUTH_REASSOCIATION_11R_events",LongType(),True),
                          StructField("CLIENT_DEASSOCIATION_clients",LongType(),True),
                          StructField("CLIENT_DEASSOCIATION_events",LongType(),True),
                          StructField("CLIENT_DEAUTHENTICATED_clients",LongType(),True),
                          StructField("CLIENT_DEAUTHENTICATED_events",LongType(),True),
                          StructField("CLIENT_DEAUTHENTICATION_clients",LongType(),True),
                          StructField("CLIENT_DEAUTHENTICATION_events",LongType(),True),
                          StructField("CLIENT_REASSOCIATION_clients",LongType(),True),
                          StructField("CLIENT_REASSOCIATION_events",LongType(),True),
                          StructField("CLIENT_AUTHENTICATED_events",LongType(),True),
                          StructField("CLIENT_AUTHENTICATED_clients",LongType(),True),
                          StructField("CLIENT_AUTH_REASSOCIATION_OKC_events",LongType(),True),
                          StructField("CLIENT_AUTH_REASSOCIATION_OKC_clients",LongType(),True),
                          StructField("events_tot",LongType(),True),
                          StructField("org_name",StringType(),True),
                          StructField("site_name",StringType(),True)])

FloatProgress(value=0.0, bar_style='info', description='Progress:', layout=Layout(height='25px', width='50%'),…

In [26]:
folder = "s3://mist-data-science-dev/marina/ap21/ap-stats-combined-analytics_v2/dt=2022-06-09/hr=*/*.parquet"
df = spark.read.schema(schema_tt).parquet(folder)

FloatProgress(value=0.0, bar_style='info', description='Progress:', layout=Layout(height='25px', width='50%'),…

In [26]:
# df.select("time").orderBy(F.col("time")).dropDuplicates().show(30, truncate=False)

FloatProgress(value=0.0, bar_style='info', description='Progress:', layout=Layout(height='25px', width='50%'),…

+-------------------+
|time               |
+-------------------+
|2022-06-09 00:00:00|
|2022-06-09 09:00:00|
|2022-06-09 05:00:00|
|2022-06-09 01:00:00|
|2022-06-09 13:00:00|
|2022-06-09 04:00:00|
|2022-06-09 10:00:00|
|2022-06-09 02:00:00|
|2022-06-09 12:00:00|
|2022-06-09 07:00:00|
|2022-06-09 08:00:00|
|2022-06-09 14:00:00|
|2022-06-09 03:00:00|
|2022-06-09 11:00:00|
|2022-06-09 06:00:00|
+-------------------+

In [27]:
cols =['CLIENT_ASSOCIATION_clients', 
       'CLIENT_ASSOCIATION_events', 
       'CLIENT_AUTHENTICATED_11R_clients', 
       'CLIENT_AUTHENTICATED_11R_events', 
       'CLIENT_AUTH_ASSOCIATION_clients', 
       'CLIENT_AUTH_ASSOCIATION_events', 
       'CLIENT_AUTH_REASSOCIATION_clients', 
       'CLIENT_AUTH_REASSOCIATION_events', 
       'CLIENT_AUTH_REASSOCIATION_11R_clients', 
       'CLIENT_AUTH_REASSOCIATION_11R_events', 
       'CLIENT_DEASSOCIATION_clients', 
       'CLIENT_DEASSOCIATION_events', 
       'CLIENT_DEAUTHENTICATED_clients',
       'CLIENT_DEAUTHENTICATED_events', 
       'CLIENT_DEAUTHENTICATION_clients', 
       'CLIENT_DEAUTHENTICATION_events',
       'CLIENT_REASSOCIATION_clients',
       'CLIENT_REASSOCIATION_events',
       "CLIENT_AUTHENTICATED_events",
       "CLIENT_AUTHENTICATED_clients",
       "CLIENT_AUTH_REASSOCIATION_OKC_events",
       "CLIENT_AUTH_REASSOCIATION_OKC_clients"
      ]
df = df.fillna(0, subset=cols)

FloatProgress(value=0.0, bar_style='info', description='Progress:', layout=Layout(height='25px', width='50%'),…

In [34]:
df.printSchema()

FloatProgress(value=0.0, bar_style='info', description='Progress:', layout=Layout(height='25px', width='50%'),…

root
 |-- site_id: string (nullable = true)
 |-- org_id: string (nullable = true)
 |-- ap: string (nullable = true)
 |-- band: string (nullable = true)
 |-- model: string (nullable = true)
 |-- dev: string (nullable = true)
 |-- time: timestamp (nullable = true)
 |-- rx_decrypt_failures: long (nullable = true)
 |-- rx_pkts: long (nullable = true)
 |-- tx_errors: long (nullable = true)
 |-- tx_pkts: long (nullable = true)
 |-- re_init: long (nullable = true)
 |-- mean_total_client_count: double (nullable = true)
 |-- mean_active_client_count: double (nullable = true)
 |-- CLIENT_ASSOCIATION_clients: long (nullable = true)
 |-- CLIENT_ASSOCIATION_events: long (nullable = true)
 |-- CLIENT_AUTHENTICATED_11R_clients: long (nullable = true)
 |-- CLIENT_AUTHENTICATED_11R_events: long (nullable = true)
 |-- CLIENT_AUTH_ASSOCIATION_clients: long (nullable = true)
 |-- CLIENT_AUTH_ASSOCIATION_events: long (nullable = true)
 |-- CLIENT_AUTH_REASSOCIATION_clients: long (nullable = true)
 |-- CLIE

In [28]:
AUTH_SUCC_LIST = ['CLIENT_AUTH_ASSOCIATION',
                  'CLIENT_AUTHENTICATED',
                  'CLIENT_AUTH_REASSOCIATION']
ASSO_SUCC_LIST = ['CLIENT_ASSOCIATION',
                  'CLIENT_REASSOCIATION']
NEUTRAL_LIST = ['CLIENT_DEAUTHENTICATION',
                'CLIENT_DEASSOCIATION',
                'CLIENT_DEAUTHENTICATED',
                'CLIENT_AUTH_ASSOCIATION_OKC',
                'CLIENT_AUTHENTICATED_11R',
                'CLIENT_AUTH_REASSOCIATION_OKC',
                'CLIENT_AUTH_REASSOCIATION_11R']

FloatProgress(value=0.0, bar_style='info', description='Progress:', layout=Layout(height='25px', width='50%'),…

In [29]:
%%pretty
df.orderBy(F.col('events_tot').desc()).show(20, truncate=False)

FloatProgress(value=0.0, bar_style='info', description='Progress:', layout=Layout(height='25px', width='50%'),…

In [30]:
cols_to_order = ['site_id', 'org_id', 'org_name', 'site_name', 'ap', 'band', 'model', 'dev', 'time',
                 'rx_decrypt_failures', 'rx_pkts', 'tx_errors', 'tx_pkts', 're_init', 
                 'mean_total_client_count', 'mean_active_client_count',                   
                 'CLIENT_ASSOCIATION_events', 
                 'CLIENT_AUTHENTICATED_11R_events', 
                 'CLIENT_AUTH_ASSOCIATION_events', 
                 'CLIENT_AUTH_REASSOCIATION_events', 
                 'CLIENT_AUTH_REASSOCIATION_11R_events', 
                 'CLIENT_DEASSOCIATION_events', 
                 'CLIENT_DEAUTHENTICATED_events', 
                 'CLIENT_DEAUTHENTICATION_events', 
                 'CLIENT_REASSOCIATION_events', 
                 "CLIENT_AUTHENTICATED_events",
                 "CLIENT_AUTH_REASSOCIATION_OKC_events",
                 'events_tot',                                  
                 'CLIENT_ASSOCIATION_clients', 
                 'CLIENT_AUTHENTICATED_11R_clients', 
                 'CLIENT_AUTH_ASSOCIATION_clients', 
                 'CLIENT_AUTH_REASSOCIATION_clients',  
                 'CLIENT_AUTH_REASSOCIATION_11R_clients', 
                 'CLIENT_DEASSOCIATION_clients', 
                 'CLIENT_DEAUTHENTICATED_clients', 
                 'CLIENT_DEAUTHENTICATION_clients',
                 'CLIENT_REASSOCIATION_clients',
                 "CLIENT_AUTHENTICATED_clients",
                 "CLIENT_AUTH_REASSOCIATION_OKC_clients"]

FloatProgress(value=0.0, bar_style='info', description='Progress:', layout=Layout(height='25px', width='50%'),…

In [31]:
df =  df.select(cols_to_order).withColumn('REASSOCIATION_tot',
                    F.col("CLIENT_AUTH_REASSOCIATION_events") + 
                    F.col("CLIENT_AUTH_REASSOCIATION_11R_events") +
                    F.col('CLIENT_REASSOCIATION_events')) \
                    .withColumn('DEAUTHENTICATION_tot',
                               F.col('CLIENT_DEAUTHENTICATED_events') + 
                               F.col('CLIENT_DEAUTHENTICATION_events'))\
                   .withColumn('ASSOCIATION_tot',
                               F.col("CLIENT_ASSOCIATION_events") + 
                               F.col("CLIENT_AUTH_ASSOCIATION_events"))\
                   .withColumn('AUTHENTICATED_tot',
                               F.col("CLIENT_AUTHENTICATED_events") + 
                               F.col("CLIENT_AUTHENTICATED_11R_events"))\
                   .withColumn('DEASSOCIATION_tot',
                               F.col('CLIENT_DEASSOCIATION_events'))

df =  df.withColumn('REASSOCIATION_ex', F.when(F.col('REASSOCIATION_tot') >0, 1).otherwise(0))\
        .withColumn('DEAUTHENTICATION_ex', F.when(F.col('DEAUTHENTICATION_tot') >0, 1).otherwise(0))\
        .withColumn('ASSOCIATION_ex', F.when(F.col('ASSOCIATION_tot') >0, 1).otherwise(0))\
        .withColumn('AUTHENTICATED_ex', F.when(F.col('AUTHENTICATED_tot') >0, 1).otherwise(0))\
        .withColumn('DEASSOCIATION_ex', F.when(F.col('DEASSOCIATION_tot') >0, 1).otherwise(0))

df =  df.withColumn('types_count', F.col('REASSOCIATION_ex') + 
                                   F.col('DEAUTHENTICATION_ex') +
                                   F.col('ASSOCIATION_ex') +
                                   F.col('AUTHENTICATED_ex') +
                                   F.col('DEASSOCIATION_ex') )

df = df.withColumn('rx_per_cl', F.col('rx_pkts')/F.col('mean_active_client_count'))

FloatProgress(value=0.0, bar_style='info', description='Progress:', layout=Layout(height='25px', width='50%'),…

In [31]:
df.count()

FloatProgress(value=0.0, bar_style='info', description='Progress:', layout=Layout(height='25px', width='50%'),…

46563

In [33]:
%%pretty
df.orderBy(F.col('events_tot').desc()).show(20, truncate=False)

FloatProgress(value=0.0, bar_style='info', description='Progress:', layout=Layout(height='25px', width='50%'),…

In [32]:
df1 = df.where(F.col('time')<"2022-06-09 10:00:00")

FloatProgress(value=0.0, bar_style='info', description='Progress:', layout=Layout(height='25px', width='50%'),…

In [33]:
df2 = df.where(F.col('time')>"2022-06-09 10:00:00")

FloatProgress(value=0.0, bar_style='info', description='Progress:', layout=Layout(height='25px', width='50%'),…

In [34]:
df1.count()

FloatProgress(value=0.0, bar_style='info', description='Progress:', layout=Layout(height='25px', width='50%'),…

29318

In [34]:
%%spark -o df1 -n 30000

FloatProgress(value=0.0, bar_style='info', description='Progress:', layout=Layout(height='25px', width='50%'),…

FloatProgress(value=0.0, bar_style='info', description='Progress:', layout=Layout(height='25px', width='50%'),…

In [35]:
%%spark -o df2 -n 30000

FloatProgress(value=0.0, bar_style='info', description='Progress:', layout=Layout(height='25px', width='50%'),…

FloatProgress(value=0.0, bar_style='info', description='Progress:', layout=Layout(height='25px', width='50%'),…

In [31]:
%%spark -o df -n 50000

FloatProgress(value=0.0, bar_style='info', description='Progress:', layout=Layout(height='25px', width='50%'),…

FloatProgress(value=0.0, bar_style='info', description='Progress:', layout=Layout(height='25px', width='50%'),…

Interrupted by user


In [48]:
%%local
import plotly.graph_objects as go
ev_out = ['CLIENT_AUTH_ASSOCIATION', 'CLIENT_AUTHENTICATED', 
          'CLIENT_AUTH_REASSOCIATION', 'CLIENT_ASSOCIATION', 
          'CLIENT_DEAUTHENTICATION', 'CLIENT_DEASSOCIATION', 
          'CLIENT_DEAUTHENTICATED', 'CLIENT_AUTH_REASSOCIATION_11R']

ev_out = [x+'_events' for x in  ev_out ]

ev_out = ['CLIENT_ASSOCIATION_events', 'CLIENT_AUTHENTICATED_11R_events', 
          'CLIENT_AUTH_ASSOCIATION_events', 'CLIENT_AUTH_REASSOCIATION_events', 
          'CLIENT_AUTH_REASSOCIATION_11R_events', 'CLIENT_DEASSOCIATION_events', 
          'CLIENT_DEAUTHENTICATED_events','CLIENT_DEAUTHENTICATION_events', 
          'CLIENT_REASSOCIATION_events']
extra = ['REASSOCIATION_tot',
         'DEAUTHENTICATION_tot',
         'ASSOCIATION_tot', 
         'AUTHENTICATED_tot',
         'DEASSOCIATION_tot']
         #'events_tot'] 

extra = ['REASSOCIATION_tot', 'CLIENT_AUTH_REASSOCIATION_events']

ev_out =  extra

fig = go.Figure()
# Add traces
# range(len(sites_g1_top))
dd = df1[df1['REASSOCIATION_tot']>0]
# dd['rx_per_cl'] = dd['rx_pkts']/dd['mean_active_client_count']
#dd = dd[dd['rx_per_cl'] < 20000]
dd = dd[dd['rx_pkts'] < 10000]
#dd = dd.sort_values(by='timestamp')
for ev in ev_out:
    fig.add_trace(go.Scatter(#x=dd['rx_per_cl'],
                             x=dd['rx_pkts'],
                             y=dd[ev],
                             # y=dd['rx_decrypt_failures'],
                             #y=dd['rx_pkts'],
                             mode='markers',
                             marker=dict(size=10),
                             name=ev))
fig.update_layout(title='Number of events vs rx_pkts',
                  xaxis_title="number of rx_pkts per client",
                  yaxis_title='events')

fig.show()

In [41]:
%%local
import plotly.graph_objects as go
ev_out = ['CLIENT_AUTH_ASSOCIATION', 'CLIENT_AUTHENTICATED', 
          'CLIENT_AUTH_REASSOCIATION', 'CLIENT_ASSOCIATION', 
          'CLIENT_DEAUTHENTICATION', 'CLIENT_DEASSOCIATION', 
          'CLIENT_DEAUTHENTICATED', 'CLIENT_AUTH_REASSOCIATION_11R']

ev_out = [x+'_events' for x in  ev_out ]

ev_out = ['CLIENT_ASSOCIATION_events', 'CLIENT_AUTHENTICATED_11R_events', 
          'CLIENT_AUTH_ASSOCIATION_events', 'CLIENT_AUTH_REASSOCIATION_events', 
          'CLIENT_AUTH_REASSOCIATION_11R_events', 'CLIENT_DEASSOCIATION_events', 
          'CLIENT_DEAUTHENTICATED_events','CLIENT_DEAUTHENTICATION_events', 
          'CLIENT_REASSOCIATION_events']
extra = [#'REASSOCIATION_tot',
         #'DEAUTHENTICATION_tot',
         'ASSOCIATION_tot'] 
         #'AUTHENTICATED_tot',
         #'DEASSOCIATION_tot']
         #'events_tot'] 

#extra = ['REASSOCIATION_tot']

ev_out =  extra

fig = go.Figure()
# Add traces
# range(len(sites_g1_top))
dd = df1
# dd = df1[df1['REASSOCIATION_tot']>0]
dd['REASSOCIATION_rate'] = dd['REASSOCIATION_tot']/(dd['ASSOCIATION_tot']+1)
#dd = dd[dd['rx_per_cl'] < 20000]
# dd = dd[dd['rx_pkts'] < 10000]
#dd = dd.sort_values(by='timestamp')
for ev in ev_out:
    fig.add_trace(go.Scatter(#x=dd['rx_per_cl'],
                             x=dd['REASSOCIATION_rate'],
                             y=dd[ev],
                             # y=dd['rx_decrypt_failures'],
                             #y=dd['rx_pkts'],
                             mode='markers',
                             marker=dict(size=10),
                             name=ev))
fig.update_layout(title='Number of events vs rx_pkts',
                  xaxis_title="number of REASSOCIATION rate ",
                  yaxis_title='events')

fig.show()

In [46]:
%%local
import plotly.express as px
dd = df1[df1['events_tot'] > 10]
dd = dd[dd['CLIENT_AUTH_REASSOCIATION_events']/dd['CLIENT_AUTH_REASSOCIATION_clients'] > 0]
dd = dd[(dd['rx_pkts'] < 10000) 
        # & (dd['rx_pkts'] < dd['rx_decrypt_failures'])
       ]
fig = px.scatter_3d(dd, x= 'ASSOCIATION_tot', y='REASSOCIATION_tot', z='rx_per_cl',
                    color='rx_decrypt_failures'
                    #,size='mean_active_client_count'
                   )
fig.show()

In [62]:
%%local
import plotly.express as px
dd = df1[df1['events_tot'] > 10]
dd = dd[dd['CLIENT_AUTH_REASSOCIATION_events']/dd['CLIENT_AUTH_REASSOCIATION_clients'] > 0]
dd = dd[(dd['rx_pkts'] < 10000) 
        # & (dd['rx_pkts'] < dd['rx_decrypt_failures'])
       ]
fig = px.scatter_3d(dd, x= 'rx_decrypt_failures', y='rx_per_cl', z='DEAUTHENTICATION_tot',
                    color='REASSOCIATION_tot'
                    #,size='mean_active_client_count'
                   )
fig.show()

In [44]:
%%local
import plotly.graph_objects as go
ev_out = ['CLIENT_AUTH_ASSOCIATION', 'CLIENT_AUTHENTICATED', 
          'CLIENT_AUTH_REASSOCIATION', 'CLIENT_ASSOCIATION', 
          'CLIENT_DEAUTHENTICATION', 'CLIENT_DEASSOCIATION', 
          'CLIENT_DEAUTHENTICATED', 'CLIENT_AUTH_REASSOCIATION_11R']

ev_out = [x+'_events' for x in  ev_out ]

ev_out = ['CLIENT_ASSOCIATION_events', 'CLIENT_AUTHENTICATED_11R_events', 
          'CLIENT_AUTH_ASSOCIATION_events', 'CLIENT_AUTH_REASSOCIATION_events', 
          'CLIENT_AUTH_REASSOCIATION_11R_events', 'CLIENT_DEASSOCIATION_events', 
          'CLIENT_DEAUTHENTICATED_events','CLIENT_DEAUTHENTICATION_events', 
          'CLIENT_REASSOCIATION_events']
extra = ['REASSOCIATION_tot',
         'DEAUTHENTICATION_tot',
         'ASSOCIATION_tot', 
         'AUTHENTICATED_tot',
         'DEASSOCIATION_tot']
         #'events_tot'] 
# extra = ['REASSOCIATION_tot',
#         'DEAUTHENTICATION_tot']
#extra = ['REASSOCIATION_tot']

ev_out =  extra
dd = df1
dd['REASSOCIATION_rate'] = dd['REASSOCIATION_tot']/(dd['ASSOCIATION_tot']+1)
dd = dd[(dd['REASSOCIATION_rate'] <20) ]
ev_out = ['REASSOCIATION_rate']
fig = go.Figure()
for ev in ev_out:
    dd = df1[(df1[ev]>1) & (df1[ev]<150)]
    fig.add_trace(go.Histogram(histfunc="count",
                               x=dd[ev],
                               #x=dd['ap'],
                               name=ev))
fig.update_layout(xaxis_title='number of events', yaxis_title='Count of hourly data per AP', legend_title='events')
#fig.update_xaxes(categoryorder='array', categoryarray=["Thur", "Fri", "Sat", "Sun"])


fig.update_layout(title='Number of events per hour or AP21: <br> date = 06.09.2022 hours: 0am-10am <br> data with  number of events > 10 and < 200')
#                  xaxis_title="number of rx_pkts per client",
#                  yaxis_title='events')

fig.show()

ValueError: 
    Invalid value of type 'builtins.str' received for the 'histfunc' property of histogram
        Received value: 'density'

    The 'histfunc' property is an enumeration that may be specified as:
      - One of the following enumeration values:
            ['count', 'sum', 'avg', 'min', 'max']

In [112]:
%%local
import plotly.graph_objects as go
ev_out = ['CLIENT_AUTH_ASSOCIATION', 'CLIENT_AUTHENTICATED', 
          'CLIENT_AUTH_REASSOCIATION', 'CLIENT_ASSOCIATION', 
          'CLIENT_DEAUTHENTICATION', 'CLIENT_DEASSOCIATION', 
          'CLIENT_DEAUTHENTICATED', 'CLIENT_AUTH_REASSOCIATION_11R']

ev_out = [x+'_events' for x in  ev_out ]

ev_out = ['CLIENT_ASSOCIATION_events', 'CLIENT_AUTHENTICATED_11R_events', 
          'CLIENT_AUTH_ASSOCIATION_events', 'CLIENT_AUTH_REASSOCIATION_events', 
          'CLIENT_AUTH_REASSOCIATION_11R_events', 'CLIENT_DEASSOCIATION_events', 
          'CLIENT_DEAUTHENTICATED_events','CLIENT_DEAUTHENTICATION_events', 
          'CLIENT_REASSOCIATION_events']
#extra = ['rx_decrypt_failures','rx_pkts', 'rx_per_cl']
#extra = ['rx_per_cl']
         #'events_tot'] 
# extra = ['REASSOCIATION_tot',
#         'DEAUTHENTICATION_tot']
#extra = ['REASSOCIATION_tot']

ev_out =  extra
#dd = df1[(df1['events_tot']>1) & (df1['events_tot']<150)]
dd['REASSOCIATION_rate'] = dd['REASSOCIATION_tot']/(dd['ASSOCIATION_tot']+1)
ev_out = 
dd = df1
fig = go.Figure()
for ev in ev_out:
    dd = df1[(df1[ev]>=0) & (df1[ev]<1000)]
    fig.add_trace(go.Histogram2dContour(histfunc="count",
                               x=dd['REASSOCIATION_rate'],
                               #x=dd['ap'],
                               name=ev))
fig.update_layout(xaxis_title='number of rx_pkts per client', yaxis_title='Count of hourly data per AP', legend_title='events')
#fig.update_xaxes(categoryorder='array', categoryarray=["Thur", "Fri", "Sat", "Sun"])


fig.update_layout(title='Rx_pkts per active client per hour or AP21: <br> date = 06.09.2022 hours: 0am-10am <br> data with  number of rx_pkts/per cl < 1000')
#                  xaxis_title="number of rx_pkts per client",
#                  yaxis_title='events')

fig.show()

In [45]:
%%local
import plotly.express as px

extra = ['REASSOCIATION_tot',
         'DEAUTHENTICATION_tot',
         'ASSOCIATION_tot', 
         'AUTHENTICATED_tot',
         'DEASSOCIATION_tot']

dd = df1

fig = px.Histogram2dContour(dd, x='REASSOCIATION_tot', y='ASSOCIATION_tot', marginal_x="histogram", marginal_y="histogram")
fig.show()

AttributeError: module 'plotly.express' has no attribute 'Histogram2dContour'

In [ ]:
df_0 = spark.read.parquet(folder)
df_0 = df_0.withColumn('time', F.lit('2022-06-08 10:00:00'))

In [ ]:
df_1 = spark.read.parquet(folder1)
df_1 = df_1.withColumn('time', F.lit('2022-06-08 11:00:00'))

In [ ]:
df_0 = df_0.withColumn('time', F.lit('2022-06-08 10:00:00'))

In [ ]:
%%pretty
df_0.orderBy(F.col('events_tot').desc()).show(20, truncate=False)

### test ground

In [ ]:
date = '2022-06-09'
hour = '10'
env ='production'
ap_models = ['AP21-US', 'AP21-WW']

df = get_joined_data(date, hour, env, models_in=ap_models)

In [ ]:
df.printSchema()

In [ ]:
df.show(10, truncate=False)

In [ ]:
date = '2022-06-09'
hour = '10'
env ='production'
ap_models = ['AP21-US', 'AP21-WW']
df_ap = get_ap21_data_ap(date, hour, env, models_in=ap_models)

In [ ]:
df_c = get_ap21_data_cl_ev(date, hour, env)

In [ ]:
df_c_ap = df_c.where(F.col('ap').isin(ap21))

In [ ]:
## Count events by type for each AP 
df_ap_ag = df_ap.groupBy(['org_id',
                          'site_id',
                          'ap',  
                          'model', 
                          'dev', 
                          'band']).agg(F.sum('rx_decrypt_failures').alias('rx_decrypt_failures'),
                                        F.sum('rx_pkts').alias('rx_pkts'),
                                        F.sum('tx_errors').alias('tx_errors'),
                                        F.sum('tx_pkts').alias('tx_pkts'),
                                        F.sum('re_init').alias('re_init'),
                                        F.mean('total_client_count').alias('mean_total_client_count'),
                                        F.mean('active_client_count').alias('mean_active_client_count')
                                   ).persist()

In [ ]:
## Count events by type for each AP 
df_cc_ap_ag = df_c_ap.where(F.col('ev_type').isin(events_out)
                           ).groupBy(['org_id',
                                      'site_id',
                                      'ap',
                                      'band']
                                    ).pivot('ev_type').agg(F.countDistinct('wcid').alias('clients'),
                                                           F.count('When').alias('events')).persist()
df_cc_ap_ag = df_cc_ap_ag.fillna(0)

In [ ]:
df_ap_tot = df_ap_ag.join(df_cc_ap_ag, ['org_id', 'site_id', 'ap', 'band'])
cols_out = [x for x in events_out if x + "_events" in df_ap_tot.columns]
df_ap_tot = df_ap_tot.withColumn('events_tot', reduce(add, [F.col(cc) for cc in cols_out]))

In [ ]:
df_ap_tot = df_ap_tot.join(t_org_1, 'org_id')
df_ap_tot = df_ap_tot.join(t_org_2, 'site_id')

In [ ]:
## Save data 
save_path = "s3://mist-data-science-dev/marina/ap21/ap-stats-combined-analytics/dt="+ date + "/"
print(save_path)
df_ap_tot.coalesce(1).write.save(save_path, format='parquet', mode='overwrite', header=True)

## STATS FOR AP21  

In [ ]:
date = '2022-06-08'
hour = '10'
env ='production'
# ap stats
sites = ['0a878d43-e796-4120-8cd8-b7359600af16', '41c289fa-a8e5-4b83-aa28-fb9d265dab26']
ap_models = ['AP21-US', 'AP21-WW']
ap_in = ['5c-5b-35-1e-70-8a', '5c-5b-35-1e-81-f6', '5c-5b-35-1e-b5-63']
fields_in_data  = ['rx_decrypt_failures', 'rx_pkts', 'rx_errors', 'tx_pkts', 'tx_errors']
ap_fields = ['site_id',
             'org_id',
             'id',
             'model', 
             'total_client_count', 
             'active_client_count', 'terminator_timestamp', 'timestamp']
# AP data 
df = get_ap_stats(date, hour, env)
df = df.where(F.col('model').isin(ap_models))

# events data
df_c = get_es_client_data(date, hour, env)
# add band 
df_c = df_c.withColumn('band', F.json_tuple("metadata", "band"))
df_c = df_c.withColumn('band', F.col("band").cast(IntegerType()))

In [ ]:
df_c.select('metadata').show(5, truncate=False)

In [ ]:
df_c.printSchema()

In [ ]:
df_c.columns

In [ ]:
df_c_test = df_c.withColumn('metadata', F.explode('metadata')).select("*", F.col("metadata.*"))

In [ ]:
ap_models = ['AP21-US', 'AP21-WW']
fields_in_data  = ['rx_decrypt_failures', 
                   'rx_pkts', 
                   'rx_errors', 
                   'tx_pkts', 
                   'tx_errors',
                   're_init']
fields_in_radio  = ['dev', 
                   'band', 
                   'channel']
ap_fields = ['site_id',
             'org_id',
             'id',
             'model',
             'uptime',
             'interval',
             'total_client_count', 
             'active_client_count', 
             'terminator_timestamp', 
             'timestamp']
df_ap = df.where(F.col('model').isin(ap_models))
df_ap = df_ap.withColumn("radios", F.explode("radios")).select("*", F.col("radios.*"))
df_ap = df_ap.withColumn('ap',  F.regexp_replace('id', '-', ''))
df_ap = df_ap.select(ap_fields + fields_in_radio + fields_in_data)
df_ap = df_ap.withColumn("timestamp_h", F.date_trunc('hour',F.col('timestamp')))
df_ap = df_ap.withColumn('ap',  F.regexp_replace('id', '-', ''))

In [ ]:
# get ap list;
ap21_out = df_ap.select('ap').dropDuplicates().collect()

In [ ]:
ap21_out = [a.ap for a in ap21_out]

In [ ]:
ap21_out

In [ ]:
df_c_ap = df_c.where(F.col('ap').isin(ap21_out))

In [ ]:
df_c_ap.columns

In [ ]:
df_ap.columns

In [ ]:
## Count events by type for each AP 
df_ap_ag = df_ap.groupBy(['org_id',
                          'site_id',
                          'ap',  
                          'model', 
                          'dev', 
                          'band']).agg(F.sum('rx_decrypt_failures').alias('nrx_decrypt_failures'),
                                        F.sum('rx_pkts').alias('nrx_pkts'),
                                        F.sum('tx_errors').alias('ntx_errors'),
                                        F.sum('tx_pkts').alias('ntx_pkts'),
                                        F.sum('re_init').alias('nre_init'),
                                        F.mean('total_client_count').alias('mean_total_client_count'),
                                        F.mean('active_client_count').alias('mean_active_client_count')
                                   ).persist()

In [ ]:
## Count events by type for each AP 
df_c_ap_ag = df_c_ap.groupBy(['org_id',
                              'site_id',
                              'ap', 
                              'ev_type', 
                              'band']).agg(F.countDistinct('wcid').alias('number_of_clients'),
                                    F.count('When').alias('number_of_events')
                                   ).persist()

In [ ]:
## Count events by type for each AP 
df_cc_ap_ag = df_c_ap.where(F.col('ev_type').isin(events_out)).groupBy(['org_id',
                    'site_id',
                    'ap', 'band']).pivot('ev_type').agg(F.countDistinct('wcid').alias('number_of_clients'),
                                    F.count('When').alias('number_of_events')
                                   ).persist()

df_cc_ap_ag = df_cc_ap_ag.fillna(0)

In [ ]:
df_cc_ap_ag.columns

In [ ]:
df_ap_ag.columns

In [ ]:
df_ap_tot = df_ap_ag.join(df_cc_ap_ag, ['org_id', 'site_id', 'ap', 'band'])

In [ ]:
%%pretty
df_ap_tot.orderBy(F.col('nrx_decrypt_failures').desc()).show(30, truncate=False)

In [ ]:
## Save data 
"""
date = '2022-06-08'
hour = '10'
save_path = "s3://mist-data-science-dev/marina/ap21/ap-stats-combined-analytics/dt="+ date + "/"
print(save_path)
df_ap_tot.coalesce(1).write.save(save_path, format='parquet', mode='overwrite', header=True)"""

In [ ]:
%%spark -o df_ap_tot -n 10000 

In [ ]:
df_ap_tot.columns

In [ ]:
df_ap_tot = df_ap_tot.withColumn('events_tot', reduce(add, [F.col(cc) for cc in cols_out]))

In [ ]:
df_ap_tot.columns

In [ ]:
cols_out = [x for x in events_out if x+"_number_of_events" in df_ap_tot.columns ]

In [ ]:
cols_out = [x+"_number_of_events" for x in events_out if x+"_number_of_events" in df_ap_tot.columns ]

In [ ]:
%%local
import plotly.express as px
df = px.data.iris()
fig = px.scatter_3d(df, x='sepal_length', y='sepal_width', z='petal_width',
                    color='petal_length', symbol='species')
fig.show()

In [ ]:
%%local
import plotly.graph_objects as go
ev_out = ['CLIENT_AUTH_ASSOCIATION', 'CLIENT_AUTHENTICATED', 
          'CLIENT_AUTH_REASSOCIATION', 'CLIENT_ASSOCIATION', 
          'CLIENT_DEAUTHENTICATION', 'CLIENT_DEASSOCIATION', 
          'CLIENT_DEAUTHENTICATED', 'CLIENT_AUTH_REASSOCIATION_11R']

fig = go.Figure()
# Add traces
# range(len(sites_g1_top))
dd = df_ap_tot[df_ap_tot['nrx_decrypt_failures']<1000]
#dd = dd.sort_values(by='timestamp')
for ev in [x+"_number_of_events" for x in ev_out]:
    fig.add_trace(go.Scatter(x=dd['nrx_decrypt_failures'],
                         y=dd[ev],
                         mode='markers',
                         marker=dict(size=10),
                         name=ev[:-17]))
"""fig.add_trace(go.Scatter(x=dd['nrx_decrypt_failures'],
                         y=dd['CLIENT_DEASSOCIATION_number_of_events'],
                         mode='markers',
                         name='CLIENT_DEASSOCIATION_number_of_events'))  
fig.add_trace(go.Scatter(x=dd['nrx_decrypt_failures'],
                         y=dd['CLIENT_DEAUTHENTICATED_number_of_events'],
                         mode='markers',
                         name='CLIENT_DEAUTHENTICATED_number_of_events'))  """  

fig.update_layout(title='Number of events vs decrypt_failures',
    xaxis_title="number of rx_decrypt_failures",
    yaxis_title='events')

fig.show()

In [ ]:
%%local
import plotly.graph_objects as go

fig = go.Figure()
# Add traces
# range(len(sites_g1_top))
dd = df_ap_tot
#dd = dd.sort_values(by='timestamp')
fig.add_trace(go.Scatter(x=dd['nrx_decrypt_failures'],
                         y=dd['nrx_pkts'],
                         mode='lines+markers',
                         name='clients'))
fig.add_trace(go.Scatter(x=dd['timestamp'],
                         y=dd['clients_with_signals'],
                         mode='lines+markers',
                         name='clients_with_signals'))   

#fig.update_layout(title='Number of events vs decrypt_failures')
fig.update_layout(title='Number of events vs decrypt_failures',
    xaxis_title="number of decrypt_failures",
    yaxis_title='events')

fig.show()

In [ ]:
%%local
# <===  PLOTS ===> 
import plotly.express as px
import plotly.graph_objects as go
fig = go.Figure()

dda = score[['client_wcid','rank_score']]
dda = dda[dda['rank_score']>=0]
trace1 = go.Histogram(
    x=dda.rank_score,
    opacity=0.75,
    nbinsx=60,
    #histnorm='probability',
    name="sle_rank_score")

data = [trace1]
fig = go.Figure(data=data)
fig.update_layout(title = 'Sticky client rssi distribution across')
fig.show()

In [ ]:
%%pretty
df_ap_tot.orderBy(F.col('nrx_decrypt_failures').desc()).show(20, truncate=False)

In [ ]:
df_c_ap_ag_pd = df_c_ap_ag.toPandas()

In [ ]:
%%pretty
df_c_ap_ag.where(F.col('ev_type').isin(events_out)
                ).orderBy(F.col('number_of_events').desc()).show(100, truncate=False)

In [ ]:
len(events_out)

In [ ]:
list(set(events_out))

In [ ]:
top_ap = df_c_ap_ag.where((F.col('ev_type').isin(events_out)) &
                          (F.col('number_of_events')>20) & 
                          (F.col('number_of_events')/F.col('number_of_clients')>2))

In [ ]:
%%pretty
top_ap.orderBy(F.col('number_of_events').desc()).show(20, truncate=False)

In [ ]:
top_ap_list = top_ap.select('ap').dropDuplicates().collect()

In [ ]:
top_ap_list = [a.ap for a in top_ap_list]

In [ ]:
len(top_ap_list)

In [ ]:
df_top_ap = df_ap_ag_pd[df_c_ap_ag_pd['ap'].isin(top_ap_list)==True]

In [ ]:
df_top_ap[:10]

In [ ]:
events_out = AUTH_SUCC_LIST + ASSO_SUCC_LIST + NEUTRAL_LIST
events_missing = AUTH_FAILURE_LIST + ASSO_FAILURE_LIST

In [ ]:
events_out

In [ ]:
df_c_ap_ag_pd = df_c_ap_ag_pd[df_c_ap_ag_pd['ev_type'].isin(events_out +events_missing)]

In [ ]:
df_c_ap_ag_pd.sort_values(by = ['number_of_clients'], ascending=False)[:20]

In [ ]:
df_c_ap_ag_pd[df_c_ap_ag_pd['ev_type']=='CLIENT_AUTH_REASSOCIATION'].sort_values(by = ['number_of_events'], 
                                                                                 ascending=True)[:20]

In [ ]:
df_ap_ag_pd = df_ap_ag.toPandas()

In [ ]:
df_ap_ag_pd[:10]

In [ ]:
df_ap_ag_pd.columns

In [ ]:
import matplotlib.pyplot as plt
import seaborn as sns
import matplotlib.pyplot as plt

test = df_ap_ag_pd
#test = test[test['nrx_decrypt_failures']>0]
#test = test[test['nrx_decrypt_failures']<20000]
fig, axes = plt.subplots(sharex=True, sharey=True, figsize = (15,5))

test.hist(column='nrx_decrypt_failures', alpha=0.6, ax=axes, log=True)
plt.legend()
# set title and axis labels
plt.suptitle("DATA FOR AP: ", x=0.5, y=1.05, ha='center', fontsize='xx-large')
plt.legend()
fig.text(0.5, 0.04, 'Number of nrx_decrypt_failures', ha='center')
fig.text(0.04, 0.5, 'number of AP21', va='center', rotation='vertical')

plt.show()

%matplot plt

In [ ]:
import matplotlib.pyplot as plt
import seaborn as sns
import matplotlib.pyplot as plt

test = df_ap_ag_pd
#test = test[test['nrx_decrypt_failures']>0]
test = test[test['nrx_decrypt_failures']<10]
fig, axes = plt.subplots(sharex=True, sharey=True, figsize = (15,5))

test.hist(column='nrx_decrypt_failures', alpha=0.6, ax=axes, log=True)
plt.legend()
# set title and axis labels
plt.suptitle("DATA FOR AP: ", x=0.5, y=1.05, ha='center', fontsize='xx-large')
plt.legend()
fig.text(0.5, 0.04, 'Number of nrx_decrypt_failures', ha='center')
fig.text(0.04, 0.5, 'number of AP21', va='center', rotation='vertical')

plt.show()

%matplot plt

In [ ]:
AUTH_SUCC_LIST = ['CLIENT_AUTH_ASSOCIATION',
                  'CLIENT_AUTHENTICATED',
                  'CLIENT_AUTH_REASSOCIATION']
ASSO_SUCC_LIST = ['CLIENT_ASSOCIATION',
                  'CLIENT_REASSOCIATION']
NEUTRAL_LIST = ['CLIENT_DEAUTHENTICATION',
                'CLIENT_DEASSOCIATION',
                'CLIENT_DEAUTHENTICATED',
                'STA_DOS_DISASSOC',
                'CLIENT_AUTH_ASSOCIATION_OKC',
                'CLIENT_AUTHENTICATED_11R',
                'CLIENT_AUTH_REASSOCIATION_OKC',
                'CLIENT_AUTH_REASSOCIATION_11R']

#### === NOT TO HAVE === ####
AUTH_FAILURE_LIST=['CLIENT_ASSOCIATION_FAILURE', 
                   'REPEATED_AUTH_FAILURES']
DHCP_FAILURE_LIST=['MARVIS_EVENT_CLIENT_DHCP_STUCK',
                    'MARVIS_EVENT_CLIENT_DHCP_FAILURE']

#### === NOT TO HAVE === ####
AUTH_FAILURE_LIST = ['MARVIS_EVENT_CLIENT_AUTH_FAILURE',
                     'REPEATED_AUTH_FAILURES',
                     'MARVIS_EVENT_CLIENT_AUTH_FAILURE']
ASSO_FAILURE_LIST = ['CLIENT_ASSOCIATION_FAILURE']

In [ ]:
import matplotlib.pyplot as plt
import seaborn as sns
import matplotlib.pyplot as plt
fig, axes = plt.subplots(sharex=True, sharey=True, figsize = (15,5))
for ev in events_out[5:6]:
    test = df_c_ap_ag_pd[df_c_ap_ag_pd['ev_type'] == ev]
    #test = test[test['nrx_decrypt_failures']>0]
    #test = test[test['nrx_decrypt_failures']<10]
    test.hist(column='number_of_events', alpha=0.6, ax=axes, log=True)
    plt.legend()
    # set title and axis labels
    plt.suptitle("DATA FOR AP: ", x=0.5, y=1.05, ha='center', fontsize='xx-large')
    plt.legend()
    fig.text(0.5, 0.04, 'Number events ' +ev, ha='center')
    fig.text(0.04, 0.5, 'number of AP21', va='center', rotation='vertical')

plt.show()

%matplot plt

In [ ]:
df_c_ap_ag.columns

In [ ]:
df_c_ap_ag_pd[:10]

In [ ]:
df.printSchema()

In [ ]:
# Number of orgs, sites, number of AP within each site, Number of clients (average) on these AP

In [ ]:
df.select(['site_id']).dropDuplicates().count()

In [ ]:
df.select(['site_id']).dropDuplicates().count().collect()

In [ ]:
df.select(['site_id']).dropDuplicates().count()

In [ ]:
df.select(['id']).dropDuplicates().count()

In [ ]:
df_ag = df.groupBy(['site_id']).agg(F.countDistinct('id').alias('number_of_AP21'),
                                    F.mean('total_client_count').alias('average_clients_on_AP21')
                                   ).persist()

In [ ]:
df_ag_pd = df_ag.toPandas()

In [ ]:
# Get plots 

In [ ]:
import matplotlib.pyplot as plt
import seaborn as sns
import matplotlib.pyplot as plt

test = df_ag_pd
test = test[test['number_of_AP21'] <50]
fig, axes = plt.subplots(sharex=True, sharey=True, figsize = (15,5))

test.hist(column='number_of_AP21', alpha=0.6, ax=axes)
plt.legend()
# set title and axis labels
plt.suptitle("DATA FOR AP: ", x=0.5, y=1.05, ha='center', fontsize='xx-large')
plt.legend()
fig.text(0.5, 0.04, 'number of AP21', ha='center')
fig.text(0.04, 0.5, 'Number of sites', va='center', rotation='vertical')

plt.show()

%matplot plt

In [ ]:
import matplotlib.pyplot as plt
import seaborn as sns
import matplotlib.pyplot as plt

test = df_ag_pd

fig, axes = plt.subplots(sharex=True, sharey=True, figsize = (15,5))

test.hist(column='average_clients_on_AP21', alpha=0.6, ax=axes)
plt.legend()
# set title and axis labels
plt.suptitle("DATA FOR AP: ", x=0.5, y=1.05, ha='center', fontsize='xx-large')
plt.legend()
fig.text(0.5, 0.04, 'average number of clients per AP21', ha='center')
fig.text(0.04, 0.5, 'Number of sites', va='center', rotation='vertical')


plt.show()

%matplot plt

In [ ]:
top_ap21 =  ['b3c32004-a0dc-4353-b697-1065fbd4f639',
             '3cf29ebc-21f1-49e5-9956-25495fe8f41b',
             '9af85d06-5698-438a-ae40-b106591fb30d',
             'f74495a9-6e7e-46ca-9e20-e8cfd1cd3921',
             '3f83d07a-94e6-4bf6-bb8d-3abb722cef0e',
             '96a99ee2-0f6e-4595-a943-711fab09528c',
             '12070490-ec81-494c-84e8-69aaa18432c9',
             '7d29e98a-bd2d-46c0-8e00-7df23f3b6059',
             'cad89db4-2600-4682-9b22-77c717a213e4',
             'aa74790e-0459-486e-bbc5-c3a91aa2e88e',
             'f77981b7-1d01-4b6f-9c20-ef61d0181896',
             '4478cc45-20bc-4df3-8499-77c0461160eb',
             '96f95789-ed10-45bc-b94c-a29b4a396400',
             '948f1fbe-3df9-4d21-b499-e2c1a7f26600',
             '3ad2070a-d351-429e-8657-7051bc5ab8a2',
             '308eac11-7564-4cc8-993e-24411991b08f',
             'f4c17c2b-7b71-41f3-8d4c-153b8a2da87f',
             'e1002edf-9388-4f70-89fb-0ea56c8527aa',
             '47dfc166-0306-41d0-95dc-cc8fda879f51',
             '811d8495-1661-495e-aec2-7ab1ed94420c',
             '3f35a194-26c7-436b-ae51-e4459764c1de',
             '41c289fa-a8e5-4b83-aa28-fb9d265dab26',
             '4a5eb0a1-032c-492e-9596-30f11547c312',
             'a6dfcda0-9069-455a-ad52-1f6c068e840d',
             '0a878d43-e796-4120-8cd8-b7359600af16',
             '7b60debf-8e4e-4dfd-b070-d88d6cdd7a88',
             'bfcce584-3bdc-4737-90ca-0153299646e5',
             '231d18f4-0c02-4511-bf14-f83635fcec94',
             '8e16c525-67df-4b64-847f-dd8daed35723',
             '41042440-f28b-497d-8b62-0045cf4dab54',
             'f5f95157-1559-448e-9df4-62a67b51d37d',
             'e8802660-1a38-4725-af37-5c16bedb00ff',
             'fc735aad-84c0-4dcb-8c76-8b2bd03b54c1',
             'c832b955-df31-4529-bdb1-22e30cfdb5e5',
             'd856dd0c-a470-488a-bbdb-5b0e36bc48de',
             'e8d2717f-467d-4102-a89f-a78108c18014',
             'f0baf907-cdd5-4a9b-b07c-f70e793ff62c',
             'df227035-ce51-465e-88b9-532812fea5fe',
             'e29cfb6f-3267-4b3c-aaf2-32ed89deb2bd',
             'bc03eac8-be83-4c83-b8c4-dcd5fd57cac9',
             '2cce2b4d-a9bb-4627-adac-e46ded4dc203',
             '1c4ab857-1604-4049-9bf2-57eb771c5cc9',
             'fad6ee4a-5480-4652-bd18-71b92019c765',
             '4b61b7cb-30c1-4163-b270-233dcba31c45',
             'd8b7b593-39ef-4871-b904-a6b1c659a8c9',
             'aef02148-2830-4465-b90c-86c0cfca4fba',
             'e432e3c6-1051-4813-9643-c76a74c4af0d',
             '202fef85-745f-4ab6-9e85-bb5024a2e549',
             'fbe41111-5870-4958-ac81-b6a65329bb5e',
             '17215a02-a6d8-4018-98b7-4cae72b5f28a',
             '0e968236-3e0d-4237-8fb8-69a5617ca88d',
             'a271048e-dde0-4ecc-ad13-71134dab4dff',
             '0aa0c6b6-1dc0-470c-922b-33d7b183c6c4',
             'ecd4e2d9-b47b-4d3e-b25a-b8a161eb5a75',
             '8f554e3c-1001-4a30-a272-0fa2236a058c',
             '5a0cf36b-749f-4ae4-a810-847870c62f37',
             '38720cc0-f54f-4735-8fed-43ff982b92b1',
             'fa122fd3-d27c-40e7-8ae2-22de12dbfa83',
             'e6bfc955-5e34-443d-9a08-fa98a6b68e01',
             '1a7c0291-7e90-49aa-8287-bb6809c90ab4',
             'f9a8c163-2b9f-4184-8ba7-17f1c19f7cbe',
             '1a6ce3a7-17c9-432e-8c9e-2020a2f1ef1e',
             '05dc25ec-313b-4b4e-9d91-815c89118d4b',
             '502a385d-c7f4-4192-848f-c57f15f60e16',
             'd163e43b-9314-4a05-be0d-65401b295b4a',
             'e3fd30b0-0306-4c00-9233-c8a6c5ce4968',
             '37c4500d-403c-4bcc-bd10-d2009a6d7c6c',
             '40d3cca2-0bed-47b0-8a56-cc06673df353',
             '9935a3ae-49f3-41a6-988e-a0cbf87afd8c',
             '997d7fd7-a4bc-4d5d-8177-fb706954097b',
             '0860d890-ce5d-4d2f-a997-3f3449cf3559',
             '2a596b1c-f4e5-45e5-8d65-c69b4aae50e7',
             '12682dc2-d50c-4d72-9383-cb25f5e73085',
             '6a4513c4-d844-4a55-9b83-a649a787a7d4',
             '1611fbc4-a4f1-4ce5-8994-712c55c202c1',
             'bd676a2d-1953-4347-bc39-54b8b92e1172',
             '09552a2a-f533-4db6-bad6-cc419464b378',
             'f3f4fe4b-db91-47d7-a7f2-094dbf529bd2',
             'cc575566-5a7d-46be-9b75-b54f060a26c1',
             '93b8af35-890c-4bae-8caa-08f131cde08b',
             'b83afb18-2a02-45aa-b077-756f67ee5ab6',
             '3dc15297-3cea-4633-bdb6-1de7038c8853',
             '6cec3a0e-93a1-4c7d-8940-4498265400c4',
             'a96ba312-7d24-4db2-bb73-820849ac7550',
             'f5428739-faf8-4a9f-9cdc-b5b667289b07',
             '214443c3-f590-4fab-9949-e33edb3e247a',
             'd9ea3a38-d11d-4d54-967f-b168b5fbba74',
             '6d757844-4d50-40a4-bb41-331b5b211053',
             'b9be66bc-7fda-4e65-a6b2-c2e104a45b77',
             '4e041e09-126e-4eec-b5a6-8ad60dbede8d',
             'd57bc9c5-bbe1-4d58-86b1-488a6eeedb8a',
             'da881251-ab43-4ea6-b206-3fb3419de70f',
             '951421fb-a77a-4a12-8b5a-7963cf13ae86',
             '759857a1-5e47-4684-9a58-c9adb2924be6',
             '0bc30855-b5eb-468c-8c86-17232df7524a',
             'd9dad007-2d3f-48f9-98dc-3be512d29b5b',
             'a93d4396-6022-482c-ae14-49a3a558c45d',
             '7eba4681-c189-4d73-8e3d-12f9c65d0577',
             '6cc5315e-a20d-438e-8305-14cc8f58b2b0']


## GET DATA 

In [ ]:
def ap21_data(date):
    hour = []
    env ='production'
    # ap stats
    sites = ['0a878d43-e796-4120-8cd8-b7359600af16', '41c289fa-a8e5-4b83-aa28-fb9d265dab26']
    ap_in = ['5c-5b-35-1e-70-8a', '5c-5b-35-1e-81-f6', '5c-5b-35-1e-b5-63']
    fields_in_data  = ['rx_decrypt_failures', 
                       'rx_pkts', 
                       'rx_errors', 
                       'tx_pkts', 
                       'tx_errors',
                       're_init']
    fields_in_radio  = ['dev', 
                       'band', 
                       'channel']
    ap_fields = ['site_id',
                 'org_id',
                 'id',
                 'model',
                 'uptime',
                 'interval',
                 'total_client_count', 
                 'active_client_count', 
                 'terminator_timestamp', 
                 'timestamp']
    
    ap_ent_fields = ['site_id',
                     'org_id',
                     'id',
                     'model',
                     'dev', 
                     'band', 
                     'channel']
    
    # AP data 
    df = get_ap_stats(date, hour, env, sites) 
    # Client data 
    df_c = get_es_client_data(date, hour, env, sites)
    # select a list of AP 
    ap_in = ['5c-5b-35-1e-70-8a', '5c-5b-35-1e-81-f6', '5c-5b-35-1e-b5-63']
    df_ap = df.where(F.col('id').isin(ap_in))
    df_ap = df_ap.withColumn("radios", F.explode("radios")).select("*", F.col("radios.*"))
    df_ap = df_ap.withColumn('ap',  F.regexp_replace('id', '-', ''))
    df_ap = df_ap.select(ap_fields + fields_in_radio + fields_in_data)
    df_ap = df_ap.withColumn("timestamp_h", F.date_trunc('hour',F.col('timestamp')))

    df_ap = df_ap.withColumn('ap',  F.regexp_replace('id', '-', ''))
    
    # get counts per h 
    entity_cols = ['org_id', 'site_id', 'id', 'ap', 'model'] + fields_in_radio + ['timestamp_h']
    for mm in fields_in_data:  
        count_col = mm
        output_col = mm + '_tot'
        df_ap = tools.get_sum(df_ap, entity_cols, count_col, output_col)
    # get ratio
    df_ap = df_ap.withColumn('rx_errors_rate', F.when(F.col('rx_pkts')!=0,
                                                      F.round(F.col('rx_errors')/F.col('rx_pkts')*100, 2)
                                                     ).otherwise(0))
    df_ap = df_ap.withColumn('rx_decrypt_failures_rate', F.when(F.col('rx_pkts')!=0,
                                                      F.round(F.col('rx_decrypt_failures')/F.col('rx_pkts')*100, 2)
                                                     ).otherwise(0))    
    df_ap = df_ap.withColumn('rx_errors_rate_tot', F.when(F.col('rx_pkts_tot')!=0,
                                                      F.round(F.col('rx_errors_tot')/F.col('rx_pkts_tot')*100, 2)
                                                     ).otherwise(0))
    df_ap = df_ap.withColumn('rx_decrypt_failures_rate_tot', F.when(F.col('rx_pkts_tot')!=0,
                                                      F.round(F.col('rx_decrypt_failures_tot')/F.col('rx_pkts_tot')*100, 2)
                                                     ).otherwise(0)) 
    
    count_col = 'total_client_count'
    output_col = count_col + '_mean'
    df_ap = tools.get_mean(df_ap, entity_cols, count_col, output_col)
    count_col = 'active_client_count'
    output_col = count_col + '_mean'
    df_ap = tools.get_mean(df_ap, entity_cols, count_col, output_col)
    
    # get aggregated hourly data
    data_h = [ 'org_id', 'site_id', 'id', 'ap', 'model', 'dev', 
               'band', 'channel', 'timestamp_h', 
               'active_client_count_mean', 'total_client_count_mean', 
               'rx_decrypt_failures_tot', 'rx_pkts_tot',  'rx_errors_tot', 
               'tx_pkts_tot', 'tx_errors_tot', 'total_client_count_mean', 
               'rx_errors_rate_tot', 'rx_decrypt_failures_rate_tot', 're_init_tot']

    df_ap_h =  df_ap.select(data_h).dropDuplicates().persist()
    df_ap_h = df_ap_h.withColumnRenamed('timestamp_h', 'timestamp')
        
    ap_in = ['5c5b351e708a', '5c5b351e81f6', '5c5b351eb563']
    df_c_ap = df_c.where(F.col('ap').isin(ap_in))
    df_c_ap = df_c_ap.withColumn("timestamp", F.date_trunc('hour',F.col('When')))
    cols_out = ['org_id', 'site_id', 'wcid', 'ap', 'ev_type', 'metadata',  
                'title', 'wlan_id', 'text', 'When', 'timestamp']
    df_c_ap = df_c_ap.select(cols_out)
    ## Select targeted events 
    events = events_out + events_missing
    df_c_ap = df_c_ap.where(F.col('ev_type').isin(events))
    
    # get counts per h 
    entity_cols = ['org_id', 'site_id', 'ap', 'ev_type', 'timestamp']
    count_col = 'When'
    output_col = 'count_events'
    df_c_ap = tools.get_counts(df_c_ap, entity_cols, count_col, output_col)

    count_col = 'wcid'
    output_col = 'count_clients_by_event'
    df_c_ap = tools.get_distinct_counts(df_c_ap, entity_cols, count_col, output_col)

    entity_cols = ['org_id', 'site_id', 'ap', 'timestamp']
    count_col = 'wcid'
    output_col = 'count_clients_by_ap'
    df_c_ap = tools.get_distinct_counts(df_c_ap, entity_cols, count_col, output_col)
    # add % of affected clients by AP 
    df_c_ap = df_c_ap.withColumn('affected_clients', 
                                 F.col('count_clients_by_event')/F.col('count_clients_by_ap')*100)
    data_h = ['org_id', 'site_id', 'ap', 'ev_type', 
          'timestamp', 'count_events', 'count_clients_by_event', 
          'count_clients_by_ap', 'affected_clients']
    df_c_ap_h =  df_c_ap.select(data_h).dropDuplicates().persist()
    return [df_ap, df_c_ap, df_ap_h, df_c_ap_h]


In [ ]:
df_all_04_15 = ap21_data('2022-04-15')

In [ ]:
df_all_02_10 = ap21_data('2022-02-10')

In [ ]:
df_all_06_03 = ap21_data('2022-06-03')

In [ ]:
%%pretty
df_ap_04.where(F.col('ap')=='5c5b351e81f6').show(20, truncate=False)

In [ ]:
df_ap_04.where((F.col('ap')=='5c5b351e81f6') & (F.col('uptime')<1000)).show(10)

In [ ]:
test = df_ap_04a.where((F.col('ap')=='5c5b351e81f6')).select('uptime').collect()

In [ ]:
max([x.uptime for x in test])

In [ ]:
df_ap_04 = df_all_04_15[0]
df_c_ap_04 = df_all_04_15[1]
df_ap_h_04 = df_all_04_15[2]
df_c_ap_h_04 = df_all_04_15[3]

In [ ]:
df_ap_02 = df_all_02_10[0]
df_c_ap_02 = df_all_02_10[1]
df_ap_h_02 = df_all_02_10[2]
df_c_ap_h_02 = df_all_02_10[3]

df_ap_06 = df_all_06_03[0]
df_c_ap_06 = df_all_06_03[1]
df_ap_h_06 = df_all_06_03[2]
df_c_ap_h_06 = df_all_06_03[3]

In [ ]:
df_ap_04.printSchema()
df_c_ap_04.printSchema()
df_ap_h_04.printSchema()
df_c_ap_h_04.printSchema()

In [ ]:
df_ap_04.count()

In [ ]:
df_c_ap_04.count()

## READ SAVED DATA 

In [ ]:
#s3://mist-data-science-dev/marina/ap21/ap-stats-analytics-raw/dt=2022-02-09/part-00000-978d6827-47a5-4eaf-9878-704a58c0100e-c000.snappy.parquet

In [ ]:
date = '2022-02-*'
save_path_ap = "s3://mist-data-science-dev/marina/ap21/ap-stats-analytics-raw/dt="+ date + "/*.parquet"
print(save_path_ap)
df_ap = spark.read.parquet(save_path_ap, header=True)
df_ap.printSchema()

save_path_c = "s3://mist-data-science-dev/marina/ap21/es-client-event-raw/dt="+ date + "/*.parquet"
print(save_path_c)
df_c = spark.read.parquet(save_path_c, header=True)
df_c.printSchema()

In [ ]:
date = '2022-02-*'
save_path_ap = "s3://mist-data-science-dev/marina/ap21/ap-stats-analytics-raw/dt="+ date + "/*.parquet"
print(save_path_ap)
df_ap_02 = spark.read.parquet(save_path_ap, header=True)
save_path_c = "s3://mist-data-science-dev/marina/ap21/es-client-event-raw/dt="+ date + "/*.parquet"
print(save_path_c)
df_c_02 = spark.read.parquet(save_path_c, header=True)

In [ ]:
date = '2022-04-*'
save_path_ap = "s3://mist-data-science-dev/marina/ap21/ap-stats-analytics-raw/dt="+ date + "/*.parquet"
print(save_path_ap)
df_ap_04 = spark.read.parquet(save_path_ap, header=True)
save_path_c = "s3://mist-data-science-dev/marina/ap21/es-client-event-raw/dt="+ date + "/*.parquet"
print(save_path_c)
df_c_04 = spark.read.parquet(save_path_c, header=True)

In [ ]:
date = '2022-06-*'
save_path_ap = "s3://mist-data-science-dev/marina/ap21/ap-stats-analytics-raw/dt="+ date + "/*.parquet"
print(save_path_ap)
df_ap_06 = spark.read.parquet(save_path_ap, header=True)
save_path_c = "s3://mist-data-science-dev/marina/ap21/es-client-event-raw/dt="+ date + "/*.parquet"
print(save_path_c)
df_c_06 = spark.read.parquet(save_path_c, header=True)

In [ ]:
%%pretty
df_ap.where(F.col('ap')=='5c5b351eb563').show(20, truncate=False)

In [ ]:
df_ap.where((F.col('ap')=='5c5b351eb563') & (F.col('rx_decrypt_failures_rate')>100)).show(20, truncate=False)

In [ ]:
%%spark -o df_ap -n 10000 

In [ ]:
%%spark -o df_c -n 10000 

In [ ]:
c_test = df_c.where(F.col('ap')=='5c5b351eb563').select(['wcid']).collect()

In [ ]:
len(list(set([x.wcid for x in c_test])))

## Get DATA FOR PLOTS 

In [ ]:
%%spark -o df_ap_04 -n 10000 

In [ ]:
%%spark -o df_ap_02 -n 10000 

In [ ]:
%%spark -o df_c_02 -n 10000 

In [ ]:
%%spark -o df_c_04 -n 10000 

In [ ]:
%%spark -o df_ap_06 -n 10000 

In [ ]:
%%spark -o df_c_ap_04 -n 10000 

In [ ]:
%%spark -o df_c_ap_02 -n 10000 

In [ ]:
%%spark -o df_c_ap_06 -n 10000 

In [ ]:
df_ap_02.printSchema()

In [ ]:
df_ap.select(['band']).dropDuplicates().show(10)

### February plots 

In [ ]:
%%local
import plotly.graph_objects as go

## <=== HOURLY AGGREGATED  DATA ===>

ap_in = ['5c5b351e708a', '5c5b351e81f6', '5c5b351eb563']
metrics = ['rx_decrypt_failures_tot',
           'rx_pkts_tot',            
           'rx_errors_tot', 
           'tx_pkts_tot',
           'tx_errors_tot', 
           'total_client_count_mean', 
           'active_client_count_mean',
           're_init_tot',
           'rx_errors_rate_tot',
           'rx_decrypt_failures_rate_tot']

k = 2
#df = df_ap_06
dev = 'r0'
df = df_ap_02
test = df[(df['ap']==ap_in[k]) & (df['dev']==dev)][metrics+['timestamp_h','ap']].drop_duplicates()

# plot ststs data per metric 
fig = go.Figure()
for m in range(len(metrics)):
    fig = go.Figure()
    dd = test.sort_values('timestamp_h')
    fig.add_trace(go.Scatter(x=dd['timestamp_h'],
                             y=dd[metrics[m]],
                             mode='lines+markers', 
                             name=metrics[m]))
    fig.update_layout(title="AP metrics for ap "+ap_in[k] + " with dev "+ dev,
    xaxis_title="Time",
    yaxis_title=metrics[m])

    fig.show()

In [ ]:
%%local
import plotly.graph_objects as go

## <=== RAW DATA ===> 

ap_in = ['5c5b351e708a', '5c5b351e81f6', '5c5b351eb563']
metrics = ['rx_decrypt_failures_tot',
           'rx_pkts_tot',            
           'rx_errors_tot', 
           'tx_pkts_tot',
           'tx_errors_tot', 
           'total_client_count_mean', 
           'active_client_count_mean', 'uptime']

metrics = ['rx_decrypt_failures', 
           'rx_pkts', 
           'rx_errors', 
           'tx_pkts', 
           'tx_errors',
           're_init',
           'rx_errors_rate',
           'rx_decrypt_failures_rate', 'uptime'
          ]
k = 2
dev = 'r0'
df = df_ap_02
test = df[(df['ap']==ap_in[k]) & (df['dev']== dev)]

# plot ststs data per metric 
fig = go.Figure()
for m in range(len(metrics)):
    fig = go.Figure()
    dd = test.sort_values('timestamp')
    fig.add_trace(go.Scatter(x=dd['timestamp'],
                             y=dd[metrics[m]],
                             mode='lines+markers', 
                             name=metrics[m]))
    fig.update_layout(title="AP metrics for ap "+ ap_in[k] + " with dev "+ dev,
    xaxis_title="Time",
    yaxis_title=metrics[m])

    fig.show()

In [ ]:
%%local
import plotly.graph_objects as go
import plotly.express as px

ap_in = ['5c5b351e708a', '5c5b351e81f6', '5c5b351eb563']
metrics = ['count_events', 'count_clients_by_event', 'count_clients_by_ap', 'affected_clients']

events_out = ['CLIENT_AUTH_ASSOCIATION',
              'CLIENT_AUTHENTICATED',
              'CLIENT_AUTH_REASSOCIATION',
              'CLIENT_ASSOCIATION',
              'CLIENT_REASSOCIATION',
              'CLIENT_DEAUTHENTICATION',
              'CLIENT_DEASSOCIATION',
              'CLIENT_DEAUTHENTICATED',
              'STA_DOS_DISASSOC',
              'CLIENT_AUTH_ASSOCIATION_OKC',
              'CLIENT_AUTHENTICATED_11R',
              'CLIENT_AUTH_REASSOCIATION_OKC',
              'CLIENT_AUTH_REASSOCIATION_11R']
events_missing = ['MARVIS_EVENT_CLIENT_AUTH_FAILURE',
                  'REPEATED_AUTH_FAILURES',
                  'CLIENT_ASSOCIATION_FAILURE']


k = 2
df = df_c_02
test = df[df['ap']==ap_in[k]]

# plot ststs for events

fig = go.Figure()
for et in events_out+events_missing:
    dd = test[test['ev_type'] == et]
    dd = dd.sort_values('timestamp')
    #dd['tt'] = p
    fig.add_trace(go.Scatter(x = dd['timestamp'],
                             #y = dd['tt'],
                             y = dd['ev_type'],
                             mode = 'lines+markers',
                             #mode = 'markers',
                             marker=dict(size=12),
                             #mode = 'markers',
                             name = et))
    fig.update_layout(title="Client Events data for ap "+ap_in[k],
    xaxis_title="Time",
    yaxis_title='event type')

fig.show()

In [ ]:
%%local
import plotly.graph_objects as go
import plotly.express as px

ap_in = ['5c5b351e708a', '5c5b351e81f6', '5c5b351eb563']
metrics = ['count_events', 'count_clients_by_event', 'count_clients_by_ap', 'affected_clients']

events_out = ['CLIENT_AUTH_ASSOCIATION',
              'CLIENT_AUTHENTICATED',
              'CLIENT_AUTH_REASSOCIATION',
              'CLIENT_ASSOCIATION',
              'CLIENT_REASSOCIATION',
              'CLIENT_DEAUTHENTICATION',
              'CLIENT_DEASSOCIATION',
              'CLIENT_DEAUTHENTICATED',
              'STA_DOS_DISASSOC',
              'CLIENT_AUTH_ASSOCIATION_OKC',
              'CLIENT_AUTHENTICATED_11R',
              'CLIENT_AUTH_REASSOCIATION_OKC',
              'CLIENT_AUTH_REASSOCIATION_11R']
events_missing = ['MARVIS_EVENT_CLIENT_AUTH_FAILURE',
                  'REPEATED_AUTH_FAILURES',
                  'CLIENT_ASSOCIATION_FAILURE']


k = 2
df = df_c
test = df[df['ap']==ap_in[k]]

# plot ststs data per metric 
for m in range(len(metrics)):
    fig = go.Figure()
    for et in events_out+events_missing:
        dd = test[test['ev_type']==et]
        dd = dd.sort_values('timestamp')
        fig.add_trace(go.Scatter(x =dd['timestamp'],
                                 y =dd[metrics[m]],
                                 mode = 'lines+markers',
                                 #mode = 'markers',
                                 marker=dict(size=12),
                                 #mode = 'markers',
                                 name = et))
        fig.update_layout(title="Client Events data for ap "+ap_in[k],
        xaxis_title="Time",
        yaxis_title=metrics[m])
    fig.show()

### April plots 

In [ ]:
%%local
import plotly.graph_objects as go

## <=== HOURLY AGGREGATED  DATA ===>

ap_in = ['5c5b351e708a', '5c5b351e81f6', '5c5b351eb563']
metrics = ['rx_decrypt_failures_tot',
           'rx_pkts_tot',            
           'rx_errors_tot', 
           'tx_pkts_tot',
           'tx_errors_tot', 
           'total_client_count_mean', 
           'active_client_count_mean',
           're_init_tot',
           'rx_errors_rate_tot',
           'rx_decrypt_failures_rate_tot']

k = 1
#df = df_ap_06
dev = 'r1'
df = df_ap_04
test = df[(df['ap']==ap_in[k]) & (df['dev']==dev)][metrics+['timestamp_h','ap']].drop_duplicates()

# plot ststs data per metric 
fig = go.Figure()
for m in range(len(metrics)):
    fig = go.Figure()
    dd = test.sort_values('timestamp_h')
    fig.add_trace(go.Scatter(x=dd['timestamp_h'],
                             y=dd[metrics[m]],
                             mode='lines+markers', 
                             name=metrics[m]))
    fig.update_layout(title="AP metrics for ap "+ap_in[k] + " with dev "+ dev,
    xaxis_title="Time",
    yaxis_title=metrics[m])

    fig.show()

In [ ]:
%%local
import plotly.graph_objects as go

## <=== RAW DATA ===> 

ap_in = ['5c5b351e708a', '5c5b351e81f6', '5c5b351eb563']
metrics = ['rx_decrypt_failures_tot',
           'rx_pkts_tot',            
           'rx_errors_tot', 
           'tx_pkts_tot',
           'tx_errors_tot', 
           'total_client_count_mean', 
           'active_client_count_mean', 'uptime']

metrics = ['rx_decrypt_failures', 
           'rx_pkts', 
           'rx_errors', 
           'tx_pkts', 
           'tx_errors',
           're_init',
           'rx_errors_rate',
           'rx_decrypt_failures_rate', 'uptime'
          ]
k = 1
dev = 'r1'
df = df_ap_04
test = df[(df['ap']==ap_in[k]) & (df['dev']== dev)]

# plot ststs data per metric 
fig = go.Figure()
for m in range(len(metrics)):
    fig = go.Figure()
    dd = test.sort_values('timestamp')
    fig.add_trace(go.Scatter(x=dd['timestamp'],
                             y=dd[metrics[m]],
                             mode='lines+markers', 
                             name=metrics[m]))
    fig.update_layout(title="AP metrics for ap "+ ap_in[k] + " with dev "+ dev,
    xaxis_title="Time",
    yaxis_title=metrics[m])

    fig.show()

In [ ]:
%%local
import plotly.graph_objects as go
import plotly.express as px

ap_in = ['5c5b351e708a', '5c5b351e81f6', '5c5b351eb563']
metrics = ['count_events', 'count_clients_by_event', 'count_clients_by_ap', 'affected_clients']

events_out = ['CLIENT_AUTH_ASSOCIATION',
              'CLIENT_AUTHENTICATED',
              'CLIENT_AUTH_REASSOCIATION',
              'CLIENT_ASSOCIATION',
              'CLIENT_REASSOCIATION',
              'CLIENT_DEAUTHENTICATION',
              'CLIENT_DEASSOCIATION',
              'CLIENT_DEAUTHENTICATED',
              'STA_DOS_DISASSOC',
              'CLIENT_AUTH_ASSOCIATION_OKC',
              'CLIENT_AUTHENTICATED_11R',
              'CLIENT_AUTH_REASSOCIATION_OKC',
              'CLIENT_AUTH_REASSOCIATION_11R']
events_missing = ['MARVIS_EVENT_CLIENT_AUTH_FAILURE',
                  'REPEATED_AUTH_FAILURES',
                  'CLIENT_ASSOCIATION_FAILURE']


k = 1
df = df_c_04
test = df[df['ap']==ap_in[k]]

# plot ststs for events

fig = go.Figure()
for et in events_out+events_missing:
    dd = test[test['ev_type'] == et]
    dd = dd.sort_values('timestamp')
    #dd['tt'] = p
    fig.add_trace(go.Scatter(x = dd['timestamp'],
                             #y = dd['tt'],
                             y = dd['ev_type'],
                             mode = 'lines+markers',
                             #mode = 'markers',
                             marker=dict(size=12),
                             #mode = 'markers',
                             name = et))
    fig.update_layout(title="Client Events data for ap "+ap_in[k],
    xaxis_title="Time",
    yaxis_title='event type')

fig.show()

In [ ]:
%%local
import plotly.graph_objects as go
import plotly.express as px

ap_in = ['5c5b351e708a', '5c5b351e81f6', '5c5b351eb563']
metrics = ['count_events', 'count_clients_by_event', 'count_clients_by_ap', 'affected_clients']

events_out = ['CLIENT_AUTH_ASSOCIATION',
              'CLIENT_AUTHENTICATED',
              'CLIENT_AUTH_REASSOCIATION',
              'CLIENT_ASSOCIATION',
              'CLIENT_REASSOCIATION',
              'CLIENT_DEAUTHENTICATION',
              'CLIENT_DEASSOCIATION',
              'CLIENT_DEAUTHENTICATED',
              'STA_DOS_DISASSOC',
              'CLIENT_AUTH_ASSOCIATION_OKC',
              'CLIENT_AUTHENTICATED_11R',
              'CLIENT_AUTH_REASSOCIATION_OKC',
              'CLIENT_AUTH_REASSOCIATION_11R']
events_missing = ['MARVIS_EVENT_CLIENT_AUTH_FAILURE',
                  'REPEATED_AUTH_FAILURES',
                  'CLIENT_ASSOCIATION_FAILURE']


k = 1
df = df_c_04
test = df[df['ap']==ap_in[k]]

# plot ststs data per metric 
for m in range(len(metrics)):
    fig = go.Figure()
    for et in events_out+events_missing:
        dd = test[test['ev_type']==et]
        dd = dd.sort_values('timestamp')
        fig.add_trace(go.Scatter(x =dd['timestamp'],
                                 y =dd[metrics[m]],
                                 mode = 'lines+markers',
                                 #mode = 'markers',
                                 marker=dict(size=12),
                                 #mode = 'markers',
                                 name = et))
        fig.update_layout(title="Client Events data for ap "+ap_in[k],
        xaxis_title="Time",
        yaxis_title=metrics[m])
    fig.show()

In [ ]:
### April data 

## PLOTS  FOR RAW DATA

In [ ]:
%%local
import plotly.graph_objects as go

ap_in = ['5c5b351e708a', '5c5b351e81f6', '5c5b351eb563']
metrics = ['rx_decrypt_failures_tot',
           'rx_pkts_tot',            
           'rx_errors_tot', 
           'tx_pkts_tot',
           'tx_errors_tot', 
           'total_client_count_mean', 
           'active_client_count_mean',
           're_init_tot',
           'rx_errors_rate_tot',
           'rx_decrypt_failures_rate_tot']

k = 2
#df = df_ap_06
df = df_ap
test = df[df['ap']==ap_in[k]][metrics+['timestamp_h','ap']].drop_duplicates()

# plot ststs data per metric 
fig = go.Figure()
for m in range(len(metrics)):
    fig = go.Figure()
    dd = test.sort_values('timestamp_h')
    fig.add_trace(go.Scatter(x=dd['timestamp_h'],
                             y=dd[metrics[m]],
                             mode='lines+markers', 
                             name=metrics[m]))
    fig.update_layout(title="AP metrics for ap "+ap_in[k],
    xaxis_title="Time",
    yaxis_title=metrics[m])

    fig.show()

In [ ]:
%%local
import plotly.graph_objects as go

ap_in = ['5c5b351e708a', '5c5b351e81f6', '5c5b351eb563']
metrics = ['rx_decrypt_failures_tot',
           'rx_pkts_tot',            
           'rx_errors_tot', 
           'tx_pkts_tot',
           'tx_errors_tot', 
           'total_client_count_mean', 
           'active_client_count_mean', 'uptime']
metrics = ['rx_decrypt_failures', 
           'rx_pkts', 
           'rx_errors', 
           'tx_pkts', 
           'tx_errors',
           're_init',
           'rx_errors_rate',
           'rx_decrypt_failures_rate', 'uptime'
          ]
k = 1
df = df_ap_06
test = df[df['ap']==ap_in[k]]

# plot ststs data per metric 
fig = go.Figure()
for m in range(len(metrics)):
    fig = go.Figure()
    dd = test.sort_values('timestamp')
    fig.add_trace(go.Scatter(x=dd['timestamp'],
                             y=dd[metrics[m]],
                             mode='lines+markers', 
                             name=metrics[m]))
    fig.update_layout(title="AP metrics for ap "+ap_in[k],
    xaxis_title="Time",
    yaxis_title=metrics[m])

    fig.show()

In [ ]:
%%local
import plotly.graph_objects as go
import plotly.express as px

ap_in = ['5c5b351e708a', '5c5b351e81f6', '5c5b351eb563']
metrics = ['count_events', 'count_clients_by_event', 'count_clients_by_ap', 'affected_clients']

events_out = ['CLIENT_AUTH_ASSOCIATION',
              'CLIENT_AUTHENTICATED',
              'CLIENT_AUTH_REASSOCIATION',
              'CLIENT_ASSOCIATION',
              'CLIENT_REASSOCIATION',
              'CLIENT_DEAUTHENTICATION',
              'CLIENT_DEASSOCIATION',
              'CLIENT_DEAUTHENTICATED',
              'STA_DOS_DISASSOC',
              'CLIENT_AUTH_ASSOCIATION_OKC',
              'CLIENT_AUTHENTICATED_11R',
              'CLIENT_AUTH_REASSOCIATION_OKC',
              'CLIENT_AUTH_REASSOCIATION_11R']
events_missing = ['MARVIS_EVENT_CLIENT_AUTH_FAILURE',
                  'REPEATED_AUTH_FAILURES',
                  'CLIENT_ASSOCIATION_FAILURE']


k = 1
df = df_c_ap_06
test = df[df['ap']==ap_in[k]]

# plot ststs data per metric
for m in range(len(metrics)):
    fig = go.Figure()
    p=1
    for et in events_out+events_missing:
        dd = test[test['ev_type'] == et]
        dd = dd.sort_values('timestamp')
        dd['tt'] = p
        fig.add_trace(go.Scatter(x = dd['timestamp'],
                                 #y = dd['tt'],
                                 y = dd['ev_type'],
                                 mode = 'lines+markers',
                                 #mode = 'markers',
                                 marker=dict(size=12),
                                 #mode = 'markers',
                                 name = et))
        fig.update_layout(title="Client Events data for ap "+ap_in[k],
        xaxis_title="Time",
        yaxis_title='even id')
        p = p+1
    fig.show()

In [ ]:
%%local
import plotly.graph_objects as go
import plotly.express as px

ap_in = ['5c5b351e708a', '5c5b351e81f6', '5c5b351eb563']
metrics = ['count_events', 'count_clients_by_event', 'count_clients_by_ap', 'affected_clients']

events_out = ['CLIENT_AUTH_ASSOCIATION',
              'CLIENT_AUTHENTICATED',
              'CLIENT_AUTH_REASSOCIATION',
              'CLIENT_ASSOCIATION',
              'CLIENT_REASSOCIATION',
              'CLIENT_DEAUTHENTICATION',
              'CLIENT_DEASSOCIATION',
              'CLIENT_DEAUTHENTICATED',
              'STA_DOS_DISASSOC',
              'CLIENT_AUTH_ASSOCIATION_OKC',
              'CLIENT_AUTHENTICATED_11R',
              'CLIENT_AUTH_REASSOCIATION_OKC',
              'CLIENT_AUTH_REASSOCIATION_11R']
events_missing = ['MARVIS_EVENT_CLIENT_AUTH_FAILURE',
                  'REPEATED_AUTH_FAILURES',
                  'CLIENT_ASSOCIATION_FAILURE']


k = 1
df = df_c_ap_04
test = df[df['ap']==ap_in[k]]

# plot ststs data per metric 
for m in range(len(metrics)):
    fig = go.Figure()
    for et in events_out+events_missing:
        dd = test[test['ev_type']==et]
        dd = dd.sort_values('timestamp')
        fig.add_trace(go.Scatter(x =dd['timestamp'],
                                 y =dd[metrics[m]],
                                 mode = 'lines+markers',
                                 #mode = 'markers',
                                 marker=dict(size=12),
                                 #mode = 'markers',
                                 name = et))
        fig.update_layout(title="Client Events data for ap "+ap_in[k],
        xaxis_title="Time",
        yaxis_title=metrics[m])
    fig.show()

## Save data 

In [ ]:
# <=== SAVE DATA ===>
save_path = "s3://mist-data-science-dev/marina/ap21/ap-stats-analytics/dt="+ date + "/"
print(save_path)
df_ap_h.coalesce(1).write.save(save_path, format='parquet', mode='overwrite', header=True)

# <=== SAVE C data ===>
save_path = "s3://mist-data-science-dev/marina/ap21/es-client-event/dt="+ date + "/"
print(save_path)
df_c_ap_h.coalesce(1).write.save(save_path, format='parquet', mode='overwrite', header=True)

## COLLECTED DATA TESTS 

In [ ]:
date = '2022-06-01'
hour = []
env ='production'
# ap stats
sites = ['0a878d43-e796-4120-8cd8-b7359600af16', '41c289fa-a8e5-4b83-aa28-fb9d265dab26']
ap_in = ['5c-5b-35-1e-70-8a', '5c-5b-35-1e-81-f6', '5c-5b-35-1e-b5-63']
fields_in_data  = ['rx_decrypt_failures', 'rx_pkts', 'rx_errors', 'tx_pkts', 'tx_errors'] # in radio
ap_fields = ['org_id',
             'site_id',
             'id',
             'model', 
             'total_client_count', 
             'active_client_count', 
             'terminator_timestamp', 
             'timestamp']

In [ ]:
date = '2022-04-15'
hour = []
env ='production'
# ap stats
sites = ['0a878d43-e796-4120-8cd8-b7359600af16', '41c289fa-a8e5-4b83-aa28-fb9d265dab26']
ap_in = ['5c-5b-35-1e-70-8a', '5c-5b-35-1e-81-f6', '5c-5b-35-1e-b5-63']
fields_in_data  = ['rx_decrypt_failures', 'rx_pkts', 'rx_errors', 'tx_pkts', 'tx_errors']
ap_fields = ['site_id',
             'org_id',
             'id',
             'model', 
             'total_client_count', 
             'active_client_count', 'terminator_timestamp', 'timestamp']
# AP data 
df = get_ap_stats(date, hour, env, sites) 
# Client data 
df_c = get_es_client_data(date, hour, env, sites)
# df.printSchema()
# df_c.printSchema()

In [ ]:
df_c.printSchema()

In [ ]:
# select a list of AP 
ap_in = ['5c-5b-35-1e-70-8a', '5c-5b-35-1e-81-f6', '5c-5b-35-1e-b5-63']
df_ap = df.where(F.col('id').isin(ap_in))
df_ap = df_ap.withColumn("radios", F.explode("radios")).select("*", F.col("radios.*"))
df_ap = df_ap.withColumn('ap',  F.regexp_replace('id', '-', ''))
df_ap = df_ap.select(ap_fields + fields_in_data)
df_ap = df_ap.withColumn("timestamp_h", F.date_trunc('hour',F.col('timestamp')))

df_ap = df_ap.withColumn('ap',  F.regexp_replace('id', '-', ''))

In [ ]:
# get counts per h 
entity_cols = ['org_id', 'site_id', 'id', 'ap', 'model', 'timestamp_h']
for mm in fields_in_data:  
    count_col = mm
    output_col = mm + '_tot'
    df_ap = tools.get_sum(df_ap, entity_cols, count_col, output_col)
    #output_col_m = mm + '_mean'
    #df_ap = df_ap.withColumn(output_col_m , F.col(output_col)/3600)
count_col = 'total_client_count'
output_col = count_col + '_mean'
df_ap = tools.get_mean(df_ap, entity_cols, count_col, output_col)
count_col = 'active_client_count'
output_col = count_col + '_mean'
df_ap = tools.get_mean(df_ap, entity_cols, count_col, output_col)
    
#df_ap = tools.get_mean(df_ap, entity_cols, count_col, output_col)
    

In [ ]:
df_ap.printSchema()

In [ ]:
%%pretty
df_ap.where(F.col('id')=='5c-5b-35-1e-81-f6').show(10, truncate=False)

In [ ]:
# select a list of AP for client data 
ap_in = ['5c5b351e708a', '5c5b351e81f6', '5c5b351eb563']
df_c_ap = df_c.where(F.col('ap').isin(ap_in))
df_c_ap = df_c_ap.withColumn("timestamp", F.date_trunc('hour',F.col('When')))
cols_out = ['org_id', 'site_id', 'wcid', 'ap', 'ev_type', 'metadata',  
            'title', 'wlan_id', 'text', 'When', 'timestamp']
df_c_ap = df_c_ap.select(cols_out)
## Select targeted events 
events = events_out + events_missing
df_c_ap = df_c_ap.where(F.col('ev_type').isin(events))

In [ ]:
# get counts per h 
entity_cols = ['org_id', 'site_id', 'ap', 'ev_type', 'timestamp']
count_col = 'When'
output_col = 'count_events'
df_c_ap = tools.get_counts(df_c_ap, entity_cols, count_col, output_col)

count_col = 'wcid'
output_col = 'count_clients_by_event'
df_c_ap = tools.get_distinct_counts(df_c_ap, entity_cols, count_col, output_col)

entity_cols = ['org_id', 'site_id', 'ap', 'timestamp']
count_col = 'wcid'
output_col = 'count_clients_by_ap'
df_c_ap = tools.get_distinct_counts(df_c_ap, entity_cols, count_col, output_col)
# add % of affected clients by AP 
df_c_ap = df_c_ap.withColumn('affected_clients', 
                             F.col('count_clients_by_event')/F.col('count_clients_by_ap')*100)

In [ ]:
# get aggregated hourly data
data_h = ['org_id', 'site_id', 'id', 'ap', 'model', 'total_client_count', 'active_client_count', 
        'timestamp_h', 'rx_decrypt_failures_tot', 'rx_pkts_tot',  'rx_errors_tot', 
        'tx_pkts_tot', 'tx_errors_tot', 'total_client_count_mean', 'active_client_count_mean']

df_ap_h =  df_ap.select(data_h).dropDuplicates().persist()
df_ap_h = df_ap_h.withColumnRenamed('timestamp_h', 'timestamp')

In [ ]:
data_h = ['org_id', 'site_id', 'ap', 'ev_type', 
          'timestamp', 'count_events', 'count_clients_by_event', 
          'count_clients_by_ap', 'affected_clients']
df_c_ap_h =  df_c_ap.select(data_h).dropDuplicates().persist()

In [ ]:
save_path = "s3://mist-data-science-dev/marina/ap21/ap-stats-analytics/dt="+ date + "/"
print(save_path)
df_ap_h.write.save(save_path, format='parquet', mode='overwrite', header=True)

In [ ]:
a=1

In [ ]:
# <=== SAVE DATA 
save_path = "s3://mist-data-science-dev/marina/ap21/ap-stats-analytics/dt="+ date + "/"
print(save_path)
df_ap_h.coalesce(1).write.save(save_path, format='parquet', mode='overwrite', header=True)
# <=== SAVE C data 
save_path = "s3://mist-data-science-dev/marina/ap21/es-client-event/dt="+ date + "/"
print(save_path)
df_c_ap_h.coalesce(1).write.save(save_path, format='parquet', mode='overwrite', header=True)

In [ ]:
df_ap.select('timestamp').dropDuplicates().show(25)

In [ ]:
df_ap.select('timestamp').dropDuplicates().count()

In [ ]:
df_ap.select('timestamp_h').dropDuplicates().count()

In [ ]:
df_c_ap.columns

In [ ]:
# get aggregated hourly data
data_h = ['org_id', 'site_id', 'id', 'ap', 'model', 'total_client_count', 'active_client_count', 
        'timestamp_h', 'rx_decrypt_failures_tot', 'rx_pkts_tot',  'rx_errors_tot', 
        'tx_pkts_tot', 'tx_errors_tot', 'total_client_count_mean', 'active_client_count_mean']

df_ap_h =  df_ap.select(data_h).dropDuplicates()

In [ ]:
data_h = ['org_id', 'site_id', 'ap', 'ev_type', 
          'timestamp', 'count_events', 'count_clients_by_event', 
          'count_clients_by_ap', 'affected_clients']
df_c_ap_h =  df_c_ap.select(data_h).dropDuplicates()

In [ ]:
df_c_ap_h.show(10, truncate=False)

In [ ]:
%%pretty
df_ap_h.orderBy(F.col( 'timestamp_h')).show(20, truncate=False)

In [ ]:
%%pretty
df_c_ap_h.orderBy(F.col( 'timestamp')).show(20, truncate=False)

In [ ]:
%%pretty
df_ap.show(10, truncate=False)

In [ ]:
df_ap.columns

In [ ]:
%%pretty
df_c_ap.show(10, truncate=False)

In [ ]:
df_ap.count()


In [ ]:
df_c_ap.count()

In [ ]:
df_c_ap.columns

In [ ]:
## Need to count events and "affected clients"  clients taht experience events among all clients 

In [ ]:
df_c.printSchema()

In [ ]:
df_c.columns

In [ ]:
%%pretty
df_c.show(10, truncate=False)

5c5b351eb563 : Feb 10 16:55 UTC
5c5b351eb563 is assigned to Site[Main Building] 
under Org[Mount Pleasant Christian Church]     

In [ ]:
# Follow the events 
date = '2022-02-10'
hour = []
df1 = get_ap_stats(date, hour, env)
df_c1 = get_es_client_data(date, hour, env)
df1.printSchema()

In [ ]:
# Follow the events 
date = '2022-02-10'
hour = '*'
df_cc1 =  get_client_stats(date, hour, env)

In [ ]:
date = '2022-04-15'
hour = []
df = get_ap_stats(date, hour, env)  
df_c = get_es_client_data(date, hour, env)
df.printSchema()

In [ ]:
# Follow the events 
date = '2022-04-15'
hour = '*'
df_cc =  get_client_stats(date, hour, env)

In [ ]:
df_c_ap_h.columns

In [ ]:
metrics = ['count_events', 'count_clients_by_event', 'count_clients_by_ap', 'affected_clients']
for m in metrics:
    df_c_ap_h= df_c_ap_h.withColumn(m, F.when(F.col('ev_type').isin(events_missing), 
                                             -1*F.col(m)).otherwise(F.col(m)))

## GET COLECTED DATA 

In [ ]:
path_6 = "s3://mist-data-science-dev/marina/ap21/es-client-event/dt=2022-06-*/*.parquet"

In [ ]:
df6 = spark.read.parquet(path_6)

In [ ]:
df6.printSchema()

In [ ]:
path_6a ="s3://mist-data-science-dev/marina/ap21/ap-stats-analytics/dt=2022-06-*/*.parquet"

In [ ]:
df6a = spark.read.parquet(path_6a)

In [ ]:
df6a.printSchema()

## Plot

In [ ]:
%%spark -o df_ap -n 10000 

In [ ]:
a=1

In [ ]:
%%spark -o df_c_ap -n 10000 

In [ ]:
%%spark -o df6 -n 10000 

In [ ]:
%%spark -o df6a -n 10000 

In [ ]:
%%spark -o df_c_ap_h -n 10000 

In [ ]:
a=1

In [ ]:
%%spark -o df_ap_h -n 10000 

In [ ]:
%%local
import plotly.graph_objects as go

ap_in = ['5c5b351e708a', '5c5b351e81f6', '5c5b351eb563']
metrics = ['rx_decrypt_failures_tot',
           'rx_pkts_tot',            
           'rx_errors_tot', 
           'tx_pkts_tot',
           'tx_errors_tot', 
           'total_client_count_mean', 
           'active_client_count_mean']

k=0
df = df_ap_h
test = df[df['ap']==ap_in[k]]

# plot ststs data per metric 
fig = go.Figure()

for m in range(len(metrics)):
    fig = go.Figure()
    dd = test.sort_values('timestamp')
    fig.add_trace(go.Scatter(x=dd['timestamp'],
                             y=dd[metrics[m]],
                             mode='lines+markers', 
                             name=metrics[m]))
    fig.update_layout(title="AP metrics for ap "+ap_in[k],
    xaxis_title="Time",
    yaxis_title=metrics[m])

    fig.show()

In [ ]:
%%local
import plotly.graph_objects as go
import plotly.express as px

ap_in = ['5c5b351e708a', '5c5b351e81f6', '5c5b351eb563']
metrics = ['count_events', 'count_clients_by_event', 'count_clients_by_ap', 'affected_clients']

events_out = ['CLIENT_AUTH_ASSOCIATION',
              'CLIENT_AUTHENTICATED',
              'CLIENT_AUTH_REASSOCIATION',
              'CLIENT_ASSOCIATION',
              'CLIENT_REASSOCIATION',
              'CLIENT_DEAUTHENTICATION',
              'CLIENT_DEASSOCIATION',
              'CLIENT_DEAUTHENTICATED',
              'STA_DOS_DISASSOC',
              'CLIENT_AUTH_ASSOCIATION_OKC',
              'CLIENT_AUTHENTICATED_11R',
              'CLIENT_AUTH_REASSOCIATION_OKC',
              'CLIENT_AUTH_REASSOCIATION_11R']


# AUTH_SUCC_LIST + ASSO_SUCC_LIST + NEUTRAL_LIST

events_missing = ['MARVIS_EVENT_CLIENT_AUTH_FAILURE',
                  'REPEATED_AUTH_FAILURES',
                  'CLIENT_ASSOCIATION_FAILURE']


k=0
df = df_c_ap_h
test = df[df['ap']==ap_in[k]]

# plot ststs data per metric 

for m in range(len(metrics)):
    fig = go.Figure()
    for et in events_out+events_missing:
        dd = test[test['ev_type']==et]
        dd = dd.sort_values('timestamp')
        fig.add_trace(go.Scatter(x =dd['timestamp'],
                                 y =dd[metrics[m]],
                                 mode = 'lines+markers',
                                 #mode = 'markers',
                                 marker=dict(size=12),
                                 #mode = 'markers',
                                 name = et))
        fig.update_layout(title="Client Events data for ap "+ap_in[k],
        xaxis_title="Time",
        yaxis_title=metrics[m])
    fig.show()

In [ ]:
%%local
import plotly.graph_objects as go

ap_in = ['5c5b351e708a', '5c5b351e81f6', '5c5b351eb563']
metrics = ['rx_decrypt_failures_tot',
           'rx_pkts_tot',            
           'rx_errors_tot', 
           'tx_pkts_tot',
           'tx_errors_tot', 
           'total_client_count_mean', 
           'active_client_count_mean']

k=2
test = df6a[df6a['ap']==ap_in[k]]

# plot ststs data per metric 
fig = go.Figure()

for m in range(len(metrics)):
    fig = go.Figure()
    dd = test.sort_values('timestamp')
    fig.add_trace(go.Scatter(x=dd['timestamp'],
                             y=dd[metrics[m]],
                             mode='lines+markers', 
                             name=metrics[m]))
    fig.update_layout(title="AP metrics for ap "+ap_in[k],
    xaxis_title="Time",
    yaxis_title=metrics[m])

    fig.show()

# events_out

In [ ]:
%%local
import plotly.graph_objects as go
import plotly.express as px

ap_in = ['5c5b351e708a', '5c5b351e81f6', '5c5b351eb563']
metrics = ['count_events', 'count_clients_by_event', 'count_clients_by_ap', 'affected_clients']

events_out = ['CLIENT_AUTH_ASSOCIATION',
              'CLIENT_AUTHENTICATED',
              'CLIENT_AUTH_REASSOCIATION',
              'CLIENT_ASSOCIATION',
              'CLIENT_REASSOCIATION',
              'CLIENT_DEAUTHENTICATION',
              'CLIENT_DEASSOCIATION',
              'CLIENT_DEAUTHENTICATED',
              'STA_DOS_DISASSOC',
              'CLIENT_AUTH_ASSOCIATION_OKC',
              'CLIENT_AUTHENTICATED_11R',
              'CLIENT_AUTH_REASSOCIATION_OKC',
              'CLIENT_AUTH_REASSOCIATION_11R']


# AUTH_SUCC_LIST + ASSO_SUCC_LIST + NEUTRAL_LIST

events_missing = ['MARVIS_EVENT_CLIENT_AUTH_FAILURE',
                  'REPEATED_AUTH_FAILURES',
                  'MARVIS_EVENT_CLIENT_AUTH_FAILURE', 
                  'CLIENT_ASSOCIATION_FAILURE']


k=2
test = df6[df6['ap']==ap_in[k]]

# plot ststs data per metric 

for m in range(len(metrics)):
    fig = go.Figure()
    for et in events_out:
        dd = test[test['ev_type']==et]
        dd = dd.sort_values('timestamp')
        fig.add_trace(go.Scatter(x =dd['timestamp'],
                                 y =dd[metrics[m]],
                                 mode = 'lines+markers',
                                 #mode = 'markers',
                                 marker=dict(size=12),
                                 #mode = 'markers',
                                 name = et))
        fig.update_layout(title="Client Events data for ap "+ap_in[k],
        xaxis_title="Time",
        yaxis_title=metrics[m])
    fig.show()
    


## Ticket Case: 'College Park Church'

In [ ]:
df_name.where((F.col('org_name') == 'College Park Church') |
              (F.col('org_name') == 'Mount Pleasant Christian Church')
             ).show(10, truncate=False)

In [ ]:
[['Mount Pleasant Christian Church', 
  'Main Building', 
  '41c289fa-a8e5-4b83-aa28-fb9d265dab26',
  '5c5b351eb563', ],
 ['College Park Church', 
  'North Indy Campus', 
  '0a878d43-e796-4120-8cd8-b7359600af16',
  '5c5b351eb563', 
  '5c5b351e81f6']
]

In [ ]:
# College Park Church
t_org_1.where(F.col('org_name') == 'College Park Church').show(10, truncate=False)

#### Case 1

In [ ]:
# Follow the events 
date = '2022-04-15'
site = ['0a878d43-e796-4120-8cd8-b7359600af16']
hour = []
df = get_ap_stats(date, hour, env, site) 
df.printSchema()

In [ ]:
# Follow the events 
date = '2022-04-15'
site = ['0a878d43-e796-4120-8cd8-b7359600af16']
hour = []
df_c = get_es_client_data(date, hour, env,  site)
df_c = df_c.where(F.col('ev_type').isin(events_out))
df_c.printSchema()

In [ ]:
# Follow the events 
date = '2022-04-15'
site = ['0a878d43-e796-4120-8cd8-b7359600af16']
hour = []
df_cc = get_client_stats(date, '*', env, site)
df_cc.printSchema()

#### Case 2 

In [ ]:
# Follow the events 
date = '2022-02-10'
site = ['41c289fa-a8e5-4b83-aa28-fb9d265dab26']
hour = []
df1 = get_ap_stats(date, hour, env, site) 
df1.printSchema()

In [ ]:
# Follow the events 
date = '2022-02-10'
site = ['41c289fa-a8e5-4b83-aa28-fb9d265dab26']
hour = []
df_c1 = get_es_client_data(date, hour, env,  site)
df_c1 = df_c1.where(F.col('ev_type').isin(events_out))
df_c1.printSchema()

In [ ]:
# Follow the events 
date = '2022-02-10'
site = ['41c289fa-a8e5-4b83-aa28-fb9d265dab26']
hour = []
df_cc1 = get_client_stats(date, '*', env, site)
df_cc1.printSchema()

### Client events data

In [ ]:
%%pretty
df_c.show(10, truncate=False)

In [ ]:
%%pretty
df_c1.show(10, truncate=False)

In [ ]:
## ap events during the day 
df_ca = df_c.where(F.col('ap')=="5c5b351e81f6")
## ap events during the day 
df_ca1 = df_c1.where(F.col('ap')=="5c5b351eb563")

In [ ]:
%%pretty
df_ca.orderBy(F.col('When'), F.col('wcid')).show(20, truncate=False)

In [ ]:
%%pretty
df_ca1.orderBy(F.col('When'), F.col('wcid')).show(20, truncate=False)

In [ ]:
df_ca.select('wcid').dropDuplicates().count()

In [ ]:
df_ca.printSchema()

In [ ]:
# events_out = AUTH_SUCC_LIST + ASSO_SUCC_LIST + NEUTRAL_LIST
# events_missing = AUTH_FAILURE_LIST + ASSO_FAILURE_LIST

In [ ]:
df_ca_pd = df_ca.toPandas()

In [ ]:
df_ca1_pd = df_ca1.toPandas()

In [ ]:
df_ca_pd[['wcid']].value_counts()

In [ ]:
df_ca_pd[['wcid', 'ev_type']].value_counts()

In [ ]:
cl_list = list(set(df_ca_pd['wcid']))

In [ ]:
cl_list

In [ ]:
df_ca_pd['ev_type'].value_counts()

In [ ]:
'CLIENT_AUTH_REASSOCIATION'        83
'CLIENT_AUTH_REASSOCIATION_11R'    25
'CLIENT_DEAUTHENTICATED '          16
'CLIENT_AUTH_ASSOCIATION'          14
'CLIENT_DEAUTHENTICATION'           6
'CLIENT_DEASSOCIATION'              3

In [ ]:
%%spark -o df_ca -n 10000

In [ ]:
%%local
import plotly.graph_objects as go

cl_list = ['2e576d16-5ade-3a39-6f33-ef758fdbb82d', 'e37a36db-1b54-8f43-e994-0ae52da30436', 
           'f528d96b-3a3a-ef89-6351-fa064d908c3c', '8e86a1ff-3b5f-4e51-484e-1e06931abf87', 
           '31be9684-01d4-16f4-bdb3-18743b2f4916', 'b1b26660-20b9-c0ba-56d6-d05b798b882d', 
           'd11de9b4-fa63-bf7d-3347-6850989d5fac', '49d23273-52ce-2b52-6319-cf9e8234fdab', 
           'ea56925e-2d2c-30b2-cfba-cd8ac19297bc', 'e3c23d1e-8e5e-0357-3f32-ad8fb4457a73', 
           'bf6ae8ae-a30a-c643-4d1e-5e23b1e11ece', '27d08e60-88d6-6584-e367-36393213dce5', 
           'd81cbd22-9fed-19ae-db52-9c22474a1b21', 'bb430a7d-8898-fbeb-fd25-98e47dcb314e', 
           '3f507493-7e23-03ed-403c-6e098517d38a', '08840bc8-7262-dec3-e425-b422eb1eec2b', 
           '1cc4b873-3a6b-44ef-bf47-2c9efb87b8a5', '3acadb0f-8a86-13fd-60f4-6a9861e67ffd', 
           'a64b8657-5979-c4e5-2c38-3cee2323a07a', 
           'cc041fa9-d37d-e3ff-0379-a25eb25f9045', 'd01111fe-b886-4768-b53e-013f775c0c45',
           '84697b49-f958-a6a5-f7cd-c2251529daba', '95ddf089-d44d-6e27-83df-97206e1eb7d1', 
           '5f22578e-c3e3-4e0b-5ddd-ab1dfaacb2d1', '38c56b61-597e-c1dc-5c12-00853bd869e8', 
           'c58e5c0b-dfdf-120b-8433-c33424d4881d', '805736c5-e5f0-48ad-817e-4134eee54e28',
           'da0ebb0b-2a49-9374-6fe3-262748459666', 'c9df083e-70c1-e7c9-df4a-fceaea9aef66', 
           '7d2cfb51-c440-2334-8abe-c57e01f9f71e', '86698c4f-d485-af93-afd9-46e42dbad961', 
           '73c003c3-30a4-1c1b-4ace-2c7ad58b32bc', 'c5d6af4f-4a9d-0f00-2e84-ca5d866b3495', 
           '67583fea-8413-5fb2-1f68-9261da0b30eb', 'a4dad20b-328e-270f-adb5-f469c492380a', 
           'c56559d4-156f-42fa-5cbf-399b81228859', '57f8e64c-76e2-093c-f56d-be6cce5478c8',
           '4724e53a-0d4b-200f-f6e2-601dce51d764', '53e08935-57ee-044b-d4a2-7d068340722b', 
           '06ba0d97-defb-1e89-db6a-497d63369b0d', 'e9a219db-5b35-a0f3-1bcd-0e81d38c3b43', 
           '3bee2ee4-930e-8a53-f4e0-3f96428d506a', '452ab224-9c9f-0a2b-f8db-e8faa1951002', 
           '49851880-f3f9-9641-4669-1b5c20a27988', '20c60a53-0e41-cdfa-83cd-cdd06648b48e', 
           '7e5c46df-667b-fe2e-8181-b3ebcfaa24c2', '8369de61-261b-7bf5-4001-de2bdd920d04']

top_clients = ['d81cbd22-9fed-19ae-db52-9c22474a1b21', 
               'e9a219db-5b35-a0f3-1bcd-0e81d38c3b43',
               'd81cbd22-9fed-19ae-db52-9c22474a1b21',
                '57f8e64c-76e2-093c-f56d-be6cce5478c8',
                'bf6ae8ae-a30a-c643-4d1e-5e23b1e11ece',
                '3f507493-7e23-03ed-403c-6e098517d38a',
               'c9df083e-70c1-e7c9-df4a-fceaea9aef66',
              'b1b26660-20b9-c0ba-56d6-d05b798b882d']
fig = go.Figure()
print('Data for: College Park Church, North Indy Campus')
print('org_id: 8c02eaa3-4275-4a6e-b2a8-f6673688e5ff')
print('site_id: 0a878d43-e796-4120-8cd8-b7359600af16')
print('ap:  5c5b351e81f6')
print('date: 04.15.2022')
print('top 8 clients with multiple REASSOCIATION events')
for c in top_clients:
    dd = df_ca.sort_values('When')
    dd  = dd[dd['wcid']==c]
    fig.add_trace(go.Scatter(x=dd['When'],
                             y=dd['ev_type'],
                             mode='lines+markers', 
                             name=c))
fig.show()

### AP data 

In [ ]:
df_ap = df.where(F.col('ap_id')=="5c-5b-35-1e-81-f6")

In [ ]:
from pyspark.sql.functions import explode
df_ap = df_ap.withColumn("radios", F.explode("radios")).select("*", F.col("radios.*"))

In [ ]:
sorted(df_ap.columns)

In [ ]:
df_ap.printSchema()

In [ ]:
fields = ['when', 'timestamp', 'tx_pkts', 'rx_pkts', 'total_client_count','active_client_count']

In [ ]:
%%pretty
df_ap.select(fields).orderBy(F.col('when')).show(10)

In [ ]:
df_ap2 = df_ap.select(fields)

In [ ]:
df_ap2.columns

In [ ]:
%%spark -o df_ap2 -n 10000

In [ ]:
%%local
import plotly.graph_objects as go

fig = go.Figure()
print('Data for: College Park Church, North Indy Campus')
print('org_id: 8c02eaa3-4275-4a6e-b2a8-f6673688e5ff')
print('site_id: 0a878d43-e796-4120-8cd8-b7359600af16')
print('ap:  5c5b351e81f6')
print('date: 04.15.2022')

dd = df_ap2.sort_values('timestamp')
fig.add_trace(go.Scatter(x=dd['timestamp'],
                         y=dd['tx_pkts'],
                         mode='lines+markers'))
fig.update_layout(
title="tx_pkts",
xaxis_title="Time",
yaxis_title="Client tx_pkts_sent")
fig.show()


fig = go.Figure()
fig.add_trace(go.Scatter(x=dd['timestamp'],
                         y=dd['rx_pkts'],
                         mode='lines+markers'))
fig.update_layout(
title="rx_pkts",
xaxis_title="Time",
yaxis_title="Client tx_pkts_sent")
fig.show()

In [ ]:
df_ap2.columns

In [ ]:
%%local
import plotly.graph_objects as go

fig = go.Figure()
print('Data for: College Park Church, North Indy Campus')
print('org_id: 8c02eaa3-4275-4a6e-b2a8-f6673688e5ff')
print('site_id: 0a878d43-e796-4120-8cd8-b7359600af16')
print('ap:  5c5b351e81f6')
print('date: 04.15.2022')
print('top 8 clients with multiple REASSOCIATION events')

dd = df_ap2.sort_values('timestamp')
fig.add_trace(go.Scatter(x=dd['timestamp'],
                         y=dd['tx_pkts'],
                         mode='lines+markers',
                         color=dd['total_client_count']))
fig.update_layout(
title="tx_pkts",
xaxis_title="Time",
yaxis_title="Client tx_pkts_sent")
fig.show()

fig = go.Figure()
fig.add_trace(go.Scatter(x=dd['timestamp'],
                         y=dd['rx_pkts'],
                         mode='lines+markers',
                         color=dd['total_client_count']))
fig.update_layout(
title="rx_pkts",
xaxis_title="Time",
yaxis_title="Client tx_pkts_sent")
fig.show()

In [ ]:
%%pretty
df_ap.select(fields).orderBy(F.col('when')).show(20, truncate=False)

In [ ]:
%%pretty
df_ap.select(fields).orderBy(F.col('when')).show(10)

### Client Stats Data

In [ ]:
df_ccc = df_cc.where(F.col('ap_id')=="5c-5b-35-1e-81-f6")

In [ ]:
df_ccc.count()

In [ ]:
%%pretty
df_ccc.select(['timestamp', 'ap_id', 'site_id', 'org_id', 'model', 'wlans', 'client_wcid', 
               'client_connected_time_sec', 'client_inactive_time_milli_sec', 
               'client_tx_bit_rate', 
               'client_tx_pkts_sent', 
               'client_rx_bit_rate','client_rx_pkts',
               'client_rxbps', 'client_rxpps', 'isActive',
               'client_os', 'client_model', 'ap_time']
             ).orderBy(F.col('timestamp')).show(20, truncate=False)

In [ ]:
test = df_ccc.select(['timestamp', 'ap_id', 'site_id', 'org_id', 'model', 'wlans', 'client_wcid', 
               'client_connected_time_sec', 'client_inactive_time_milli_sec', 
               'client_tx_bit_rate', 
               'client_tx_pkts_sent', 
               'client_rx_bit_rate','client_rx_pkts',
               'client_rxbps', 'client_rxpps', 'isActive',
               'client_os', 'client_model', 'ap_time']
             )

In [ ]:
test_pd = test.toPandas()

In [ ]:
%%spark -o test -n 10000

In [ ]:
%%local
import plotly.graph_objects as go

cl_list = ['2e576d16-5ade-3a39-6f33-ef758fdbb82d', 'e37a36db-1b54-8f43-e994-0ae52da30436', 
           'f528d96b-3a3a-ef89-6351-fa064d908c3c', '8e86a1ff-3b5f-4e51-484e-1e06931abf87', 
           '31be9684-01d4-16f4-bdb3-18743b2f4916', 'b1b26660-20b9-c0ba-56d6-d05b798b882d', 
           'd11de9b4-fa63-bf7d-3347-6850989d5fac', '49d23273-52ce-2b52-6319-cf9e8234fdab', 
           'ea56925e-2d2c-30b2-cfba-cd8ac19297bc', 'e3c23d1e-8e5e-0357-3f32-ad8fb4457a73', 
           'bf6ae8ae-a30a-c643-4d1e-5e23b1e11ece', '27d08e60-88d6-6584-e367-36393213dce5', 
           'd81cbd22-9fed-19ae-db52-9c22474a1b21', 'bb430a7d-8898-fbeb-fd25-98e47dcb314e', 
           '3f507493-7e23-03ed-403c-6e098517d38a', '08840bc8-7262-dec3-e425-b422eb1eec2b', 
           '1cc4b873-3a6b-44ef-bf47-2c9efb87b8a5', '3acadb0f-8a86-13fd-60f4-6a9861e67ffd', 
           'a64b8657-5979-c4e5-2c38-3cee2323a07a', 
           'cc041fa9-d37d-e3ff-0379-a25eb25f9045', 'd01111fe-b886-4768-b53e-013f775c0c45',
           '84697b49-f958-a6a5-f7cd-c2251529daba', '95ddf089-d44d-6e27-83df-97206e1eb7d1', 
           '5f22578e-c3e3-4e0b-5ddd-ab1dfaacb2d1', '38c56b61-597e-c1dc-5c12-00853bd869e8', 
           'c58e5c0b-dfdf-120b-8433-c33424d4881d', '805736c5-e5f0-48ad-817e-4134eee54e28',
           'da0ebb0b-2a49-9374-6fe3-262748459666', 'c9df083e-70c1-e7c9-df4a-fceaea9aef66', 
           '7d2cfb51-c440-2334-8abe-c57e01f9f71e', '86698c4f-d485-af93-afd9-46e42dbad961', 
           '73c003c3-30a4-1c1b-4ace-2c7ad58b32bc', 'c5d6af4f-4a9d-0f00-2e84-ca5d866b3495', 
           '67583fea-8413-5fb2-1f68-9261da0b30eb', 'a4dad20b-328e-270f-adb5-f469c492380a', 
           'c56559d4-156f-42fa-5cbf-399b81228859', '57f8e64c-76e2-093c-f56d-be6cce5478c8',
           '4724e53a-0d4b-200f-f6e2-601dce51d764', '53e08935-57ee-044b-d4a2-7d068340722b', 
           '06ba0d97-defb-1e89-db6a-497d63369b0d', 'e9a219db-5b35-a0f3-1bcd-0e81d38c3b43', 
           '3bee2ee4-930e-8a53-f4e0-3f96428d506a', '452ab224-9c9f-0a2b-f8db-e8faa1951002', 
           '49851880-f3f9-9641-4669-1b5c20a27988', '20c60a53-0e41-cdfa-83cd-cdd06648b48e', 
           '7e5c46df-667b-fe2e-8181-b3ebcfaa24c2', '8369de61-261b-7bf5-4001-de2bdd920d04']

top_clients = ['d81cbd22-9fed-19ae-db52-9c22474a1b21', 
               'e9a219db-5b35-a0f3-1bcd-0e81d38c3b43',
               'd81cbd22-9fed-19ae-db52-9c22474a1b21',
                '57f8e64c-76e2-093c-f56d-be6cce5478c8',
                'bf6ae8ae-a30a-c643-4d1e-5e23b1e11ece',
                '3f507493-7e23-03ed-403c-6e098517d38a',
               'c9df083e-70c1-e7c9-df4a-fceaea9aef66',
              'b1b26660-20b9-c0ba-56d6-d05b798b882d']
fig = go.Figure()
print('Data for: College Park Church, North Indy Campus')
print('org_id: 8c02eaa3-4275-4a6e-b2a8-f6673688e5ff')
print('site_id: 0a878d43-e796-4120-8cd8-b7359600af16')
print('ap:  5c5b351e81f6')
print('date: 04.15.2022')
print('top 8 clients with multiple REASSOCIATION events')
for c in top_clients:
    dd = test.sort_values('timestamp')
    dd  = dd[dd['client_wcid']==c]
    fig.add_trace(go.Scatter(x=dd['timestamp'],
                             y=dd['client_tx_pkts_sent'],
                             mode='lines+markers', 
                             name=c))
fig.update_layout(
title="Client data tx_pkts_sent",
xaxis_title="Time",
yaxis_title="Client tx_pkts_sent")

fig.show()

In [ ]:
%%local
import plotly.graph_objects as go

cl_list = ['2e576d16-5ade-3a39-6f33-ef758fdbb82d', 'e37a36db-1b54-8f43-e994-0ae52da30436', 
           'f528d96b-3a3a-ef89-6351-fa064d908c3c', '8e86a1ff-3b5f-4e51-484e-1e06931abf87', 
           '31be9684-01d4-16f4-bdb3-18743b2f4916', 'b1b26660-20b9-c0ba-56d6-d05b798b882d', 
           'd11de9b4-fa63-bf7d-3347-6850989d5fac', '49d23273-52ce-2b52-6319-cf9e8234fdab', 
           'ea56925e-2d2c-30b2-cfba-cd8ac19297bc', 'e3c23d1e-8e5e-0357-3f32-ad8fb4457a73', 
           'bf6ae8ae-a30a-c643-4d1e-5e23b1e11ece', '27d08e60-88d6-6584-e367-36393213dce5', 
           'd81cbd22-9fed-19ae-db52-9c22474a1b21', 'bb430a7d-8898-fbeb-fd25-98e47dcb314e', 
           '3f507493-7e23-03ed-403c-6e098517d38a', '08840bc8-7262-dec3-e425-b422eb1eec2b', 
           '1cc4b873-3a6b-44ef-bf47-2c9efb87b8a5', '3acadb0f-8a86-13fd-60f4-6a9861e67ffd', 
           'a64b8657-5979-c4e5-2c38-3cee2323a07a', 
           'cc041fa9-d37d-e3ff-0379-a25eb25f9045', 'd01111fe-b886-4768-b53e-013f775c0c45',
           '84697b49-f958-a6a5-f7cd-c2251529daba', '95ddf089-d44d-6e27-83df-97206e1eb7d1', 
           '5f22578e-c3e3-4e0b-5ddd-ab1dfaacb2d1', '38c56b61-597e-c1dc-5c12-00853bd869e8', 
           'c58e5c0b-dfdf-120b-8433-c33424d4881d', '805736c5-e5f0-48ad-817e-4134eee54e28',
           'da0ebb0b-2a49-9374-6fe3-262748459666', 'c9df083e-70c1-e7c9-df4a-fceaea9aef66', 
           '7d2cfb51-c440-2334-8abe-c57e01f9f71e', '86698c4f-d485-af93-afd9-46e42dbad961', 
           '73c003c3-30a4-1c1b-4ace-2c7ad58b32bc', 'c5d6af4f-4a9d-0f00-2e84-ca5d866b3495', 
           '67583fea-8413-5fb2-1f68-9261da0b30eb', 'a4dad20b-328e-270f-adb5-f469c492380a', 
           'c56559d4-156f-42fa-5cbf-399b81228859', '57f8e64c-76e2-093c-f56d-be6cce5478c8',
           '4724e53a-0d4b-200f-f6e2-601dce51d764', '53e08935-57ee-044b-d4a2-7d068340722b', 
           '06ba0d97-defb-1e89-db6a-497d63369b0d', 'e9a219db-5b35-a0f3-1bcd-0e81d38c3b43', 
           '3bee2ee4-930e-8a53-f4e0-3f96428d506a', '452ab224-9c9f-0a2b-f8db-e8faa1951002', 
           '49851880-f3f9-9641-4669-1b5c20a27988', '20c60a53-0e41-cdfa-83cd-cdd06648b48e', 
           '7e5c46df-667b-fe2e-8181-b3ebcfaa24c2', '8369de61-261b-7bf5-4001-de2bdd920d04']

top_clients = ['d81cbd22-9fed-19ae-db52-9c22474a1b21', 
               'e9a219db-5b35-a0f3-1bcd-0e81d38c3b43',
               'd81cbd22-9fed-19ae-db52-9c22474a1b21',
                '57f8e64c-76e2-093c-f56d-be6cce5478c8',
                'bf6ae8ae-a30a-c643-4d1e-5e23b1e11ece',
                '3f507493-7e23-03ed-403c-6e098517d38a',
               'c9df083e-70c1-e7c9-df4a-fceaea9aef66',
              'b1b26660-20b9-c0ba-56d6-d05b798b882d']

fig = go.Figure()
print('Data for: College Park Church, North Indy Campus')
print('org_id: 8c02eaa3-4275-4a6e-b2a8-f6673688e5ff')
print('site_id: 0a878d43-e796-4120-8cd8-b7359600af16')
print('ap:  5c5b351e81f6')
print('date: 04.15.2022')
print('top 8 clients with multiple REASSOCIATION events')
for c in top_clients:
    dd = test.sort_values('timestamp')
    dd  = dd[dd['client_wcid']==c]
    fig.add_trace(go.Scatter(x=dd['timestamp'],
                             y=dd['client_tx_pkts_sent'],
                             mode='lines+markers', 
                             name=c))
fig.update_layout(
title="Client data tx_pkts_sent",
xaxis_title="Time",
yaxis_title="Client tx_pkts_sent")
fig.show()

fig = go.Figure()
for c in top_clients:
    dd = test.sort_values('timestamp')
    dd  = dd[dd['client_wcid']==c]
    fig.add_trace(go.Scatter(x=dd['timestamp'],
                             y=dd['client_rx_pkts'],
                             mode='lines+markers', 
                             name=c))
fig.update_layout(
title="Client data rx_pkts",
xaxis_title="Time",
yaxis_title="Client rx_pkts")

fig.show()

fig = go.Figure()
for c in top_clients:
    dd = df_ca.sort_values('When')
    dd  = dd[dd['wcid']==c]
    fig.add_trace(go.Scatter(x=dd['When'],
                             y=dd['ev_type'],
                             mode='lines+markers', 
                             name=c))

fig.update_layout(
title="Client Events data",
xaxis_title="Time",
yaxis_title="Events type")

fig.show()

In [ ]:
%%local
import plotly.graph_objects as go

top_clients = ['d81cbd22-9fed-19ae-db52-9c22474a1b21', 
               'e9a219db-5b35-a0f3-1bcd-0e81d38c3b43',
               'd81cbd22-9fed-19ae-db52-9c22474a1b21',
                '57f8e64c-76e2-093c-f56d-be6cce5478c8',
                'bf6ae8ae-a30a-c643-4d1e-5e23b1e11ece',
                '3f507493-7e23-03ed-403c-6e098517d38a',
               'c9df083e-70c1-e7c9-df4a-fceaea9aef66',
              'b1b26660-20b9-c0ba-56d6-d05b798b882d']
fig = go.Figure()
print('Data for: College Park Church, North Indy Campus')
print('org_id: 8c02eaa3-4275-4a6e-b2a8-f6673688e5ff')
print('site_id: 0a878d43-e796-4120-8cd8-b7359600af16')
print('ap:  5c5b351e81f6')
print('date: 04.15.2022')
print('top 8 clients with multiple REASSOCIATION events')
for c in top_clients:
    dd = df_ca.sort_values('When')
    dd  = dd[dd['wcid']==c]
    fig.add_trace(go.Scatter(x=dd['When'],
                             y=dd['ev_type'],
                             mode='lines+markers', 
                             name=c))

fig.update_layout(
title="Client Events data",
xaxis_title="Time",
yaxis_title="Events type")

fig.show()

### PLOTS SAMPLES 

In [ ]:
%%local
import plotly.graph_objects as go

clients_in = clients_in_RTG
p = 0
client_in = clients_in[p]
print('client: '+ client_in)


site_id = list(df_a[df_a['client_wcid']==client_in]['site_id'][0:1])[0]
print('site id  = ' + site_id)
print([x[2:4] for x in hsc_sites_in if x[1]==site_id])

dd = df_a[df_a['client_wcid']==client_in].sort_values(by='time')
dd = dd.reindex()
dd['ap_band_info'] = dd['ap_id'].astype(str) +'; band :'+  dd['client_band'].astype(str)
dd_sticky = dd[(dd['client_wcid']==client_in) & (dd['persist_sticky_count_tot']>0)]
ddr_in = dd[dd['metric']=='roaming']

sticky_sessions = list(set(dd_sticky['sticky_session']))
print(sticky_sessions)

class_data = {  'CLIENT_AUTH_REASSOCIATION': 6,
                'CLIENT_AUTH_REASSOCIATION_11R':5,
                'CLIENT_DEAUTHENTICATED ': 4 ,
                'CLIENT_AUTH_ASSOCIATION': 3,
                'CLIENT_DEAUTHENTICATION':2,
                'CLIENT_DEASSOCIATION':1}

#"data_fields5":["client_connected_time_sec"]

fig = go.Figure()
for data in data_fields: 
    fig = go.Figure()
    for data_in in data_fields[data]:
        fig.add_trace(go.Scatter(x=dd['timestamp'],
                                 y=dd[data_in],
                                 mode='lines+markers',
                                 name=data_in))
        fig.update_layout(title=str(data_fields[data]))
    fig.show()
    
print('site id  = ' + site_id)
print([x[2:4] for x in hsc_sites_in if x[1]==site_id])

fig = go.Figure()
fig.add_trace(go.Scatter(x=dd['timestamp'],
                         y=dd['client_rssi'],
                         text= dd['client_band'], 
                         mode='lines', name= 'time series data'))

for s in sticky_sessions:
    dd_in = dd_sticky[dd_sticky['sticky_session']==s]
    # mm = max(list(dd_in['time']))
    # ii = dd_sticky.loc[dd_sticky['time'] == mm].index[0]
    fig.add_trace(go.Scatter(x=dd_in['timestamp'],
                             y=dd_in['client_rssi'], 
                             mode='lines+markers',
                             name='persistent sticky session '+ str(s)))

for signal in class_data:
    ddin = dd[(dd['classifier']==signal)].sort_values(by='timestamp')
    zz = class_data[signal]
    fig.add_trace(go.Scatter(x=ddin['timestamp'],
                             y=ddin['client_rssi'],
                             mode='markers',
                             marker_size=zz,
                             text=ddin['ap_band_info'],
                             name= signal))
    
fig.add_trace(go.Scatter(x=ddr_in['timestamp'],
                         y=ddr_in['client_rssi'],
                         text= ddr_in['ap_band_info'], 
                         mode='markers', name= 'roaming event'))

fig.update_layout(title='Client: ' + client_in)
fig.show()

# DATA SCHEMAS

In [ ]:
root
 |-- id: string (nullable = true)
 |-- site_id: string (nullable = true)
 |-- org_id: string (nullable = true)
 |-- firmware_version: string (nullable = true)
 |-- model: string (nullable = true)
 |-- uptime: integer (nullable = true)
 |-- interval: long (nullable = true)
 |-- config_time: long (nullable = true)
 |-- when: long (nullable = true)
 |-- total_client_count: integer (nullable = true)
 |-- active_client_count: integer (nullable = true)
 |-- terminator_remote_addr: string (nullable = true)
 |-- terminator_timestamp: long (nullable = true)
 |-- dnsServers: array (nullable = true)
 |    |-- element: string (containsNull = true)
 |-- svis: array (nullable = true)
 |    |-- element: struct (containsNull = true)
 |    |    |-- dev: string (nullable = true)
 |    |    |-- vlan: integer (nullable = true)
 |    |    |-- ips: array (nullable = true)
 |    |    |    |-- element: string (containsNull = true)
 |-- inactive_wired_vlans: array (nullable = true)
 |    |-- element: integer (containsNull = true)
 |-- IPv4Routers: array (nullable = true)
 |    |-- element: struct (containsNull = true)
 |    |    |-- dest: string (nullable = true)
 |    |    |-- gateway: string (nullable = true)
 |-- dhcpclients: array (nullable = true)
 |    |-- element: struct (containsNull = true)
 |    |    |-- dev: string (nullable = true)
 |    |    |-- ip: string (nullable = true)
 |    |    |-- gateway: string (nullable = true)
 |-- l2tptunnels: array (nullable = true)
 |    |-- element: struct (containsNull = true)
 |    |    |-- id: string (nullable = true)
 |    |    |-- state: string (nullable = true)
 |    |    |-- router_id: integer (nullable = true)
 |    |    |-- uptime: integer (nullable = true)
 |    |    |-- local_connection_id: integer (nullable = true)
 |    |    |-- remote_connection_id: integer (nullable = true)
 |    |    |-- tx_control_pkts: integer (nullable = true)
 |    |    |-- rx_control_pkts: integer (nullable = true)
 |    |    |-- sessions: array (nullable = true)
 |    |    |    |-- element: struct (containsNull = true)
 |    |    |    |    |-- dev: string (nullable = true)
 |    |    |    |    |-- remote_end_id: string (nullable = true)
 |    |    |    |    |-- state: string (nullable = true)
 |    |    |    |    |-- local_session_id: integer (nullable = true)
 |    |    |    |    |-- remote_session_id: integer (nullable = true)
 |    |    |-- outer_pmtu: integer (nullable = true)
 |    |    |-- last_stop_ccnresult: struct (nullable = true)
 |    |    |    |-- code: integer (nullable = true)
 |    |    |    |-- err_code: integer (nullable = true)
 |    |    |    |-- err_msg: string (nullable = true)
 |    |    |    |-- when: long (nullable = true)
 |    |    |-- last_peer_stop_ccnresult: struct (nullable = true)
 |    |    |    |-- code: integer (nullable = true)
 |    |    |    |-- err_code: integer (nullable = true)
 |    |    |    |-- err_msg: string (nullable = true)
 |    |    |    |-- when: long (nullable = true)
 |    |    |-- peer_mist_id: string (nullable = true)
 |    |    |-- peer_mist_org_id: string (nullable = true)
 |    |    |-- peer_mist_site_id: string (nullable = true)
 |    |    |-- peer_mist_cluster_id: string (nullable = true)
 |    |    |-- peers_config_index: integer (nullable = true)
 |    |    |-- local_addr: string (nullable = true)
 |    |    |-- peer_addr: string (nullable = true)
 |    |    |-- last_error: string (nullable = true)
 |-- lldp_nd: struct (nullable = true)
 |    |-- port_desc: string (nullable = true)
 |    |-- sys_name: string (nullable = true)
 |    |-- sys_desc: string (nullable = true)
 |    |-- mgmt_addr: string (nullable = true)
 |    |-- port_id: string (nullable = true)
 |    |-- model: string (nullable = true)
 |    |-- version: string (nullable = true)
 |    |-- vendor: string (nullable = true)
 |    |-- mfg_name: string (nullable = true)
 |    |-- model_name: string (nullable = true)
 |    |-- chassis_id: string (nullable = true)
 |-- lldp_pwr: struct (nullable = true)
 |    |-- req_cnt: integer (nullable = true)
 |    |-- xtnd_sup: boolean (nullable = true)
 |    |-- pse_avail: integer (nullable = true)
 |    |-- pd_req: integer (nullable = true)
 |    |-- pd_needs: integer (nullable = true)
 |-- radios: array (nullable = true)
 |    |-- element: struct (containsNull = true)
 |    |    |-- dev: string (nullable = true)
 |    |    |-- band: string (nullable = true)
 |    |    |-- channel: integer (nullable = true)
 |    |    |-- secondary_channel: integer (nullable = true)
 |    |    |-- bandwidth: integer (nullable = true)
 |    |    |-- noise_floor: integer (nullable = true)
 |    |    |-- tx_power: integer (nullable = true)
 |    |    |-- max_tx_power: integer (nullable = true)
 |    |    |-- per_antenna_rssi: array (nullable = true)
 |    |    |    |-- element: integer (containsNull = true)
 |    |    |-- utilization_all: double (nullable = true)
 |    |    |-- utilization_tx: double (nullable = true)
 |    |    |-- utilization_rx_in_bss: double (nullable = true)
 |    |    |-- utilization_rx_other_bss: double (nullable = true)
 |    |    |-- utilization_unknown_wifi: double (nullable = true)
 |    |    |-- utilization_non_wifi: double (nullable = true)
 |    |    |-- dfs_radar_detected: boolean (nullable = true)
 |    |    |-- dfs_cac_state: integer (nullable = true)
 |    |    |-- tx_bytes: long (nullable = true)
 |    |    |-- tx_pkts: integer (nullable = true)
 |    |    |-- tx_mgmt: integer (nullable = true)
 |    |    |-- tx_errors: integer (nullable = true)
 |    |    |-- rx_bytes: long (nullable = true)
 |    |    |-- rx_pkts: integer (nullable = true)
 |    |    |-- rx_mgmt: integer (nullable = true)
 |    |    |-- rx_errors: integer (nullable = true)
 |    |    |-- tx_failed_arp: integer (nullable = true)
 |    |    |-- tx_drop_arp: integer (nullable = true)
 |    |    |-- tx_psblk_fifo: integer (nullable = true)
 |    |    |-- tx_toss: integer (nullable = true)
 |    |    |-- tx_toss_arp: integer (nullable = true)
 |    |    |-- tx_toss_bcmc: integer (nullable = true)
 |    |    |-- tx_toss_unicast: integer (nullable = true)
 |    |    |-- tx_bcmc2unicast: integer (nullable = true)
 |    |    |-- tx_bcmc2unicast_client: integer (nullable = true)
 |    |    |-- tx_bcn_intr: integer (nullable = true)
 |    |    |-- tx_phy_err: integer (nullable = true)
 |    |    |-- tx_failed: integer (nullable = true)
 |    |    |-- tx_retries: integer (nullable = true)
 |    |    |-- tx_retried: integer (nullable = true)
 |    |    |-- rx_dups: integer (nullable = true)
 |    |    |-- rx_retried: integer (nullable = true)
 |    |    |-- tx_bcmc2unicast_bytes: long (nullable = true)
 |    |    |-- tx_bcmc2unicast_client_bytes: long (nullable = true)
 |    |    |-- re_init: integer (nullable = true)
 |    |    |-- re_init_throttle: integer (nullable = true)
 |    |    |-- tx_mgmt_dropped: integer (nullable = true)
 |    |    |-- rx_fifo_overflow: integer (nullable = true)
 |    |    |-- rx_hl_fifo_overflow: integer (nullable = true)
 |    |    |-- rx_hwprobe_req: integer (nullable = true)
 |    |    |-- rx_hwprobe_req_qoverflow: integer (nullable = true)
 |    |    |-- tx_hwprobe_resp: integer (nullable = true)
 |    |    |-- tx_hwprobe_resp_failed: integer (nullable = true)
 |    |    |-- tx_hwprobe_resp_drop_timeout: integer (nullable = true)
 |    |    |-- ampdutx_fifo_full: integer (nullable = true)
 |    |    |-- ampdutx_drop: integer (nullable = true)
 |    |    |-- ampdutx_stuck: integer (nullable = true)
 |    |    |-- ampdutx_orphan: integer (nullable = true)
 |    |    |-- ampdutx_stuck_ps: integer (nullable = true)
 |    |    |-- ampdutx_r0hole: integer (nullable = true)
 |    |    |-- ampdutx_rnhole: integer (nullable = true)
 |    |    |-- ampdutx_rlag: integer (nullable = true)
 |    |    |-- ampdutx_tx_add_ba_req: integer (nullable = true)
 |    |    |-- ampdutx_rx_add_ba_resp: integer (nullable = true)
 |    |    |-- ampdutx_lost: integer (nullable = true)
 |    |    |-- ampdutx_tx_bar: integer (nullable = true)
 |    |    |-- ampdutx_rx_ba: integer (nullable = true)
 |    |    |-- ampdutx_no_ba: integer (nullable = true)
 |    |    |-- ampdutx_rx_unexpect: integer (nullable = true)
 |    |    |-- ampdutx_tx_del_ba: integer (nullable = true)
 |    |    |-- ampdutx_rx_del_ba: integer (nullable = true)
 |    |    |-- ampdutx_block_data_fifo: integer (nullable = true)
 |    |    |-- ampdutx_orphan_bad_ini: integer (nullable = true)
 |    |    |-- ampdutx_drop_no_buf: integer (nullable = true)
 |    |    |-- ampdutx_drop_err: integer (nullable = true)
 |    |    |-- ampdutx_orphan_bad_ini_free: integer (nullable = true)
 |    |    |-- ampdurx_holes: integer (nullable = true)
 |    |    |-- ampdurx_stuck: integer (nullable = true)
 |    |    |-- ampdurx_rx_add_ba_req: integer (nullable = true)
 |    |    |-- ampdurx_tx_add_ba_resp: integer (nullable = true)
 |    |    |-- ampdurx_rx_bar: integer (nullable = true)
 |    |    |-- ampdurx_tx_ba: integer (nullable = true)
 |    |    |-- ampdurx_rx_unexpect: integer (nullable = true)
 |    |    |-- ampdurx_tx_del_ba: integer (nullable = true)
 |    |    |-- ampdurx_rx_del_ba: integer (nullable = true)
 |    |    |-- num_clients: integer (nullable = true)
 |    |    |-- radio_missing: boolean (nullable = true)
 |    |    |-- interrupt_stats_tx_bcn_succ: integer (nullable = true)
 |    |    |-- interrupt_stats_dmaint: integer (nullable = true)
 |    |    |-- narstats_queued: integer (nullable = true)
 |    |    |-- narstats_dequeued: integer (nullable = true)
 |    |    |-- narstats_held: integer (nullable = true)
 |    |    |-- narstats_dropped: integer (nullable = true)
 |    |    |-- phy_type: integer (nullable = true)
 |    |    |-- rx_probe_req_bc: integer (nullable = true)
 |    |    |-- rx_probe_req_non_bc: integer (nullable = true)
 |    |    |-- ignore_probe_req_min_rssi: integer (nullable = true)
 |    |    |-- tx_probe_resp_sw: integer (nullable = true)
 |    |    |-- rx_probe_req_rand: integer (nullable = true)
 |    |    |-- pkt_queue_requested: integer (nullable = true)
 |    |    |-- pkt_queue_full_dropped: integer (nullable = true)
 |    |    |-- pkt_queue_dropped: integer (nullable = true)
 |    |    |-- pkt_queue_retried: integer (nullable = true)
 |    |    |-- pkt_pend_bk: integer (nullable = true)
 |    |    |-- pkt_pend_be: integer (nullable = true)
 |    |    |-- pkt_pend_vi: integer (nullable = true)
 |    |    |-- pkt_pend_vo: integer (nullable = true)
 |    |    |-- pkt_pend_bcmc: integer (nullable = true)
 |    |    |-- pkt_pend_atim: integer (nullable = true)
 |    |    |-- pkt_pend_common: integer (nullable = true)
 |    |    |-- pkt_pend_ampdu: integer (nullable = true)
 |    |    |-- pkt_pend_amsdu: integer (nullable = true)
 |    |    |-- pkt_pend_ps: integer (nullable = true)
 |    |    |-- pkt_pend_hw: integer (nullable = true)
 |    |    |-- pkt_pend_all: integer (nullable = true)
 |    |    |-- wlans: array (nullable = true)
 |    |    |    |-- element: string (containsNull = true)
 |    |    |-- scan_channel: boolean (nullable = true)
 |    |    |-- ampdutx_tx_ampdu_succ: integer (nullable = true)
 |    |    |-- ampdurx_rx_mpdu: integer (nullable = true)
 |    |    |-- ampdurx_rx_ampdu: integer (nullable = true)
 |    |    |-- radio_counter_delta: boolean (nullable = true)
 |    |    |-- num_active_clients: integer (nullable = true)
 |    |    |-- active_client_wcid: array (nullable = true)
 |    |    |    |-- element: string (containsNull = true)
 |    |    |-- mac_stats_rxf0ovfl: integer (nullable = true)
 |    |    |-- mac_stats_rxhlovfl: integer (nullable = true)
 |    |    |-- rx_decrypt_failures: integer (nullable = true)
 |    |    |-- mac_stats_tx_all_frm: integer (nullable = true)
 |    |    |-- mac_stats_tx_rts_frm: integer (nullable = true)
 |    |    |-- mac_stats_tx_cts_frm: integer (nullable = true)
 |    |    |-- mac_stats_tx_data_null_frm: integer (nullable = true)
 |    |    |-- mac_stats_tx_bcn_frm: integer (nullable = true)
 |    |    |-- mac_stats_tx_ampdu: integer (nullable = true)
 |    |    |-- mac_stats_tx_mpdu: integer (nullable = true)
 |    |    |-- mac_stats_tx_unfl: integer (nullable = true)
 |    |    |-- mac_stats_tx_bcn_unfl: integer (nullable = true)
 |    |    |-- mac_stats_tx_phy_err: integer (nullable = true)
 |    |    |-- mac_stats_rx_ucast_pky_eng: integer (nullable = true)
 |    |    |-- mac_stats_rx_mcast_pkt_eng: integer (nullable = true)
 |    |    |-- mac_stats_rx_frm_too_long: integer (nullable = true)
 |    |    |-- mac_stats_rx_frm_too_short: integer (nullable = true)
 |    |    |-- mac_stats_rx_ant_err: integer (nullable = true)
 |    |    |-- mac_stats_rx_bad_fas: integer (nullable = true)
 |    |    |-- mac_stats_rx_bad_plcp: integer (nullable = true)
 |    |    |-- mac_stats_rx_glitch: integer (nullable = true)
 |    |    |-- mac_stats_rx_start: integer (nullable = true)
 |    |    |-- mac_stats_rx_ucast_mbss: integer (nullable = true)
 |    |    |-- mac_stats_rx_mgmt_mbss: integer (nullable = true)
 |    |    |-- mac_stats_rx_ctl: integer (nullable = true)
 |    |    |-- mac_stats_rx_rts: integer (nullable = true)
 |    |    |-- mac_stats_rx_cts: integer (nullable = true)
 |    |    |-- mac_stats_rx_ack: integer (nullable = true)
 |    |    |-- mac_stats_rx_ucast_na: integer (nullable = true)
 |    |    |-- mac_stats_rx_mgmt_na: integer (nullable = true)
 |    |    |-- mac_stats_rx_ctl_na: integer (nullable = true)
 |    |    |-- mac_stats_rx_rts_na: integer (nullable = true)
 |    |    |-- mac_stats_rx_cts_na: integer (nullable = true)
 |    |    |-- mac_stats_rx_data_mcast: integer (nullable = true)
 |    |    |-- mac_stats_rx_mgmt_mcast: integer (nullable = true)
 |    |    |-- mac_stats_rx_ctl_mcast: integer (nullable = true)
 |    |    |-- mac_stats_rx_bcn_mbss: integer (nullable = true)
 |    |    |-- mac_stats_rx_ucast_obss: integer (nullable = true)
 |    |    |-- mac_stats_rx_bcn_obss: integer (nullable = true)
 |    |    |-- mac_stats_rx_tsp_timeout: integer (nullable = true)
 |    |    |-- mac_stats_tx_bcn_cancel: integer (nullable = true)
 |    |    |-- mac_stats_rx_no_delimiter: integer (nullable = true)
 |    |    |-- mac_stats_rxf1ovfl: integer (nullable = true)
 |    |    |-- mac_stats_miss_bcn_dbg: integer (nullable = true)
 |    |    |-- mac_stats_pmqovfl: integer (nullable = true)
 |    |    |-- mac_stats_rx_hwprobe_req: integer (nullable = true)
 |    |    |-- mac_stats_rx_hwprobe_req_qoverflow: integer (nullable = true)
 |    |    |-- mac_stats_tx_hwprobe_resp: integer (nullable = true)
 |    |    |-- mac_stats_tx_hwprobe_resp_failed: integer (nullable = true)
 |    |    |-- mac_stats_tx_hwprobe_resp_drop_timeout: integer (nullable = true)
 |    |    |-- mac_stats_tx_rts_fail: integer (nullable = true)
 |    |    |-- mac_stats_tx_ucast: integer (nullable = true)
 |    |    |-- mac_stats_tx_in_rts_txop: integer (nullable = true)
 |    |    |-- mac_stats_rx_block_ack: integer (nullable = true)
 |    |    |-- mac_stats_tx_block_ack: integer (nullable = true)
 |    |    |-- mac_stats_phy_rx_glitch: integer (nullable = true)
 |    |    |-- mac_stats_rx_drop2nd: integer (nullable = true)
 |    |    |-- mac_stats_rx_too_late: integer (nullable = true)
 |    |    |-- mac_stats_phy_bad_plcp: integer (nullable = true)
 |    |    |-- tx_pkts_sent: integer (nullable = true)
 |    |    |-- tx_pkts_sent_mcast: integer (nullable = true)
 |-- wlans: array (nullable = true)
 |    |-- element: struct (containsNull = true)
 |    |    |-- id: string (nullable = true)
 |    |    |-- radio_index: integer (nullable = true)
 |    |    |-- bssid: string (nullable = true)
 |    |    |-- dev: string (nullable = true)
 |    |    |-- ssid: string (nullable = true)
 |    |    |-- num_clients: integer (nullable = true)
 |    |    |-- tx_mcast_pkts: integer (nullable = true)
 |    |    |-- tx_mcast_bytes: long (nullable = true)
 |    |    |-- radius_auth: array (nullable = true)
 |    |    |    |-- element: struct (containsNull = true)
 |    |    |    |    |-- ip: string (nullable = true)
 |    |    |    |    |-- port: integer (nullable = true)
 |    |    |    |    |-- requests: integer (nullable = true)
 |    |    |    |    |-- retransmissions: integer (nullable = true)
 |    |    |    |    |-- access_accepts: integer (nullable = true)
 |    |    |    |    |-- access_rejects: integer (nullable = true)
 |    |    |    |    |-- access_challenges: integer (nullable = true)
 |    |    |    |    |-- responses: integer (nullable = true)
 |    |    |    |    |-- malformed_responses: integer (nullable = true)
 |    |    |    |    |-- bad_authenticators: integer (nullable = true)
 |    |    |    |    |-- timeouts: integer (nullable = true)
 |    |    |    |    |-- unknown_types: integer (nullable = true)
 |    |    |    |    |-- packets_dropped: integer (nullable = true)
 |    |    |    |    |-- round_trip_time_ms: integer (nullable = true)
 |    |    |-- radius_acct: array (nullable = true)
 |    |    |    |-- element: struct (containsNull = true)
 |    |    |    |    |-- ip: string (nullable = true)
 |    |    |    |    |-- port: integer (nullable = true)
 |    |    |    |    |-- requests: integer (nullable = true)
 |    |    |    |    |-- retransmissions: integer (nullable = true)
 |    |    |    |    |-- responses: integer (nullable = true)
 |    |    |    |    |-- malformed_responses: integer (nullable = true)
 |    |    |    |    |-- timeouts: integer (nullable = true)
 |    |    |    |    |-- unknown_types: integer (nullable = true)
 |    |    |    |    |-- packets_dropped: integer (nullable = true)
 |    |    |    |    |-- round_trip_time_ms: integer (nullable = true)
 |    |    |-- radio: string (nullable = true)
 |-- pwr_src: string (nullable = true)
 |-- pwr_budget: integer (nullable = true)
 |-- pwr_needed: integer (nullable = true)
 |-- pwr_available: integer (nullable = true)
 |-- memory_total_kb: long (nullable = true)
 |-- memory_used_kb: long (nullable = true)
 |-- cpu_total_time: long (nullable = true)
 |-- cpu_user: long (nullable = true)
 |-- cpu_system: long (nullable = true)
 |-- fs_available_kb: long (nullable = true)
 |-- fs_total_kb: long (nullable = true)
 |-- load_total: integer (nullable = true)
 |-- slab_active_objs: integer (nullable = true)
 |-- slab_num_objs: integer (nullable = true)
 |-- slab_obj_size: integer (nullable = true)
 |-- cloud_last_rtt: float (nullable = true)
 |-- cloud_pmtu: integer (nullable = true)
 |-- temperature_attitude: float (nullable = true)
 |-- temperature_cpu: float (nullable = true)
 |-- temperature_ambient: float (nullable = true)
 |-- orientation_accel_x: float (nullable = true)
 |-- orientation_accel_y: float (nullable = true)
 |-- orientation_accel_z: float (nullable = true)
 |-- orientation_magne_x: float (nullable = true)
 |-- orientation_magne_y: float (nullable = true)
 |-- orientation_magne_z: float (nullable = true)
 |-- switchports: array (nullable = true)
 |    |-- element: struct (containsNull = true)
 |    |    |-- name: string (nullable = true)
 |    |    |-- link: boolean (nullable = true)
 |    |    |-- full_duplex: boolean (nullable = true)
 |    |    |-- mbps: integer (nullable = true)
 |    |    |-- rx_bytes: long (nullable = true)
 |    |    |-- rx_pkts: integer (nullable = true)
 |    |    |-- tx_bytes: long (nullable = true)
 |    |    |-- tx_pkts: integer (nullable = true)
 |    |    |-- rx_errors: integer (nullable = true)
 |    |    |-- rx_pause_pkts: integer (nullable = true)
 |    |    |-- rx_undersize_errors: integer (nullable = true)
 |    |    |-- rx_oversize_errors: integer (nullable = true)
 |    |    |-- rx_jabber_errors: integer (nullable = true)
 |    |    |-- rx_alignment_errors: integer (nullable = true)
 |    |    |-- rx_fcs_errors: integer (nullable = true)
 |    |    |-- rx_fragment_errors: integer (nullable = true)
 |    |    |-- rx_symbol_errors: integer (nullable = true)
 |    |    |-- rx_overrun_errors: integer (nullable = true)
 |    |    |-- rx_discards: integer (nullable = true)
 |    |    |-- rx_peakbps: long (nullable = true)
 |    |    |-- tx_peakbps: long (nullable = true)
 |    |    |-- switchport_counter_delta: boolean (nullable = true)
 |-- delta: boolean (nullable = true)
 |-- deltaErrorMsg: string (nullable = true)
 |-- ap_id: string (nullable = true)
 |-- delta_interval: integer (nullable = true)
 |-- ap_counter_delta: boolean (nullable = true)
 |-- input_cloud_partition: integer (nullable = true)
 |-- mesh: struct (nullable = true)
 |    |-- bssid: string (nullable = true)
 |    |-- mac: string (nullable = true)
 |    |-- dev: string (nullable = true)
 |    |-- last_connect_time: long (nullable = true)
 |-- ip: string (nullable = true)
 |-- hostname: string (nullable = true)
 |-- map_id: string (nullable = true)
 |-- terminator: string (nullable = true)
 |-- timestamp: timestamp (nullable = true)

In [ ]:
root
 |-- ap_id: string (nullable = true)
 |-- site_id: string (nullable = true)
 |-- org_id: string (nullable = true)
 |-- firmware_version: string (nullable = true)
 |-- model: string (nullable = true)
 |-- uptime: integer (nullable = true)
 |-- interval: long (nullable = true)
 |-- when: long (nullable = true)
 |-- radios: array (nullable = true)
 |    |-- element: struct (containsNull = true)
 |    |    |-- dev: string (nullable = true)
 |    |    |-- band: integer (nullable = true)
 |    |    |-- channel: integer (nullable = true)
 |    |    |-- secondary_channel: integer (nullable = true)
 |    |    |-- bandwidth: integer (nullable = true)
 |    |    |-- noise_floor: integer (nullable = true)
 |    |    |-- tx_power: integer (nullable = true)
 |    |    |-- max_tx_power: integer (nullable = true)
 |    |    |-- utilization: struct (nullable = true)
 |    |    |    |-- all: double (nullable = true)
 |    |    |    |-- tx: double (nullable = true)
 |    |    |    |-- rx_in_bss: double (nullable = true)
 |    |    |    |-- rx_other_bss: double (nullable = true)
 |    |    |    |-- unknown_wifi: double (nullable = true)
 |    |    |    |-- non_wifi: double (nullable = true)
 |    |    |-- per_antenna_rssi: array (nullable = true)
 |    |    |    |-- element: integer (containsNull = true)
 |    |    |-- dfs: struct (nullable = true)
 |    |    |    |-- radar_detected: boolean (nullable = true)
 |    |    |    |-- cac_state: integer (nullable = true)
 |    |    |-- counter: struct (nullable = true)
 |    |    |    |-- tx_bytes: long (nullable = true)
 |    |    |    |-- tx_pkts: integer (nullable = true)
 |    |    |    |-- tx_mgmt: integer (nullable = true)
 |    |    |    |-- tx_errors: integer (nullable = true)
 |    |    |    |-- rx_bytes: long (nullable = true)
 |    |    |    |-- rx_pkts: integer (nullable = true)
 |    |    |    |-- rx_mgmt: integer (nullable = true)
 |    |    |    |-- rx_errors: integer (nullable = true)
 |    |    |-- num_clients: integer (nullable = true)
 |    |    |-- radio_missing: boolean (nullable = true)
 |-- wlans: array (nullable = true)
 |    |-- element: struct (containsNull = true)
 |    |    |-- id: string (nullable = true)
 |    |    |-- radio_index: integer (nullable = true)
 |    |    |-- bssid: binary (nullable = true)
 |    |    |-- dev: string (nullable = true)
 |    |    |-- ssid: string (nullable = true)
 |    |    |-- for_mesh: boolean (nullable = true)
 |    |    |-- num_clients: integer (nullable = true)
 |    |    |-- tx_mcast_pkts: integer (nullable = true)
 |    |    |-- tx_mcast_bytes: long (nullable = true)
 |-- app_ss: array (nullable = true)
 |    |-- element: struct (containsNull = true)
 |    |    |-- hostname: string (nullable = true)
 |    |    |-- protocol: integer (nullable = true)
 |    |    |-- src_port: integer (nullable = true)
 |    |    |-- dst_port: integer (nullable = true)
 |    |    |-- upload_byte: integer (nullable = true)
 |    |    |-- download_byte: integer (nullable = true)
 |    |    |-- app: string (nullable = true)
 |    |    |-- dst_ip: string (nullable = true)
 |    |    |-- ssid: string (nullable = true)
 |    |    |-- wlan_id: string (nullable = true)
 |-- terminator_remote_addr: string (nullable = true)
 |-- terminator_timestamp: long (nullable = true)
 |-- client_mac: string (nullable = true)
 |-- client_wcid: string (nullable = true)
 |-- client_radio_index: integer (nullable = true)
 |-- client_band: string (nullable = true)
 |-- client_bssid: string (nullable = true)
 |-- client_wlan_id: string (nullable = true)
 |-- client_wlan_ssid: string (nullable = true)
 |-- client_connected_time_sec: integer (nullable = true)
 |-- client_inactive_time_milli_sec: integer (nullable = true)
 |-- client_rssi: integer (nullable = true)
 |-- client_per_antenna_rssi: array (nullable = true)
 |    |-- element: integer (containsNull = true)
 |-- client_avg_rssi: integer (nullable = true)
 |-- client_tx_bit_rate: integer (nullable = true)
 |-- client_tx_unicast_bytes: long (nullable = true)
 |-- client_tx_unicast_pkts: integer (nullable = true)
 |-- client_tx_pkts_sent: integer (nullable = true)
 |-- client_tx_retries: integer (nullable = true)
 |-- client_tx_retried: integer (nullable = true)
 |-- client_tx_failed: integer (nullable = true)
 |-- client_txbps: integer (nullable = true)
 |-- client_txpps: integer (nullable = true)
 |-- client_tx_retry_exhausted: integer (nullable = true)
 |-- client_tx_rate_fall_back: integer (nullable = true)
 |-- client_rx_bit_rate: integer (nullable = true)
 |-- client_rx_bytes: long (nullable = true)
 |-- client_rx_pkts: integer (nullable = true)
 |-- client_rx_mcast_pkts: integer (nullable = true)
 |-- client_rx_mcast_bytes: long (nullable = true)
 |-- client_rx_retried: integer (nullable = true)
 |-- client_rx_retries: integer (nullable = true)
 |-- client_rx_dups: integer (nullable = true)
 |-- client_rx_decrypt_failures: integer (nullable = true)
 |-- client_rxbps: integer (nullable = true)
 |-- client_rxpps: integer (nullable = true)
 |-- client_rx_probe_reqs24: integer (nullable = true)
 |-- client_rx_probe_reqs5: integer (nullable = true)
 |-- client_pq_requested: integer (nullable = true)
 |-- client_pq_dropped: integer (nullable = true)
 |-- client_pq_retried: integer (nullable = true)
 |-- client_pq_rtsfail: integer (nullable = true)
 |-- client_pq_throughput: integer (nullable = true)
 |-- client_pq_airuse: integer (nullable = true)
 |-- client_pqmax_used: integer (nullable = true)
 |-- client_pq_length: integer (nullable = true)
 |-- client_tx_delay: array (nullable = true)
 |    |-- element: struct (containsNull = true)
 |    |    |-- hist: array (nullable = true)
 |    |    |    |-- element: integer (containsNull = true)
 |    |    |-- retry_hist: array (nullable = true)
 |    |    |    |-- element: integer (containsNull = true)
 |    |    |-- retry_sum: array (nullable = true)
 |    |    |    |-- element: integer (containsNull = true)
 |    |    |-- no_ack: integer (nullable = true)
 |    |    |-- min: integer (nullable = true)
 |    |    |-- max: integer (nullable = true)
 |-- client_ipv4: string (nullable = true)
 |-- client_vlan_id: integer (nullable = true)
 |-- client_username: string (nullable = true)
 |-- client_cckrates: struct (nullable = true)
 |    |-- rx1_mbps: integer (nullable = true)
 |    |-- tx1_mbps: integer (nullable = true)
 |    |-- tx1_mbps_succ: integer (nullable = true)
 |    |-- rx2_mbps: integer (nullable = true)
 |    |-- tx2_mbps: integer (nullable = true)
 |    |-- tx2_mbps_succ: integer (nullable = true)
 |    |-- rx5_mbps: integer (nullable = true)
 |    |-- tx5_mbps: integer (nullable = true)
 |    |-- tx5_mbps_succ: integer (nullable = true)
 |    |-- rx11_mbps: integer (nullable = true)
 |    |-- tx11_mbps: integer (nullable = true)
 |    |-- tx11_mbps_succ: integer (nullable = true)
 |-- client_ofdmrates: struct (nullable = true)
 |    |-- rx6_mbps: integer (nullable = true)
 |    |-- tx6_mbps: integer (nullable = true)
 |    |-- tx6_mbps_succ: integer (nullable = true)
 |    |-- rx9_mbps: integer (nullable = true)
 |    |-- tx9_mbps: integer (nullable = true)
 |    |-- tx9_mbps_succ: integer (nullable = true)
 |    |-- rx12_mbps: integer (nullable = true)
 |    |-- tx12_mbps: integer (nullable = true)
 |    |-- tx12_mbps_succ: integer (nullable = true)
 |    |-- rx18_mbps: integer (nullable = true)
 |    |-- tx18_mbps: integer (nullable = true)
 |    |-- tx18_mbps_succ: integer (nullable = true)
 |    |-- rx24_mbps: integer (nullable = true)
 |    |-- tx24_mbps: integer (nullable = true)
 |    |-- tx24_mbps_succ: integer (nullable = true)
 |    |-- rx36_mbps: integer (nullable = true)
 |    |-- tx36_mbps: integer (nullable = true)
 |    |-- tx36_mbps_succ: integer (nullable = true)
 |    |-- rx48_mbps: integer (nullable = true)
 |    |-- tx48_mbps: integer (nullable = true)
 |    |-- tx48_mbps_succ: integer (nullable = true)
 |    |-- rx54_mbps: integer (nullable = true)
 |    |-- tx54_mbps: integer (nullable = true)
 |    |-- tx54_mbps_succ: integer (nullable = true)
 |-- client_mcsrates: struct (nullable = true)
 |    |-- mcstype: string (nullable = true)
 |    |-- rx: struct (nullable = true)
 |    |    |-- chain1: array (nullable = true)
 |    |    |    |-- element: integer (containsNull = true)
 |    |    |-- chain2: array (nullable = true)
 |    |    |    |-- element: integer (containsNull = true)
 |    |    |-- chain3: array (nullable = true)
 |    |    |    |-- element: integer (containsNull = true)
 |    |    |-- chain4: array (nullable = true)
 |    |    |    |-- element: integer (containsNull = true)
 |    |-- tx: struct (nullable = true)
 |    |    |-- chain1: array (nullable = true)
 |    |    |    |-- element: integer (containsNull = true)
 |    |    |-- chain2: array (nullable = true)
 |    |    |    |-- element: integer (containsNull = true)
 |    |    |-- chain3: array (nullable = true)
 |    |    |    |-- element: integer (containsNull = true)
 |    |    |-- chain4: array (nullable = true)
 |    |    |    |-- element: integer (containsNull = true)
 |    |-- tx_succ: struct (nullable = true)
 |    |    |-- chain1: array (nullable = true)
 |    |    |    |-- element: integer (containsNull = true)
 |    |    |-- chain2: array (nullable = true)
 |    |    |    |-- element: integer (containsNull = true)
 |    |    |-- chain3: array (nullable = true)
 |    |    |    |-- element: integer (containsNull = true)
 |    |    |-- chain4: array (nullable = true)
 |    |    |    |-- element: integer (containsNull = true)
 |    |-- rx_ampdu: struct (nullable = true)
 |    |    |-- chain1: array (nullable = true)
 |    |    |    |-- element: integer (containsNull = true)
 |    |    |-- chain2: array (nullable = true)
 |    |    |    |-- element: integer (containsNull = true)
 |    |    |-- chain3: array (nullable = true)
 |    |    |    |-- element: integer (containsNull = true)
 |    |    |-- chain4: array (nullable = true)
 |    |    |    |-- element: integer (containsNull = true)
 |    |-- tx_ampdu: struct (nullable = true)
 |    |    |-- chain1: array (nullable = true)
 |    |    |    |-- element: integer (containsNull = true)
 |    |    |-- chain2: array (nullable = true)
 |    |    |    |-- element: integer (containsNull = true)
 |    |    |-- chain3: array (nullable = true)
 |    |    |    |-- element: integer (containsNull = true)
 |    |    |-- chain4: array (nullable = true)
 |    |    |    |-- element: integer (containsNull = true)
 |    |-- tx_ampdusucc: struct (nullable = true)
 |    |    |-- chain1: array (nullable = true)
 |    |    |    |-- element: integer (containsNull = true)
 |    |    |-- chain2: array (nullable = true)
 |    |    |    |-- element: integer (containsNull = true)
 |    |    |-- chain3: array (nullable = true)
 |    |    |    |-- element: integer (containsNull = true)
 |    |    |-- chain4: array (nullable = true)
 |    |    |    |-- element: integer (containsNull = true)
 |-- client_protocol: string (nullable = true)
 |-- client_num_streams: integer (nullable = true)
 |-- client_multi_pskname: string (nullable = true)
 |-- cloud_last_rtt: float (nullable = true)
 |-- cloud_when_last_rtt: long (nullable = true)
 |-- client_count: integer (nullable = true)
 |-- delta: boolean (nullable = true)
 |-- deltaErrorMsg: string (nullable = true)
 |-- delta_interval: integer (nullable = true)
 |-- isActive: boolean (nullable = true)
 |-- hostname: string (nullable = true)
 |-- user_agent: string (nullable = true)
 |-- client_mfg: string (nullable = true)
 |-- client_device: string (nullable = true)
 |-- client_os: string (nullable = true)
 |-- client_model: string (nullable = true)
 |-- client_multi_pskid: string (nullable = true)
 |-- ap_time: long (nullable = true)
 |-- timestamp: timestamp (nullable = true)


## Initial investigation 

In [ ]:
# https://manage.mist.com/admin/?org_id=8c02eaa3-4275-4a6e-b2a8-f6673688e5ff#!ap/0a878d43-e796-4120-8cd8-b7359600af16

In [ ]:
date = '2022-04-15'
hour = '15'
df = get_ap_stats(date, hour, env)
df_c = get_es_client_data(date, hour, env)
df.printSchema()

In [ ]:
df_c.printSchema()

In [ ]:
df_c.select(['ap', 'apfw'] ).show(10, truncate=False)

In [ ]:
df.where(F.col('ap_id')=="5c-5b-35-1e-81-f6").show(10, truncate=False)

In [ ]:
ap_models = ['AP21-US', 'AP21-WW']

In [ ]:
AUTH_SUCC_LIST = ['CLIENT_AUTH_ASSOCIATION',
                  'CLIENT_AUTHENTICATED',
                  'CLIENT_AUTH_REASSOCIATION']
ASSO_SUCC_LIST = ['CLIENT_ASSOCIATION',
                  'CLIENT_REASSOCIATION']
NEUTRAL_LIST = ['CLIENT_DEAUTHENTICATION',
                'CLIENT_DEASSOCIATION',
                'CLIENT_DEAUTHENTICATED',
                'STA_DOS_DISASSOC',
                'CLIENT_AUTH_ASSOCIATION_OKC',
                'CLIENT_AUTHENTICATED_11R',
                'CLIENT_AUTH_REASSOCIATION_OKC',
                'CLIENT_AUTH_REASSOCIATION_11R']
events_out = AUTH_SUCC_LIST + ASSO_SUCC_LIST + NEUTRAL_LIST
#    ['MARVIS_EVENT_CLIENT_STATIC_DNS_BLOCKED',
#     'MARVIS_EVENT_CLIENT_STATIC_IP_BLOCKED']

In [ ]:
df_c = df_c.where(F.col('ev_type').isin(events_out))
df_c.show(10, truncate=False)

In [ ]:
df_ap21 = df.where(F.col('model').isin(ap_models)).select(['site_id', 'org_id', 'ap_id', 'model']).dropDuplicates()

In [ ]:
df_data = df.where(F.col('model').isin(ap_models))

In [ ]:
df_data = df_data.withColumn('ap',  F.regexp_replace('ap_id', '-', ''))

In [ ]:
ap21_list = df_data.select('ap').collect()
ap21_list = list(set([ap.ap for ap in ap21_list]))

In [ ]:
ap21_list[:10]

In [ ]:
df_data.select(['site_id', 'org_id', 'ap_id', 'ap', 'model']).show(10)

In [ ]:
events0 = df_data.select(['site_id', 'org_id', 'ap_id', 'ap', 'model']).join(df_c,['site_id', 'org_id', 'ap'])

In [ ]:
events = df_c.join(df_data.select(['site_id', 'org_id', 'ap_id', 'ap', 'model']), ['site_id', 'org_id', 'ap'], 'inner')

In [ ]:
events2 = df_c.where(F.col('ap').isin(ap21_list))

In [ ]:
events2_gg = events2.groupBy(['site_id', 
                              'org_id',
                              'ap', 
                              'ev_type']).agg(F.count('When').alias('num_of_events'),
                                              F.countDistinct('wcid').alias('num_of_clients'))

In [ ]:
%%pretty
df_c.where(F.col('ap')=="5c5b351e81f6").show(20, truncate=False)

In [ ]:
%%pretty
events2_gg.orderBy(F.col('num_of_events').desc()).show(20, truncate=False)

In [ ]:
events.printSchema()

In [ ]:
events.count()

In [ ]:
events_gg = events.groupBy(['site_id', 
                            'org_id',
                            'ap_id',
                            'ap', 
                            'ev_type']).agg(F.count('When').alias('num_of_events'),
                                            F.countDistinct('wcid').alias('num_of_clients'))

In [ ]:
%%pretty
events_gg.orderBy(F.col('num_of_events').desc()).show(20, truncate=False)

In [ ]:
%%pretty
events_gg.where(F.col('ap_id')=="5c-5b-35-1e-81-f6").show(20, truncate=False)

In [ ]:
%%pretty
df_c.where(F.col('ap')=="5c5b351e81f6").show(20, truncate=False)

In [ ]:
%%pretty
df_ap21.show(20, truncate=False)

In [ ]:
df_ap21.dropDuplicates().count()

In [ ]:
%%pretty
df_c.show(10, truncate=False)

In [ ]:
model_list = df.select(F.col('model')).dropDuplicates()

In [ ]:
model_list.orderBy(F.col('model')).show(100, truncate=False)

In [ ]:
# model      : AP21 (sku=AP21-US)

In [ ]:
%%pretty
df.where(F.col('ap_id')=="5c-5b-35-1e-81-f6").show(10, truncate=False)

In [ ]:
"5c-5b-35-1e-81-f6"

In [ ]:
# read data for tests 
fields =  [ "timestamp",
            "when",
            "terminator_timestamp",
            "org_id",            
            "site_id",
            "ap_id",
            "client_radio_index", 
            "client_band", 
            "client_wlan_id",
            "client_wcid",
            "client_device",
            "client_os",
            "client_model",
            "client_connected_time_sec",
            "client_inactive_time_milli_sec",
            "client_rssi",
            "client_tx_bit_rate",
            "client_tx_unicast_bytes",
            "client_tx_retries",
            'client_tx_retried',
            'client_tx_failed',
            'client_txbps',
            "client_rx_bit_rate",
            "client_rx_bytes",
            "client_rx_mcast_bytes",
            "client_rx_retried",
            "client_rx_retries",
            "client_rx_dups",
            "client_rxbps",
            "client_mac", 
            'client_bssid','isActive']

In [ ]:
|-- id: string (nullable = true)
 |-- site_id: string (nullable = true)
 |-- org_id: string (nullable = true)
 |-- firmware_version: string (nullable = true)
 |-- model: string (nullable = true)
 |-- uptime: integer (nullable = true)
 |-- interval: long (nullable = true)
 |-- config_time: long (nullable = true)
 |-- when: long (nullable = true)
 |-- total_client_count: integer (nullable = true)
 |-- active_client_count: integer (nullable = true)
 |-- terminator_remote_addr: string (nullable = true)
 |-- terminator_timestamp: long (nullable = true)
 |-- dnsServers: array (nullable = true)
 |    |-- element: string (containsNull = true)
 |-- svis: array (nullable = true)
 |    |-- element: struct (containsNull = true)
 |    |    |-- dev: string (nullable = true)
 |    |    |-- vlan: integer (nullable = true)
 |    |    |-- ips: array (nullable = true)
 |    |    |    |-- element: string (containsNull = true)
 |-- inactive_wired_vlans: array (nullable = true)
 |    |-- element: integer (containsNull = true)
 |-- IPv4Routers: array (nullable = true)
 |    |-- element: struct (containsNull = true)
 |    |    |-- dest: string (nullable = true)
 |    |    |-- gateway: string (nullable = true)
 |-- dhcpclients: array (nullable = true)
 |    |-- element: struct (containsNull = true)
 |    |    |-- dev: string (nullable = true)
 |    |    |-- ip: string (nullable = true)
 |    |    |-- gateway: string (nullable = true)
 |-- l2tptunnels: array (nullable = true)
 |    |-- element: struct (containsNull = true)
 |    |    |-- id: string (nullable = true)
 |    |    |-- state: string (nullable = true)
 |    |    |-- router_id: integer (nullable = true)
 |    |    |-- uptime: integer (nullable = true)
 |    |    |-- local_connection_id: integer (nullable = true)
 |    |    |-- remote_connection_id: integer (nullable = true)
 |    |    |-- tx_control_pkts: integer (nullable = true)
 |    |    |-- rx_control_pkts: integer (nullable = true)
 |    |    |-- sessions: array (nullable = true)
 |    |    |    |-- element: struct (containsNull = true)
 |    |    |    |    |-- dev: string (nullable = true)
 |    |    |    |    |-- remote_end_id: string (nullable = true)
 |    |    |    |    |-- state: string (nullable = true)
 |    |    |    |    |-- local_session_id: integer (nullable = true)
 |    |    |    |    |-- remote_session_id: integer (nullable = true)
 |    |    |-- outer_pmtu: integer (nullable = true)
 |    |    |-- last_stop_ccnresult: struct (nullable = true)
 |    |    |    |-- code: integer (nullable = true)
 |    |    |    |-- err_code: integer (nullable = true)
 |    |    |    |-- err_msg: string (nullable = true)
 |    |    |    |-- when: long (nullable = true)
 |    |    |-- last_peer_stop_ccnresult: struct (nullable = true)
 |    |    |    |-- code: integer (nullable = true)
 |    |    |    |-- err_code: integer (nullable = true)
 |    |    |    |-- err_msg: string (nullable = true)
 |    |    |    |-- when: long (nullable = true)
 |    |    |-- peer_mist_id: string (nullable = true)
 |    |    |-- peer_mist_org_id: string (nullable = true)
 |    |    |-- peer_mist_site_id: string (nullable = true)
 |    |    |-- peer_mist_cluster_id: string (nullable = true)
 |    |    |-- peers_config_index: integer (nullable = true)
 |    |    |-- local_addr: string (nullable = true)
 |    |    |-- peer_addr: string (nullable = true)
 |    |    |-- last_error: string (nullable = true)
 |-- lldp_nd: struct (nullable = true)
 |    |-- port_desc: string (nullable = true)
 |    |-- sys_name: string (nullable = true)
 |    |-- sys_desc: string (nullable = true)
 |    |-- mgmt_addr: string (nullable = true)
 |    |-- port_id: string (nullable = true)
 |    |-- model: string (nullable = true)
 |    |-- version: string (nullable = true)
 |    |-- vendor: string (nullable = true)
 |    |-- mfg_name: string (nullable = true)
 |    |-- model_name: string (nullable = true)
 |    |-- chassis_id: string (nullable = true)
 |-- lldp_pwr: struct (nullable = true)
 |    |-- req_cnt: integer (nullable = true)
 |    |-- xtnd_sup: boolean (nullable = true)
 |    |-- pse_avail: integer (nullable = true)
 |    |-- pd_req: integer (nullable = true)
 |    |-- pd_needs: integer (nullable = true)
 |-- radios: array (nullable = true)
 |    |-- element: struct (containsNull = true)
 |    |    |-- dev: string (nullable = true)
 |    |    |-- band: string (nullable = true)
 |    |    |-- channel: integer (nullable = true)
 |    |    |-- secondary_channel: integer (nullable = true)
 |    |    |-- bandwidth: integer (nullable = true)
 |    |    |-- noise_floor: integer (nullable = true)
 |    |    |-- tx_power: integer (nullable = true)
 |    |    |-- max_tx_power: integer (nullable = true)
 |    |    |-- per_antenna_rssi: array (nullable = true)
 |    |    |    |-- element: integer (containsNull = true)
 |    |    |-- utilization_all: double (nullable = true)
 |    |    |-- utilization_tx: double (nullable = true)
 |    |    |-- utilization_rx_in_bss: double (nullable = true)
 |    |    |-- utilization_rx_other_bss: double (nullable = true)
 |    |    |-- utilization_unknown_wifi: double (nullable = true)
 |    |    |-- utilization_non_wifi: double (nullable = true)
 |    |    |-- dfs_radar_detected: boolean (nullable = true)
 |    |    |-- dfs_cac_state: integer (nullable = true)
 |    |    |-- tx_bytes: long (nullable = true)
 |    |    |-- tx_pkts: integer (nullable = true)
 |    |    |-- tx_mgmt: integer (nullable = true)
 |    |    |-- tx_errors: integer (nullable = true)
 |    |    |-- rx_bytes: long (nullable = true)
 |    |    |-- rx_pkts: integer (nullable = true)
 |    |    |-- rx_mgmt: integer (nullable = true)
 |    |    |-- rx_errors: integer (nullable = true)
 |    |    |-- tx_failed_arp: integer (nullable = true)
 |    |    |-- tx_drop_arp: integer (nullable = true)
 |    |    |-- tx_psblk_fifo: integer (nullable = true)
 |    |    |-- tx_toss: integer (nullable = true)
 |    |    |-- tx_toss_arp: integer (nullable = true)
 |    |    |-- tx_toss_bcmc: integer (nullable = true)
 |    |    |-- tx_toss_unicast: integer (nullable = true)
 |    |    |-- tx_bcmc2unicast: integer (nullable = true)
 |    |    |-- tx_bcmc2unicast_client: integer (nullable = true)
 |    |    |-- tx_bcn_intr: integer (nullable = true)
 |    |    |-- tx_phy_err: integer (nullable = true)
 |    |    |-- tx_failed: integer (nullable = true)
 |    |    |-- tx_retries: integer (nullable = true)
 |    |    |-- tx_retried: integer (nullable = true)
 |    |    |-- rx_dups: integer (nullable = true)
 |    |    |-- rx_retried: integer (nullable = true)
 |    |    |-- tx_bcmc2unicast_bytes: long (nullable = true)
 |    |    |-- tx_bcmc2unicast_client_bytes: long (nullable = true)
 |    |    |-- re_init: integer (nullable = true)
 |    |    |-- re_init_throttle: integer (nullable = true)
 |    |    |-- tx_mgmt_dropped: integer (nullable = true)
 |    |    |-- rx_fifo_overflow: integer (nullable = true)
 |    |    |-- rx_hl_fifo_overflow: integer (nullable = true)
 |    |    |-- rx_hwprobe_req: integer (nullable = true)
 |    |    |-- rx_hwprobe_req_qoverflow: integer (nullable = true)
 |    |    |-- tx_hwprobe_resp: integer (nullable = true)
 |    |    |-- tx_hwprobe_resp_failed: integer (nullable = true)
 |    |    |-- tx_hwprobe_resp_drop_timeout: integer (nullable = true)
 |    |    |-- ampdutx_fifo_full: integer (nullable = true)
 |    |    |-- ampdutx_drop: integer (nullable = true)
 |    |    |-- ampdutx_stuck: integer (nullable = true)
 |    |    |-- ampdutx_orphan: integer (nullable = true)
 |    |    |-- ampdutx_stuck_ps: integer (nullable = true)
 |    |    |-- ampdutx_r0hole: integer (nullable = true)
 |    |    |-- ampdutx_rnhole: integer (nullable = true)
 |    |    |-- ampdutx_rlag: integer (nullable = true)
 |    |    |-- ampdutx_tx_add_ba_req: integer (nullable = true)
 |    |    |-- ampdutx_rx_add_ba_resp: integer (nullable = true)
 |    |    |-- ampdutx_lost: integer (nullable = true)
 |    |    |-- ampdutx_tx_bar: integer (nullable = true)
 |    |    |-- ampdutx_rx_ba: integer (nullable = true)
 |    |    |-- ampdutx_no_ba: integer (nullable = true)
 |    |    |-- ampdutx_rx_unexpect: integer (nullable = true)
 |    |    |-- ampdutx_tx_del_ba: integer (nullable = true)
 |    |    |-- ampdutx_rx_del_ba: integer (nullable = true)
 |    |    |-- ampdutx_block_data_fifo: integer (nullable = true)
 |    |    |-- ampdutx_orphan_bad_ini: integer (nullable = true)
 |    |    |-- ampdutx_drop_no_buf: integer (nullable = true)
 |    |    |-- ampdutx_drop_err: integer (nullable = true)
 |    |    |-- ampdutx_orphan_bad_ini_free: integer (nullable = true)
 |    |    |-- ampdurx_holes: integer (nullable = true)
 |    |    |-- ampdurx_stuck: integer (nullable = true)
 |    |    |-- ampdurx_rx_add_ba_req: integer (nullable = true)
 |    |    |-- ampdurx_tx_add_ba_resp: integer (nullable = true)
 |    |    |-- ampdurx_rx_bar: integer (nullable = true)
 |    |    |-- ampdurx_tx_ba: integer (nullable = true)
 |    |    |-- ampdurx_rx_unexpect: integer (nullable = true)
 |    |    |-- ampdurx_tx_del_ba: integer (nullable = true)
 |    |    |-- ampdurx_rx_del_ba: integer (nullable = true)
 |    |    |-- num_clients: integer (nullable = true)
 |    |    |-- radio_missing: boolean (nullable = true)
 |    |    |-- interrupt_stats_tx_bcn_succ: integer (nullable = true)
 |    |    |-- interrupt_stats_dmaint: integer (nullable = true)
 |    |    |-- narstats_queued: integer (nullable = true)
 |    |    |-- narstats_dequeued: integer (nullable = true)
 |    |    |-- narstats_held: integer (nullable = true)
 |    |    |-- narstats_dropped: integer (nullable = true)
 |    |    |-- phy_type: integer (nullable = true)
 |    |    |-- rx_probe_req_bc: integer (nullable = true)
 |    |    |-- rx_probe_req_non_bc: integer (nullable = true)
 |    |    |-- ignore_probe_req_min_rssi: integer (nullable = true)
 |    |    |-- tx_probe_resp_sw: integer (nullable = true)
 |    |    |-- rx_probe_req_rand: integer (nullable = true)
 |    |    |-- pkt_queue_requested: integer (nullable = true)
 |    |    |-- pkt_queue_full_dropped: integer (nullable = true)
 |    |    |-- pkt_queue_dropped: integer (nullable = true)
 |    |    |-- pkt_queue_retried: integer (nullable = true)
 |    |    |-- pkt_pend_bk: integer (nullable = true)
 |    |    |-- pkt_pend_be: integer (nullable = true)
 |    |    |-- pkt_pend_vi: integer (nullable = true)
 |    |    |-- pkt_pend_vo: integer (nullable = true)
 |    |    |-- pkt_pend_bcmc: integer (nullable = true)
 |    |    |-- pkt_pend_atim: integer (nullable = true)
 |    |    |-- pkt_pend_common: integer (nullable = true)
 |    |    |-- pkt_pend_ampdu: integer (nullable = true)
 |    |    |-- pkt_pend_amsdu: integer (nullable = true)
 |    |    |-- pkt_pend_ps: integer (nullable = true)
 |    |    |-- pkt_pend_hw: integer (nullable = true)
 |    |    |-- pkt_pend_all: integer (nullable = true)
 |    |    |-- wlans: array (nullable = true)
 |    |    |    |-- element: string (containsNull = true)
 |    |    |-- scan_channel: boolean (nullable = true)
 |    |    |-- ampdutx_tx_ampdu_succ: integer (nullable = true)
 |    |    |-- ampdurx_rx_mpdu: integer (nullable = true)
 |    |    |-- ampdurx_rx_ampdu: integer (nullable = true)
 |    |    |-- radio_counter_delta: boolean (nullable = true)
 |    |    |-- num_active_clients: integer (nullable = true)
 |    |    |-- active_client_wcid: array (nullable = true)
 |    |    |    |-- element: string (containsNull = true)
 |    |    |-- mac_stats_rxf0ovfl: integer (nullable = true)
 |    |    |-- mac_stats_rxhlovfl: integer (nullable = true)
 |    |    |-- rx_decrypt_failures: integer (nullable = true)
 |    |    |-- mac_stats_tx_all_frm: integer (nullable = true)
 |    |    |-- mac_stats_tx_rts_frm: integer (nullable = true)
 |    |    |-- mac_stats_tx_cts_frm: integer (nullable = true)
 |    |    |-- mac_stats_tx_data_null_frm: integer (nullable = true)
 |    |    |-- mac_stats_tx_bcn_frm: integer (nullable = true)
 |    |    |-- mac_stats_tx_ampdu: integer (nullable = true)
 |    |    |-- mac_stats_tx_mpdu: integer (nullable = true)
 |    |    |-- mac_stats_tx_unfl: integer (nullable = true)
 |    |    |-- mac_stats_tx_bcn_unfl: integer (nullable = true)
 |    |    |-- mac_stats_tx_phy_err: integer (nullable = true)
 |    |    |-- mac_stats_rx_ucast_pky_eng: integer (nullable = true)
 |    |    |-- mac_stats_rx_mcast_pkt_eng: integer (nullable = true)
 |    |    |-- mac_stats_rx_frm_too_long: integer (nullable = true)
 |    |    |-- mac_stats_rx_frm_too_short: integer (nullable = true)
 |    |    |-- mac_stats_rx_ant_err: integer (nullable = true)
 |    |    |-- mac_stats_rx_bad_fas: integer (nullable = true)
 |    |    |-- mac_stats_rx_bad_plcp: integer (nullable = true)
 |    |    |-- mac_stats_rx_glitch: integer (nullable = true)
 |    |    |-- mac_stats_rx_start: integer (nullable = true)
 |    |    |-- mac_stats_rx_ucast_mbss: integer (nullable = true)
 |    |    |-- mac_stats_rx_mgmt_mbss: integer (nullable = true)
 |    |    |-- mac_stats_rx_ctl: integer (nullable = true)
 |    |    |-- mac_stats_rx_rts: integer (nullable = true)
 |    |    |-- mac_stats_rx_cts: integer (nullable = true)
 |    |    |-- mac_stats_rx_ack: integer (nullable = true)
 |    |    |-- mac_stats_rx_ucast_na: integer (nullable = true)
 |    |    |-- mac_stats_rx_mgmt_na: integer (nullable = true)
 |    |    |-- mac_stats_rx_ctl_na: integer (nullable = true)
 |    |    |-- mac_stats_rx_rts_na: integer (nullable = true)
 |    |    |-- mac_stats_rx_cts_na: integer (nullable = true)
 |    |    |-- mac_stats_rx_data_mcast: integer (nullable = true)
 |    |    |-- mac_stats_rx_mgmt_mcast: integer (nullable = true)
 |    |    |-- mac_stats_rx_ctl_mcast: integer (nullable = true)
 |    |    |-- mac_stats_rx_bcn_mbss: integer (nullable = true)
 |    |    |-- mac_stats_rx_ucast_obss: integer (nullable = true)
 |    |    |-- mac_stats_rx_bcn_obss: integer (nullable = true)
 |    |    |-- mac_stats_rx_tsp_timeout: integer (nullable = true)
 |    |    |-- mac_stats_tx_bcn_cancel: integer (nullable = true)
 |    |    |-- mac_stats_rx_no_delimiter: integer (nullable = true)
 |    |    |-- mac_stats_rxf1ovfl: integer (nullable = true)
 |    |    |-- mac_stats_miss_bcn_dbg: integer (nullable = true)
 |    |    |-- mac_stats_pmqovfl: integer (nullable = true)
 |    |    |-- mac_stats_rx_hwprobe_req: integer (nullable = true)
 |    |    |-- mac_stats_rx_hwprobe_req_qoverflow: integer (nullable = true)
 |    |    |-- mac_stats_tx_hwprobe_resp: integer (nullable = true)
 |    |    |-- mac_stats_tx_hwprobe_resp_failed: integer (nullable = true)
 |    |    |-- mac_stats_tx_hwprobe_resp_drop_timeout: integer (nullable = true)
 |    |    |-- mac_stats_tx_rts_fail: integer (nullable = true)
 |    |    |-- mac_stats_tx_ucast: integer (nullable = true)
 |    |    |-- mac_stats_tx_in_rts_txop: integer (nullable = true)
 |    |    |-- mac_stats_rx_block_ack: integer (nullable = true)
 |    |    |-- mac_stats_tx_block_ack: integer (nullable = true)
 |    |    |-- mac_stats_phy_rx_glitch: integer (nullable = true)
 |    |    |-- mac_stats_rx_drop2nd: integer (nullable = true)
 |    |    |-- mac_stats_rx_too_late: integer (nullable = true)
 |    |    |-- mac_stats_phy_bad_plcp: integer (nullable = true)
 |    |    |-- tx_pkts_sent: integer (nullable = true)
 |    |    |-- tx_pkts_sent_mcast: integer (nullable = true)
 |-- wlans: array (nullable = true)
 |    |-- element: struct (containsNull = true)
 |    |    |-- id: string (nullable = true)
 |    |    |-- radio_index: integer (nullable = true)
 |    |    |-- bssid: string (nullable = true)
 |    |    |-- dev: string (nullable = true)
 |    |    |-- ssid: string (nullable = true)
 |    |    |-- num_clients: integer (nullable = true)
 |    |    |-- tx_mcast_pkts: integer (nullable = true)
 |    |    |-- tx_mcast_bytes: long (nullable = true)
 |    |    |-- radius_auth: array (nullable = true)
 |    |    |    |-- element: struct (containsNull = true)
 |    |    |    |    |-- ip: string (nullable = true)
 |    |    |    |    |-- port: integer (nullable = true)
 |    |    |    |    |-- requests: integer (nullable = true)
 |    |    |    |    |-- retransmissions: integer (nullable = true)
 |    |    |    |    |-- access_accepts: integer (nullable = true)
 |    |    |    |    |-- access_rejects: integer (nullable = true)
 |    |    |    |    |-- access_challenges: integer (nullable = true)
 |    |    |    |    |-- responses: integer (nullable = true)
 |    |    |    |    |-- malformed_responses: integer (nullable = true)
 |    |    |    |    |-- bad_authenticators: integer (nullable = true)
 |    |    |    |    |-- timeouts: integer (nullable = true)
 |    |    |    |    |-- unknown_types: integer (nullable = true)
 |    |    |    |    |-- packets_dropped: integer (nullable = true)
 |    |    |    |    |-- round_trip_time_ms: integer (nullable = true)
 |    |    |-- radius_acct: array (nullable = true)
 |    |    |    |-- element: struct (containsNull = true)
 |    |    |    |    |-- ip: string (nullable = true)
 |    |    |    |    |-- port: integer (nullable = true)
 |    |    |    |    |-- requests: integer (nullable = true)
 |    |    |    |    |-- retransmissions: integer (nullable = true)
 |    |    |    |    |-- responses: integer (nullable = true)
 |    |    |    |    |-- malformed_responses: integer (nullable = true)
 |    |    |    |    |-- timeouts: integer (nullable = true)
 |    |    |    |    |-- unknown_types: integer (nullable = true)
 |    |    |    |    |-- packets_dropped: integer (nullable = true)
 |    |    |    |    |-- round_trip_time_ms: integer (nullable = true)
 |    |    |-- radio: string (nullable = true)
 |-- pwr_src: string (nullable = true)
 |-- pwr_budget: integer (nullable = true)
 |-- pwr_needed: integer (nullable = true)
 |-- pwr_available: integer (nullable = true)
 |-- memory_total_kb: long (nullable = true)
 |-- memory_used_kb: long (nullable = true)
 |-- cpu_total_time: long (nullable = true)
 |-- cpu_user: long (nullable = true)
 |-- cpu_system: long (nullable = true)
 |-- fs_available_kb: long (nullable = true)
 |-- fs_total_kb: long (nullable = true)
 |-- load_total: integer (nullable = true)
 |-- slab_active_objs: integer (nullable = true)
 |-- slab_num_objs: integer (nullable = true)
 |-- slab_obj_size: integer (nullable = true)
 |-- cloud_last_rtt: float (nullable = true)
 |-- cloud_pmtu: integer (nullable = true)
 |-- temperature_attitude: float (nullable = true)
 |-- temperature_cpu: float (nullable = true)
 |-- temperature_ambient: float (nullable = true)
 |-- orientation_accel_x: float (nullable = true)
 |-- orientation_accel_y: float (nullable = true)
 |-- orientation_accel_z: float (nullable = true)
 |-- orientation_magne_x: float (nullable = true)
 |-- orientation_magne_y: float (nullable = true)
 |-- orientation_magne_z: float (nullable = true)
 |-- switchports: array (nullable = true)
 |    |-- element: struct (containsNull = true)
 |    |    |-- name: string (nullable = true)
 |    |    |-- link: boolean (nullable = true)
 |    |    |-- full_duplex: boolean (nullable = true)
 |    |    |-- mbps: integer (nullable = true)
 |    |    |-- rx_bytes: long (nullable = true)
 |    |    |-- rx_pkts: integer (nullable = true)
 |    |    |-- tx_bytes: long (nullable = true)
 |    |    |-- tx_pkts: integer (nullable = true)
 |    |    |-- rx_errors: integer (nullable = true)
 |    |    |-- rx_pause_pkts: integer (nullable = true)
 |    |    |-- rx_undersize_errors: integer (nullable = true)
 |    |    |-- rx_oversize_errors: integer (nullable = true)
 |    |    |-- rx_jabber_errors: integer (nullable = true)
 |    |    |-- rx_alignment_errors: integer (nullable = true)
 |    |    |-- rx_fcs_errors: integer (nullable = true)
 |    |    |-- rx_fragment_errors: integer (nullable = true)
 |    |    |-- rx_symbol_errors: integer (nullable = true)
 |    |    |-- rx_overrun_errors: integer (nullable = true)
 |    |    |-- rx_discards: integer (nullable = true)
 |    |    |-- rx_peakbps: long (nullable = true)
 |    |    |-- tx_peakbps: long (nullable = true)
 |    |    |-- switchport_counter_delta: boolean (nullable = true)
 |-- delta: boolean (nullable = true)
 |-- deltaErrorMsg: string (nullable = true)
 |-- ap_id: string (nullable = true)
 |-- delta_interval: integer (nullable = true)
 |-- ap_counter_delta: boolean (nullable = true)
 |-- input_cloud_partition: integer (nullable = true)
 |-- mesh: struct (nullable = true)
 |    |-- bssid: string (nullable = true)
 |    |-- mac: string (nullable = true)
 |    |-- dev: string (nullable = true)
 |    |-- last_connect_time: long (nullable = true)
 |-- ip: string (nullable = true)
 |-- hostname: string (nullable = true)
 |-- map_id: string (nullable = true)